## -2. 更新日志

+ 【2017/05/11】
    - 重新梳理前期实验结果，并整合到该份报告中
    - 前期实验报告参见同一目录下的其他以 `trial_` 开头的 `.ipynb` 文件

## -1. 备注

1. 搜索该符号以定位到报告中待完善的部分：。。。
2. 稍后可考虑将部分代码包装成 Python 脚本，以模块的形式导入，使整个 notebook 更简洁？或者不这样处理，从而使读者更方便阅读（而不用另外切换于多个页面之间）？
3. 。。。

## 0. 参考文献

1. (#miscellaneous) [20 Newsgroup Document Classification Report](http://cn-static.udacity.com/mlnd/Capstone_Poject_Sample01.pdf)
2. (#word2vec, #tensorflow) [Vector Representations of Words](https://www.tensorflow.org/tutorials/word2vec)
3. (#word2vec) [Distributed Representations of Words and Phrases and their Compositionality](http://papers.nips.cc/paper/5021-distributed-representations-of-words-and-phrases-and-their-compositionality.pdf)
4. (#word2vec, #gensim) [models.word2vec – Deep learning with word2vec](https://radimrehurek.com/gensim/models/word2vec.html)
5. (#CNN, #tensorflow) [Deep MNIST for Experts](https://www.tensorflow.org/get_started/mnist/pros)
6. (#text8) [text8](http://mattmahoney.net/dc/textdata)
7. 。。。

## 1. 实验模块规划

粗略规划如下，稍后精细整理：实现下述共计 15 种「表示 + 训练」组合

词汇模型 | 文档表示模型 | 分类器训练法
---------------|---------------------|---------------------
BOW + TF-IDF | Plain BOW | SVM
                     | Plain BOW | NB(Gaussian NB)
                     | Plain BOW | RF
                     | LSA | SVM
                     | LSA | NB(Gaussian NB)
                     | LSA | RF
                     | LDA | SVM
                     | LDA | NB(Gaussian NB)
                     | LDA | RF
Word2Vec      | arithmatic mean of Word2Vec | SVM
                     | arithmatic mean of Word2Vec | DNN
                     | arithmatic mean of Word2Vec | CNN
                     | word-clustering of Word2Vec | SVM
                     | word-clustering  of Word2Vec | DNN
                     | word-clustering  of Word2Vec | CNN

其中：
+ 名词解释
    - 词汇表示模型
        * BOW：Bag-of-Words，词袋模型
        * TF-IDF：Term Frequency - Inverse Document Frequency，文档-逆文档频率，其中
            - TF：词频，指该[词汇在文档中出现的原始频数](http://scikit-learn.org/stable/modules/feature_extraction.html#tfidf-term-weighting)
            - IDF：逆文档频率，指 $idf(d, t) = log( \frac{n}{df(d, t)} ) + 1$（该公式为 sklearn 中对 $idf(d, t)$的[实现](https://github.com/scikit-learn/scikit-learn/blob/14031f6/sklearn/feature_extraction/text.py#L1017)），其中 $df(d, t)$ 为[包含词汇 $t$ 的文档 $d$ 数目](http://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.TfidfTransformer.html#sklearn.feature_extraction.text.TfidfTransformer)
    - 文档表示模型
        * Plain BOW：直接用词袋向量表示每一篇文档，向量中每个维度的值为该词的 TF \* IDF 值
        * LSA：潜在语义分析
        * LDA：Latent Dirichlet Allocation，隐含狄利克雷分布
    - 分类器训练法
        * SVM：Support Vector Machine，支持向量机
        * NB(Gaussian NB)：NB(Naive Bayes) 朴素贝叶斯；Gaussian NB 高斯朴素贝叶斯（认为特征项服从于高斯分布，即正态分布）
        * RF：RandomForest，随机森林
        * DNN：Deep Neural Network，深度神经网络（普通的多层感知机构成的多层神经网络）
        * CNN：Convolution Neural Network，卷积神经网络
+ 训练工具
    - 表示模型
        * BOW+TF-IDF：使用 scikit-learn 建模
        * Word2Vec：使用 gensim 与 TensorFlow 建模
    - 分类器训练法
        * 传统算法：SVM, LSA, LDA 使用 scikit-learn 训练
        * 神经网络算法：DNN, CNN：使用 TensorFlow 训练

## 2. 实验流程规划

1. 模块导入
2. 数据预处理（通用预处理）
  + 对文本进行清洗，包括但不限于去除特殊符号、进行大小写转换等工作，最终使文本中只包含：由小写字母 a-z 组成的单词、单一空格
  + 不在 a-z 之间的字符将一律被转换为空格
3. 文本表示建模
  + BOW+TF-IDF 表示：
      1. 读入原始语料并保存
      2. 使用 scikit-learn，在原始语料的基础上，进行建立词袋（BOW）、计算 TF-IDF
      3. 通过使用 BOW+TF-IDF 向量表示文档中的每个词，从而表示每篇文档（包括所有语料：训练集和测试集）
      4. 每篇文档对应的标签独热（one-hot）向量化
  + Word2Vec 表示：
      1. 分别使用 gensim 和 TensorFlow 中的每一种，分别在 text8 的基础上、在待学习样本的基础上，建立词嵌入（word embedding）模型（Word2Vec）
          + 即：训练出 gensim+text8, gensim+待学习样本, TensorFlow+text8, TensorFlow+待学习样本 共计 4 种表示模型
          + 使用 Skip-Gram 方法进行建模
      2. 通过使用 Word2Vec 向量表示文档中的每个词，然后建立 2 种文档表示模型：
          + 求这些词向量的和，以求和向量表示每一篇文档；对于不在词汇表中的词，以某常量代替——具体而言，可指定为加入零向量，或在求和向量乘上某个常量系数
          + 对于上述求和向量进行求算术平均，使用算术平均向量表示每一篇文档；对于不在词汇表中的词，同上述处理方法
      3. 每篇文档对应的标签独热（one-hot）向量化
4. 分类器训练
  + 传统算法：SVM, LSA, LDA 使用 scikit-learn 训练
  + 神经网络算法：DNN, CNN：使用 TensorFlow 训练
5. 分类器评估
  + 对于传统算法：
    - 使用 sckit-learn 提供的 GridSearchCV 与 LearningCurve 方法寻找最优参数组合
    - 使用 scikit-learn 提供的 accuracy_score（查准率 P） 与 f1_score（F1 分数，同时考察了查准率 P 与查全率 R） 评估训练结果
  + 对于神经网络算法：
    - 暂定手工选择一组参数进行训练；待考察是否可使用 GridSearchCV 与 LearningCurve 进行参数组合寻找最优参数组合
    - 暂定使用手工编写的方法计算查准率 P、查全率 R、F1 分数；待考察是否可对数据格式进行一定程度上的转换或存储，以使用上述提及的 scikit-learn 提供的评估工具

## 3. 实验记录

In [1]:
# Step 0: import module

from __future__ import absolute_import
from __future__ import print_function
from __future__ import division

import os
import random
import datetime

import pandas as pd
import numpy as np

from sklearn.preprocessing import LabelBinarizer

from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score

import gensim
import tensorflow as tf

from IPython.display import display
%matplotlib inline

print("import modules successfully")

import modules successfully


In [2]:
%%time

# Step 1: preprocess the data
vecsize = 784

paths = {}
paths['dir.dataroot'] =  os.path.join(os.getcwd(), '..', 'data')
paths['dir.train'] = os.path.join(paths['dir.dataroot'], 'trialdata', 'train')
paths['dir.test'] = os.path.join(paths['dir.dataroot'], 'trialdata', 'test')
        
preprocessedFlag = os.path.join(paths['dir.dataroot'], 'preprocessed')
if not os.path.isfile(preprocessedFlag):
    for tpart in ['train', 'test']:
        dirpath = paths['dir.{}'.format(tpart)]
        for cls in os.listdir(dirpath):
            clspath = os.path.join(dirpath, cls)
            files = os.listdir(clspath)
            for f in files:
                fpath = os.path.join(clspath, f)
                os.system('mv {} {}.old'.format(fpath, fpath))
                os.system('perl {} {}.old > {}'.format(os.path.join(paths['dir.dataroot'], 'newfil.pl'), fpath, fpath))
                os.system('rm {}.old'.format(fpath))
    os.system('touch {}'.format(preprocessedFlag))
                
print("file preporcessing succefully")
            
stopwordlist = []
with open(os.path.join(paths['dir.dataroot'], 'stoplist-web.txt'), 'r') as readf:
    stopwordlist = readf.read()
    stopwordlist = stopwordlist.split('\n')
            
print("read stop word list successfully")
        
print("Step 1 Succeed")

file preporcessing succefully
read stop word list successfully
Step 1 Succeed
CPU times: user 4 ms, sys: 0 ns, total: 4 ms
Wall time: 781 µs


### 3.1 BOW+TF-IDF 表示法

In [3]:
%%time

# Step 2: read data and save it in data['nearRaw.train'] 和 data['nearRaw.test']
modelChoice = 'TFIDF'

data = {}
data['nearRaw.train'] = {'content':[], 'class':[]}
data['nearRaw.test'] = {'content':[], 'class':[]}

for tpart in ['train', 'test']:
    dirpath = paths['dir.{}'.format(tpart)]
    for (ind, cls) in enumerate(os.listdir(dirpath)):
        clspath = os.path.join(dirpath, cls)
        files = os.listdir(clspath)
        for f in files:
            fpath = os.path.join(clspath, f)
            with open(fpath, 'r') as readf:
                data['nearRaw.{}'.format(tpart)]['content'].append(readf.read())
                data['nearRaw.{}'.format(tpart)]['class'].append(cls)
    tmp = data['nearRaw.{}'.format(tpart)]
    ind = (random.sample(range(len(tmp['class'])), 1))[0]
    print("sample(transformed) from {}[{}]:\n[content]\n {}\n[class]\n{}".format(
            tpart, ind, tmp['content'][ind], tmp['class'][ind]
        )
    )
    print() 
    
print("Step 2 Succeed")

sample(transformed) from train[2540]:
[content]
  from dwestner cardhu mcs dundee ac uk dominik westner subject need a viewer for gl files organization maths c s dept dundee university scotland uk lines one zero nntp posting host cardhu mcs dundee ac uk x newsreader tin version one one pl nine hi the subject says it all is there a pd viewer for gl files for x thanks dominik
[class]
comp.graphics

sample(transformed) from test[1389]:
[content]
  from car three seven seven cbnewsj cb att com charles a rogers subject re shaft drives and wheelies organization at t summary another one bites the dust lines one nine in article wayne orwig atlantaga ncr com wayne orwig writes is it possible to do a wheelie on a motorcycle with shaft drive no mike it is imposible due to the shaft effect the centripital effects of the rotating shaft counteract any tendency for the front wheel to lift off the ground well my last two motorcycles have been shaft driven and they will wheelie the rear gear does climb

#### 3.1.1 普通 VSM 表示模型

<center>参数列表</center>

参数 |  取值
--------|-----------
max_df | 0.9
min_df | 0.01
max_features | 784
analyzer | 'word'
stop_words | stopwordlist（来自文件）

In [88]:
%%time

# Step 3: CountVectorizer.fit + TfidfVectorizer.transform + save in Pandas.DataFrame
# A. 使用 sklearn.feature_extraction.text.TfidfVectorizer.fit 拟合训练数据，建立 BOW+TF-IDF 
# B. 使用 sklearn.feature_extraction.text.TfidfVectorizer.transform 将data['nearRaw.train']中的 stringContent 和 data['nearRaw.test']中的 stringContent 进行处理，
# 将 BOW+TF-IDF 表示结果输出到 data['matrix.train'] 与 data['matrix.test'] 中，供后续学习和训练使用
# 
# C. 将 data['matrix.train'] 与 data['matrix.test'] 转换成 Pandas.DataFrame 格式，保存到 df['train'] 和 df['test'] 中（df 为字典格式：String -> DataFrame）

# Substep A: vectorization + TF-IDF calculation

vecsize=784
countVector = CountVectorizer(max_df=0.9, min_df=0.01, analyzer='word', stop_words=stopwordlist)
countVector.fit(data['nearRaw.train']['content'])
tfidf = TfidfTransformer()

print("Substep A finished.")
print("--------------------------------------------------")

## Substep B: Transformation

for tpart in ['train', 'test']:
    data['matrix.{}'.format(tpart)] = countVector.transform(data['nearRaw.{}'.format(tpart)]['content']) 
    data['matrix.{}'.format(tpart)] = tfidf.fit_transform(data['matrix.{}'.format(tpart)])
    ind = (random.sample(range(data['matrix.{}'.format(tpart)].shape[0]), 1))[0]
    print("sample for matrix.{}".format(tpart))
    print("from ind: {}".format(ind))
    print(data['matrix.{}'.format(tpart)][ind])
    print() 
    
print("Substep B finished.")
print("--------------------------------------------------")

# Substep C: integrate data into DataFrame format

csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')
if not os.path.isdir(csvpath_root):
    os.mkdir(csvpath_root)

df = {}
for tpart in ['train', 'test']:
    datadict = {}
    datadict['class'] = data['nearRaw.{}'.format(tpart)]['class']
    for col in range(data['matrix.{}'.format(tpart)].shape[1]):
        datadict[col]= [i[0] for i in data['matrix.{}'.format(tpart)].getcol(col).toarray()]
#         datadict[str(col)]= [i[0] for i in data['matrix.{}'.format(tpart)].getcol(col).toarray()]

    df[tpart] = pd.DataFrame(data=datadict)
    print("See df[{}]".format(tpart))
    display(df[tpart])
    print("\n\n\n")
    # write data in DataFrame into CSV
    csvpath = os.path.join(csvpath_root, "{}-{}.csv".format(tpart, modelChoice))
    df[tpart].to_csv(csvpath, columns=df[tpart].columns)

print("Substep C finished.")
print("--------------------------------------------------")

print("Step 3 Succeed.")

# 繁琐点：研究如何把 CSR 矩阵中的数据规整好放到 DataFrame 中，并与 Class 一一对应

Substep A finished.
--------------------------------------------------
sample for matrix.train
from ind: 513
  (0, 1909)	0.264534266538
  (0, 1904)	0.0642548323148
  (0, 1893)	0.0296472419171
  (0, 1884)	0.0514743455666
  (0, 1854)	0.0687211360071
  (0, 1842)	0.0887145186604
  (0, 1841)	0.0796432450524
  (0, 1832)	0.0981896678566
  (0, 1830)	0.092500221377
  (0, 1755)	0.094884071181
  (0, 1711)	0.091330505832
  (0, 1706)	0.0789737439999
  (0, 1695)	0.112612802394
  (0, 1632)	0.0839580852865
  (0, 1597)	0.081871765367
  (0, 1565)	0.0873399124149
  (0, 1544)	0.092500221377
  (0, 1542)	0.0311605033666
  (0, 1505)	0.0639455871487
  (0, 1501)	0.0865615312436
  (0, 1491)	0.0752954176213
  (0, 1487)	0.0689163872414
  (0, 1484)	0.0673188037535
  (0, 1392)	0.0500723853919
  (0, 1355)	0.0807240573146
  :	:
  (0, 637)	0.204895948761
  (0, 590)	0.0968150616111
  (0, 555)	0.0613628532836
  (0, 538)	0.0955579514014
  (0, 503)	0.0905109566388
  (0, 493)	0.0587477480792
  (0, 470)	0.0627173743122
  (0

0         1         2         3         4         5         6  \
0     0.00000  0.112101  0.000000  0.000000  0.000000  0.000000  0.000000   
1     0.00000  0.000000  0.000000  0.000000  0.000000  0.078664  0.000000   
2     0.00000  0.000000  0.000000  0.000000  0.063955  0.000000  0.000000   
3     0.00000  0.065352  0.000000  0.000000  0.000000  0.000000  0.000000   
4     0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
5     0.00000  0.051058  0.000000  0.000000  0.000000  0.000000  0.000000   
6     0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
7     0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
8     0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
9     0.00000  0.000000  0.000000  0.000000  0.000000  0.197190  0.129913   
10    0.00000  0.000000  0.000000  0.000000  0.044900  0.000000  0.000000   
11    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
12    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
13    0.00000  0.000000  0.000000  0.000000  0.103947  0.000000  0.000000   
14    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
15    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
16    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
17    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
18    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
19    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
20    0.00000  0.000000  0.480723  0.174808  0.000000  0.000000  0.000000   
21    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
22    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
23    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
24    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
25    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
26    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
27    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
28    0.05879  0.000000  0.244248  0.000000  0.000000  0.000000  0.000000   
29    0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
...       ...       ...       ...       ...       ...       ...       ...   
2825  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2826  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2827  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2828  0.00000  0.000000  0.000000  0.000000  0.057348  0.000000  0.000000   
2829  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2830  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2831  0.00000  0.000000  0.000000  0.000000  0.388034  0.000000  0.000000   
2832  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2833  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2834  0.00000  0.000000  0.000000  0.000000  0.397802  0.000000  0.000000   
2835  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2836  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2837  0.00000  0.000000  0.000000  0.000000  0.094382  0.000000  0.000000   
2838  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2839  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2840  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2841  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2842  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2843  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2844  0.00000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2845  0.





See df[test]


0         1    2         3         4         5         6  \
0     0.000000  0.054858  0.0  0.000000  0.000000  0.000000  0.000000   
1     0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
2     0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
3     0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
4     0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
5     0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
6     0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
7     0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.077960   
8     0.000000  0.000000  0.0  0.000000  0.000000  0.063088  0.000000   
9     0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
10    0.000000  0.000000  0.0  0.000000  0.000000  0.050092  0.000000   
11    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
12    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.127287   
13    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
14    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
15    0.000000  0.062163  0.0  0.000000  0.000000  0.000000  0.000000   
16    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
17    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
18    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
19    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
20    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
21    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
22    0.000000  0.086798  0.0  0.000000  0.000000  0.000000  0.000000   
23    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
24    0.000000  0.120794  0.0  0.000000  0.325497  0.000000  0.000000   
25    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
26    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
27    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
28    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
29    0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
...        ...       ...  ...       ...       ...       ...       ...   
1870  0.000000  0.108429  0.0  0.000000  0.000000  0.000000  0.000000   
1871  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1872  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1873  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1874  0.000000  0.000000  0.0  0.000000  0.061653  0.000000  0.000000   
1875  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1876  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1877  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1878  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1879  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1880  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1881  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1882  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1883  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1884  0.000000  0.025688  0.0  0.000000  0.000000  0.000000  0.000000   
1885  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1886  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1887  0.000000  0.075977  0.0  0.000000  0.272974  0.000000  0.000000   
1888  0.000000  0.000000  0.0  0.000000  0.058837  0.000000  0.000000   
1889  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1890  0.064947  0.000000  0.0  0.000000  0.000000  0.000000  0.000000   
1891  0.000000  0.123691  0.0  0.000000  0.000000  0.000000  0.000000   
1892  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  0.000000  





Substep C finished.
--------------------------------------------------
Step 3 Succeed.
CPU times: user 11.1 s, sys: 256 ms, total: 11.4 s
Wall time: 11.2 s


In [89]:
%%time

# if wanna read data from CSV file

df = {}

for tpart in ['train', 'test']:
    csvpath = os.path.join(paths['dir.dataroot'], 'data_CSV', '{}-{}.csv'.format(tpart, modelChoice))
    if os.path.exists(csvpath):
        df[tpart] = pd.DataFrame.from_csv(csvpath)
        df[tpart] = df[tpart].sample(frac=1)
        df[tpart].reset_index(drop=True, inplace=True)
        print("read {} successfully".format(tpart))
        display(df[tpart])


read train successfully


0         1         2    3         4         5         6  \
0     0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
1     0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2     0.000000  0.000000  0.000000  0.0  0.000000  0.099791  0.000000   
3     0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
4     0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
5     0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
6     0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
7     0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.174175   
8     0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
9     0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
10    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
11    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
12    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
13    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
14    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
15    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
16    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
17    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
18    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
19    0.000000  0.000000  0.133796  0.0  0.000000  0.000000  0.000000   
20    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
21    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
22    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
23    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
24    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
25    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
26    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
27    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
28    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
29    0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
...        ...       ...       ...  ...       ...       ...       ...   
2825  0.000000  0.000000  0.000000  0.0  0.157998  0.000000  0.000000   
2826  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2827  0.083659  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2828  0.000000  0.089372  0.000000  0.0  0.000000  0.000000  0.000000   
2829  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2830  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2831  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2832  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2833  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2834  0.000000  0.000000  0.000000  0.0  0.071846  0.000000  0.000000   
2835  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2836  0.000000  0.077561  0.000000  0.0  0.000000  0.000000  0.000000   
2837  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2838  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2839  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2840  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2841  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2842  0.126756  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2843  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2844  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2845  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2846  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000   
2847  0.000000  0.000000  0.000000  0.0  0.000000  0.000000  0.000000  

read test successfully


0         1    2         3         4    5         6         7  \
0     0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1     0.000000  0.000000  0.0  0.059273  0.000000  0.0  0.000000  0.000000   
2     0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
3     0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
4     0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
5     0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
6     0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
7     0.513551  0.000000  0.0  0.000000  0.176652  0.0  0.000000  0.000000   
8     0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
9     0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
10    0.000000  0.000000  0.0  0.000000  0.091367  0.0  0.000000  0.000000   
11    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
12    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
13    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
14    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
15    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
16    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
17    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
18    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
19    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
20    0.000000  0.000000  0.0  0.000000  0.197269  0.0  0.000000  0.000000   
21    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
22    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
23    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
24    0.000000  0.107061  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
25    0.000000  0.000000  0.0  0.000000  0.060461  0.0  0.000000  0.000000   
26    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
27    0.000000  0.000000  0.0  0.131178  0.000000  0.0  0.000000  0.000000   
28    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
29    0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.068989   
...        ...       ...  ...       ...       ...  ...       ...       ...   
1870  0.000000  0.053940  0.0  0.069335  0.000000  0.0  0.000000  0.000000   
1871  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1872  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1873  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1874  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1875  0.000000  0.000000  0.0  0.000000  0.085797  0.0  0.000000  0.000000   
1876  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1877  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1878  0.160852  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1879  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1880  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1881  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1882  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1883  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1884  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1885  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.096792   
1886  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1887  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1888  0.000000  0.000000  0.0  0.000000  0.000000  0.0  0.000000  0.000000   
1889  0.000000  0.000000  0.0  0.00

CPU times: user 1 s, sys: 44 ms, total: 1.05 s
Wall time: 1.04 s


In [90]:
# %%time

# # Step 4: One-hot representation for labels

# csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')

# lb = LabelBinarizer()
# lb.fit(df['train']['class'])

# df_new = {}
# for tpart in ['train', 'test']:
#     labels = lb.transform(df[tpart]['class'])
#     labelsDf = pd.DataFrame(labels, columns=["class-{}".format(i) for i in range(len(lb.classes_))])
#     df_new[tpart] = {}
#     df_new[tpart]['y'] = labelsDf
#     df_new[tpart]['x'] = df[tpart].drop('class', axis=1)
#     df_new[tpart]['all'] = df_new[tpart]['x'].join(df_new[tpart]['y'])
#     #save in CSV
#     for subpart in ['x', 'y', 'all']:
#         csvpath = os.path.join(csvpath_root, "{}-cleanLabels-{}-{}.csv".format(tpart, subpart, modelChoice))
#         df_new[tpart][subpart].to_csv(csvpath)
    
# print("label cleaning succussfully")

###### SVM classifier(BOW+TFIDF)

In [91]:
%%time

from sklearn.svm import LinearSVC

# if 'TFIDF' == modelChoice:

#train
X_train = df['train'].drop('class', axis=1)
y_train = df['train']['class']
#test
X_test = df['test'].drop('class', axis=1)
y_test_true = df['test']['class']

# else:
#     #train
#     X_train = df_new['train']['x']
#     y_train = df_new['train']['y']
#     #test
#     X_test = df_new['test']['x']
#     y_test_true = df_new['test']['y']

clf = LinearSVC()
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 156 ms, sys: 8 ms, total: 164 ms
Wall time: 160 ms


In [92]:
%%time

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

# print f1_score(y_test_true, tensorPredCls, average='micro')


# 0.891052631579
# 0.888626036046
# 0.891052631579

0.89
0.887417283793
0.89
CPU times: user 28 ms, sys: 0 ns, total: 28 ms
Wall time: 27.1 ms


###### GaussianNB classifier(BOW+TFIDF)

In [93]:
%%time

from sklearn.naive_bayes import GaussianNB

# if 'TFIDF' == modelChoice:

#train
X_train = df['train'].drop('class', axis=1)
y_train = df['train']['class']
#test
X_test = df['test'].drop('class', axis=1)
y_test_true = df['test']['class']

# else:
#     #train
#     X_train = df_new['train']['x']
#     y_train = df_new['train']['y']
#     #test
#     X_test = df_new['test']['x']
#     y_test_true = df_new['test']['y']

clf = GaussianNB()
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 128 ms, sys: 20 ms, total: 148 ms
Wall time: 147 ms


In [94]:
%%time

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

# print f1_score(y_test_true, tensorPredCls, average='micro')

0.792631578947
0.792735075167
0.792631578947
CPU times: user 132 ms, sys: 4 ms, total: 136 ms
Wall time: 134 ms


###### RF classifier(BOW+TFIDF)

In [95]:
%%time

from sklearn.ensemble import RandomForestClassifier

# if 'TFIDF' == modelChoice:

#train
X_train = df['train'].drop('class', axis=1)
y_train = df['train']['class']
#test
X_test = df['test'].drop('class', axis=1)
y_test_true = df['test']['class']

# else:
#     #train
#     X_train = df_new['train']['x']
#     y_train = df_new['train']['y']
#     #test
#     X_test = df_new['test']['x']
#     y_test_true = df_new['test']['y']

clf = RandomForestClassifier(random_state=19, n_estimators=15)
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 284 ms, sys: 12 ms, total: 296 ms
Wall time: 332 ms


In [96]:
%%time

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

# print f1_score(y_test_true, tensorPredCls, average='micro')

0.821052631579
0.815607194901
0.821052631579
CPU times: user 32 ms, sys: 4 ms, total: 36 ms
Wall time: 34.3 ms


###### Output stopwords

In [13]:
%%time

temps = ""
with open(os.path.join(paths['dir.dataroot'], 'stoplist-baseTFIDF.txt'), 'w') as stoplistfile:
    for w in vectorizer.stop_words_:
        temps += "{} ".format(w)
    stoplistfile.write(temps)
    
print("Output stoplist successfully.")

Output stoplist successfully.
CPU times: user 40 ms, sys: 0 ns, total: 40 ms
Wall time: 46.3 ms


#### 3.1.2 基于 BOW+TFIDF 的 LSA 表示

<center>参数列表</center>

参数 |  取值
--------|-----------
k(n_components) | 200
n_iter | 10
random_state | 19

In [97]:
%%time

# Step 4: LSA based on BOW+TFIDF
# 注意：sklearn.decomposition.TruncatedSVD 的 fit() 与 transform() 方法接受的参数虽然说要求是稀疏矩阵（sparse matrix），但只要求输入

from sklearn.decomposition import TruncatedSVD

modelChoice = 'LSA'

csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')

svd = TruncatedSVD(n_components=200, n_iter=10, random_state=19)
svd.fit(df['train'].drop('class', axis=1))

df_new = {}
for tpart in ['train', 'test']:
    df_new[tpart] = {}
    datadict = {}
    X_LSA = svd.transform(df[tpart].drop('class', axis=1))
    for col in range(X_LSA.shape[1]):
        datadict[col] = X_LSA[:, col]
    df_new[tpart]['y'] = df[tpart]['class']
    df_new[tpart]['x'] = pd.DataFrame(data=datadict)
    df_new[tpart]['all'] = df_new[tpart]['x'].join(df_new[tpart]['y'])
    print('Finish {} for data: {}'.format(modelChoice, tpart))
    display(df_new[tpart]['all'])
    print("\n\n\n")
    #save in CSV
    for subpart in ['x', 'y', 'all']:
        csvpath = os.path.join(csvpath_root, "{}-cleanLabels-{}-{}.csv".format(tpart, subpart, modelChoice))
        df_new[tpart][subpart].to_csv(csvpath)

Finish LSA for data: train


0         1         2         3         4         5         6  \
0     0.188972  0.071130  0.094857  0.091979 -0.114947  0.072275 -0.021450   
1     0.257543  0.025823  0.112925  0.012267 -0.100985  0.021599  0.177765   
2     0.355085  0.145139 -0.238573 -0.044952  0.064532  0.056341  0.007718   
3     0.374163  0.179965 -0.119052 -0.106891  0.035110  0.072592  0.043526   
4     0.137856  0.056576  0.116101  0.098419 -0.081422  0.148872 -0.117619   
5     0.136039  0.172791  0.221007  0.243989  0.241634  0.106942 -0.257634   
6     0.339705 -0.096705 -0.003002  0.051510 -0.012402  0.002908  0.126625   
7     0.241882  0.180199  0.029688  0.096595  0.064813 -0.032263 -0.023685   
8     0.233238  0.041447  0.240793 -0.156869 -0.014313 -0.110089  0.128215   
9     0.214532 -0.100363  0.054047 -0.143573  0.024492  0.078260 -0.001258   
10    0.233794  0.037374  0.075458  0.054795 -0.073689 -0.011226  0.030732   
11    0.332807 -0.043761  0.051021 -0.024289 -0.099183  0.084902  0.022405   
12    0.359374 -0.045970  0.008090  0.152487 -0.200404 -0.049538  0.080530   
13    0.465553 -0.155031  0.029735 -0.123658  0.103721 -0.169668 -0.035862   
14    0.496029 -0.045046  0.007193  0.037430 -0.091805  0.194339 -0.023920   
15    0.222995  0.216615 -0.117495 -0.062202  0.035259 -0.010800  0.043596   
16    0.222336  0.039805  0.152129 -0.070853 -0.037431 -0.099859  0.089399   
17    0.456840 -0.010924 -0.015046  0.099974 -0.105758 -0.114252  0.066463   
18    0.270520 -0.011178  0.050964  0.086851 -0.119224 -0.156360  0.109482   
19    0.265663  0.089310  0.189706  0.138616  0.327488  0.045193  0.212969   
20    0.360313 -0.123802  0.004532 -0.028924  0.062405 -0.238527  0.019525   
21    0.252851  0.029718 -0.012533  0.061024 -0.080235 -0.069030 -0.004535   
22    0.272212  0.035550  0.166786  0.030975  0.014996  0.071654  0.236728   
23    0.156926  0.198357  0.016144 -0.007163 -0.009339 -0.036366  0.023864   
24    0.130926  0.006255  0.149195 -0.142182 -0.019068 -0.135251 -0.057083   
25    0.227809  0.111826  0.090967  0.056796 -0.009773  0.139127 -0.085407   
26    0.105366  0.076660  0.046000  0.084384 -0.070872  0.061653 -0.115409   
27    0.438407 -0.131150 -0.050765 -0.098399  0.089868  0.000629 -0.001159   
28    0.183457  0.108369 -0.017694 -0.091459  0.016140  0.018764  0.072672   
29    0.265414 -0.041996  0.117750 -0.161574 -0.001173  0.018719 -0.157206   
...        ...       ...       ...       ...       ...       ...       ...   
2825  0.173916  0.044167 -0.002073 -0.031134 -0.043917 -0.045796 -0.019503   
2826  0.572289 -0.191072 -0.035076  0.038788 -0.005190  0.142450 -0.044579   
2827  0.411783 -0.077326 -0.041013  0.127013 -0.074295  0.047573  0.019514   
2828  0.277007 -0.022581 -0.029196  0.116264 -0.037649 -0.093428  0.033627   
2829  0.440479 -0.146216 -0.085730 -0.020307  0.137460 -0.228661 -0.091133   
2830  0.409776 -0.072652  0.079026 -0.180369  0.055671  0.066798 -0.006294   
2831  0.140451  0.016534  0.148650 -0.125024 -0.034170 -0.060393 -0.050614   
2832  0.217459 -0.006911  0.174517 -0.054854  0.009098 -0.062268  0.159834   
2833  0.134796  0.022027  0.110898 -0.133270 -0.034007 -0.089017 -0.028929   
2834  0.270184  0.101919  0.047604  0.078642 -0.129636 -0.071451 -0.051155   
2835  0.091419  0.058906  0.066682 -0.043765 -0.023384 -0.071098  0.042521   
2836  0.158410  0.325087 -0.159482 -0.040665  0.061451 -0.000917 -0.016095   
2837  0.182936  0.075920  0.046185  0.127462 -0.119644  0.018804 -0.070705   
2838  0.357994 -0.065683  0.016650 -0.012246  0.006221  0.007875  0.081809   
2839  0.504882 -0.152336  0.023314 -0.020104 -0.007160  0.102301 -0.059591   
2840  0.181110  0.254215 -0.054838  0.003969 -0.042370 -0.059607  0.025743   
2841  0.226373  0.241312 -0.061342 -0.049659  0.070011 -0.007772 -0.060062   
2842  0.182136  0.113322  0.016089  0.140183  0.053228  0.105495 -0.109923   
2843  0.453674 -0.057140 -0.111765  0.068774  0.025909  0.047198 -0.029842   
2844  0.142310  0.045561  0.185312 





Finish LSA for data: test


0         1         2         3         4         5         6  \
0     0.355580 -0.052788 -0.007453 -0.031688  0.035609  0.053119  0.060243   
1     0.202752 -0.016259 -0.023209  0.138482 -0.099814 -0.082671 -0.014771   
2     0.246044  0.116713  0.024573  0.082475 -0.055013  0.012335 -0.026643   
3     0.211923  0.068596 -0.007437 -0.068433 -0.038257  0.078021  0.003817   
4     0.220424 -0.040344 -0.013521  0.036365 -0.024230  0.050122 -0.012944   
5     0.299360 -0.003347 -0.000546 -0.135834 -0.019654  0.173514  0.079810   
6     0.398143 -0.119192  0.000713 -0.053978  0.076851  0.178920 -0.022524   
7     0.133049  0.068591  0.080711 -0.037843 -0.033350 -0.009559 -0.052315   
8     0.154407  0.059741  0.025908  0.089533 -0.087494 -0.017161 -0.019233   
9     0.265694  0.044120  0.105120  0.012647 -0.095210  0.092118 -0.085938   
10    0.212293  0.017235 -0.022831  0.007965  0.036744 -0.122229 -0.050189   
11    0.152243 -0.018668  0.084467  0.037260 -0.042598 -0.057101  0.093790   
12    0.158566  0.073314  0.048934  0.110255 -0.111981 -0.018258 -0.071820   
13    0.332661 -0.030584 -0.053901  0.109352 -0.088101 -0.022592  0.017930   
14    0.519441 -0.104701 -0.156405  0.190549 -0.022855 -0.202109 -0.001947   
15    0.415167 -0.134340 -0.054862  0.023381 -0.023933  0.079497  0.050279   
16    0.216797  0.072370  0.051612  0.051649 -0.055913  0.007230  0.079857   
17    0.117415  0.152202 -0.005393  0.048584  0.045749 -0.048704  0.034264   
18    0.325258 -0.012946  0.040107  0.088516 -0.074161  0.137350 -0.115819   
19    0.332305  0.103490  0.090077  0.016832 -0.052927 -0.075576  0.059441   
20    0.211918 -0.007567  0.132535 -0.168269 -0.051633 -0.005454 -0.135213   
21    0.400240 -0.059013  0.032743 -0.001148 -0.030840  0.030213  0.004325   
22    0.318082 -0.005831  0.058289  0.136135 -0.096985 -0.056839 -0.036714   
23    0.568390 -0.203433 -0.073552  0.048487  0.007535  0.090575  0.005834   
24    0.244853 -0.015744  0.022049  0.103278 -0.057427 -0.081844  0.090389   
25    0.183506  0.025553  0.002748  0.157964 -0.185733 -0.064101  0.036870   
26    0.219407  0.255853 -0.110904 -0.006886 -0.012975 -0.007295 -0.016405   
27    0.289189 -0.024404  0.082345  0.021548  0.000566 -0.013715  0.202086   
28    0.104298  0.129574  0.193822  0.192315  0.218742  0.118477 -0.200454   
29    0.211115  0.245704 -0.171267 -0.082391  0.012271  0.035108 -0.013180   
...        ...       ...       ...       ...       ...       ...       ...   
1870  0.487843 -0.181020 -0.119942  0.164939 -0.009124 -0.100456 -0.027473   
1871  0.189116 -0.021033  0.072672  0.096870 -0.127724  0.057096 -0.020732   
1872  0.210134  0.279001 -0.086768 -0.060752 -0.021155  0.002540  0.027798   
1873  0.397425 -0.052743 -0.061554  0.010330  0.035788  0.012773  0.001797   
1874  0.275669 -0.049216  0.068526  0.037381 -0.052885  0.036786  0.020536   
1875  0.346905 -0.046573 -0.061271  0.120785 -0.016209 -0.042548 -0.043302   
1876  0.284352 -0.009920  0.083758 -0.048258 -0.019688  0.032281  0.096098   
1877  0.227921  0.073319  0.122889  0.034119 -0.107610  0.014914  0.096084   
1878  0.342970 -0.055144  0.099804 -0.123950  0.046438 -0.162988 -0.198994   
1879  0.210102  0.056093  0.033127  0.112279 -0.144403 -0.109441  0.106649   
1880  0.352289 -0.098693 -0.008289 -0.016395 -0.026643  0.059483  0.004997   
1881  0.246426 -0.013959 -0.012141  0.096147 -0.032397 -0.139392  0.027917   
1882  0.163794  0.038492  0.007357 -0.000474  0.049792 -0.051769 -0.022896   
1883  0.271786  0.013563  0.080313  0.039312 -0.082162  0.024791  0.130694   
1884  0.186776  0.169753 -0.041028  0.000482 -0.032427  0.050492 -0.043048   
1885  0.119017  0.162981 -0.029653  0.019971 -0.014005 -0.013805 -0.047294   
1886  0.323992 -0.010112  0.054886 -0.017439 -0.026222 -0.032528  0.122115   
1887  0.266064  0.079069 -0.000102 -0.063681  0.026620  0.024241 -0.040263   
1888  0.260669 -0.034591  0.192308 -0.233332  0.012252 -0.107953 -0.135824   
1889  0.447568 -0.104939 -0.049060 





CPU times: user 20.8 s, sys: 15.4 s, total: 36.2 s
Wall time: 6.03 s


###### SVM classifier(BOW+TFIDF+LSA)

In [98]:
%%time

# Step 5: Training

# if 'TFIDF' == modelChoice:
#     #train
#     X_train = df['train'].drop('class', axis=1)
#     y_train = df['train']['class']
#     #test
#     X_test = df['test'].drop('class', axis=1)
#     y_test_true = df['test']['class']
# else:

#train
X_train = df_new['train']['x']
y_train = df_new['train']['y']
#test
X_test = df_new['test']['x']
y_test_true = df_new['test']['y']

clf = LinearSVC()
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 152 ms, sys: 4 ms, total: 156 ms
Wall time: 156 ms


In [99]:
%%time

# Step 6: Evaluate

y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

0.893684210526
0.890675497575
0.893684210526
CPU times: user 16 ms, sys: 0 ns, total: 16 ms
Wall time: 15.7 ms


###### GaussianNB classifier(BOW+TFIDF+LSA)

In [100]:
%%time

from sklearn.naive_bayes import GaussianNB

# if 'TFIDF' == modelChoice:
#     #train
#     X_train = df['train'].drop('class', axis=1)
#     y_train = df['train']['class']
#     #test
#     X_test = df['test'].drop('class', axis=1)
#     y_test_true = df['test']['class']
# else:

#train
X_train = df_new['train']['x']
y_train = df_new['train']['y']
#test
X_test = df_new['test']['x']
y_test_true = df_new['test']['y']

clf = GaussianNB()
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 12 ms, sys: 0 ns, total: 12 ms
Wall time: 12.7 ms


In [101]:
%%time

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

# print f1_score(y_test_true, tensorPredCls, average='micro')

0.76
0.757885474234
0.76
CPU times: user 24 ms, sys: 0 ns, total: 24 ms
Wall time: 23.8 ms


###### RF classifier(BOW+TFIDF+LSA)

In [102]:
%%time

from sklearn.ensemble import RandomForestClassifier

# if 'TFIDF' == modelChoice:
#     #train
#     X_train = df['train'].drop('class', axis=1)
#     y_train = df['train']['class']
#     #test
#     X_test = df['test'].drop('class', axis=1)
#     y_test_true = df['test']['class']
# else:

#train
X_train = df_new['train']['x']
y_train = df_new['train']['y']
#test
X_test = df_new['test']['x']
y_test_true = df_new['test']['y']

clf = RandomForestClassifier(random_state=19, n_estimators=15)
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 420 ms, sys: 0 ns, total: 420 ms
Wall time: 419 ms


In [103]:
%%time

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

# print f1_score(y_test_true, tensorPredCls, average='micro')

0.772105263158
0.768184785712
0.772105263158
CPU times: user 24 ms, sys: 4 ms, total: 28 ms
Wall time: 27.3 ms


#### 3.1.3 基于 BOW+TFIDF 的 LDA 表示

<center>参数列表</center>

参数 |  取值
--------|-----------
n_topic | 50
max_iter | 10
random_state | 19

> 注意：实验表明，主题数的选择会影响训练效果。目前测试过 5, 35, 50, 75, 100, 200，似乎以 50 效果最好。因此最后保留 50 的训练结果。

In [104]:
%%time

# Step 4: LDA based on BOW+TFIDF
# 注意：sklearn.decomposition.TruncatedSVD 的 fit() 与 transform() 方法接受的参数虽然说要求是稀疏矩阵（sparse matrix），但只要求输入

from sklearn.decomposition import LatentDirichletAllocation

modelChoice = 'LDA'

csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')

lda = LatentDirichletAllocation(n_topics=50, max_iter=10, random_state=19, learning_method='batch')
lda.fit(df['train'].drop('class', axis=1))

df_new = {}
for tpart in ['train', 'test']:
    df_new[tpart] = {}
    datadict = {}
    X_LDA = lda.transform(df[tpart].drop('class', axis=1))
    for col in range(X_LDA.shape[1]):
        datadict[col] = X_LDA[:, col]
    df_new[tpart]['y'] = df[tpart]['class']
    df_new[tpart]['x'] = pd.DataFrame(data=datadict)
    df_new[tpart]['all'] = df_new[tpart]['x'].join(df_new[tpart]['y'])
    print('Finish {} for data: {}'.format(modelChoice, tpart))
    display(df_new[tpart]['all'])
    print("\n\n\n")
    #save in CSV
    for subpart in ['x', 'y', 'all']:
        csvpath = os.path.join(csvpath_root, "{}-cleanLabels-{}-{}.csv".format(tpart, subpart, modelChoice))
        df_new[tpart][subpart].to_csv(csvpath)

Finish LDA for data: train


0         1         2         3         4         5         6  \
0     0.002584  0.002584  0.002584  0.002584  0.002584  0.002584  0.002584   
1     0.002761  0.002761  0.002761  0.002761  0.020472  0.002761  0.002761   
2     0.002261  0.002261  0.002261  0.002261  0.002261  0.002261  0.002261   
3     0.001872  0.001872  0.001872  0.001872  0.001872  0.001872  0.001872   
4     0.003533  0.003533  0.003533  0.426517  0.051819  0.003533  0.003533   
5     0.002495  0.002495  0.002495  0.002495  0.002495  0.002495  0.002495   
6     0.052395  0.003124  0.003124  0.003124  0.003124  0.003124  0.003124   
7     0.002012  0.002012  0.002012  0.002012  0.002012  0.002012  0.002012   
8     0.003387  0.003387  0.003387  0.003387  0.003387  0.003387  0.003387   
9     0.005320  0.005320  0.005320  0.005320  0.005320  0.005320  0.005320   
10    0.002969  0.002969  0.002969  0.002969  0.030772  0.002969  0.002969   
11    0.003178  0.003178  0.003178  0.003178  0.003178  0.003178  0.003178   
12    0.002631  0.002631  0.002631  0.002631  0.002631  0.002631  0.002631   
13    0.002856  0.002856  0.002856  0.002856  0.002856  0.002856  0.002856   
14    0.002256  0.002256  0.002256  0.002256  0.002256  0.002256  0.002256   
15    0.003002  0.003002  0.003002  0.003002  0.003002  0.003002  0.003002   
16    0.003005  0.003005  0.003005  0.003005  0.003005  0.003005  0.003005   
17    0.001837  0.001837  0.001837  0.001837  0.001837  0.001837  0.001837   
18    0.002736  0.002736  0.002736  0.002736  0.002736  0.002736  0.002736   
19    0.002846  0.002846  0.002846  0.002846  0.002846  0.002846  0.002846   
20    0.003512  0.003512  0.003512  0.003512  0.003512  0.003512  0.003512   
21    0.002179  0.002179  0.002179  0.002179  0.002179  0.002179  0.002179   
22    0.002787  0.002787  0.002787  0.002787  0.002787  0.002787  0.002787   
23    0.002283  0.002283  0.002283  0.002283  0.002283  0.002283  0.002283   
24    0.003545  0.003545  0.003545  0.003545  0.003545  0.003545  0.003545   
25    0.002572  0.002572  0.002572  0.002572  0.002572  0.002572  0.002572   
26    0.003574  0.003574  0.003574  0.003574  0.003574  0.003574  0.003574   
27    0.002966  0.002966  0.002966  0.002966  0.002966  0.002966  0.002966   
28    0.003591  0.003591  0.003591  0.003591  0.003591  0.003591  0.003591   
29    0.003621  0.003621  0.003621  0.003621  0.003621  0.003621  0.003621   
...        ...       ...       ...       ...       ...       ...       ...   
2825  0.003621  0.003621  0.003621  0.003621  0.003621  0.003621  0.003621   
2826  0.002395  0.002395  0.002395  0.002395  0.002395  0.002395  0.002395   
2827  0.002108  0.002108  0.002108  0.002108  0.002108  0.002108  0.002108   
2828  0.002359  0.002359  0.002359  0.002359  0.002359  0.002359  0.002359   
2829  0.002318  0.002318  0.002318  0.002318  0.002318  0.002318  0.002318   
2830  0.003240  0.003240  0.003240  0.003240  0.003240  0.003240  0.003240   
2831  0.003525  0.003525  0.003525  0.003525  0.003525  0.003525  0.003525   
2832  0.003368  0.003368  0.003368  0.003368  0.003368  0.003368  0.003368   
2833  0.004588  0.004588  0.004588  0.004588  0.004588  0.004588  0.004588   
2834  0.002019  0.002019  0.002019  0.002019  0.002019  0.002019  0.002019   
2835  0.003898  0.003898  0.003898  0.003898  0.003898  0.003898  0.003898   
2836  0.001827  0.001827  0.001827  0.001827  0.001827  0.001827  0.001827   
2837  0.003308  0.003308  0.003308  0.003308  0.003308  0.003308  0.003308   
2838  0.003104  0.003104  0.003104  0.003104  0.003104  0.003104  0.003104   
2839  0.002524  0.002524  0.002524  0.002524  0.002524  0.002524  0.002524   
2840  0.002093  0.002093  0.002093  0.002093  0.002093  0.002093  0.058180   
2841  0.002279  0.002279  0.002279  0.002279  0.002279  0.002279  0.002279   
2842  0.002620  0.002620  0.002620  0.002620  0.002620  0.002620  0.002620   
2843  0.002318  0.002318  0.002318  0.002318  0.002318  0.002318  0.002318   
2844  0.003485  0.003485  0.003485 





Finish LDA for data: test


0         1         2         3         4         5         6  \
0     0.002645  0.002645  0.002645  0.002645  0.002645  0.002645  0.002645   
1     0.003035  0.003035  0.003035  0.003035  0.003035  0.003035  0.003035   
2     0.001966  0.001966  0.001966  0.001966  0.001966  0.001966  0.001966   
3     0.002767  0.002767  0.002767  0.002767  0.042433  0.002767  0.002767   
4     0.003887  0.003887  0.003887  0.003887  0.003887  0.003887  0.003887   
5     0.003622  0.003622  0.003622  0.003622  0.003622  0.003622  0.003622   
6     0.003265  0.003265  0.003265  0.003265  0.003265  0.003265  0.003265   
7     0.003995  0.003995  0.003995  0.003995  0.003995  0.003995  0.003995   
8     0.002589  0.002589  0.002589  0.002589  0.002589  0.002589  0.002589   
9     0.002523  0.002523  0.002523  0.002523  0.002523  0.002523  0.002523   
10    0.002791  0.002791  0.002791  0.002791  0.002791  0.002791  0.002791   
11    0.004400  0.004400  0.004400  0.004400  0.004400  0.004400  0.004400   
12    0.002790  0.002790  0.002790  0.002790  0.002790  0.002790  0.002790   
13    0.002142  0.002142  0.002142  0.002142  0.046437  0.002142  0.002142   
14    0.002014  0.002014  0.002014  0.002014  0.002014  0.002014  0.002014   
15    0.002463  0.002463  0.002463  0.002463  0.002463  0.002463  0.002463   
16    0.002762  0.002762  0.002762  0.002762  0.002762  0.002762  0.002762   
17    0.003368  0.003368  0.003368  0.003368  0.003368  0.003368  0.003368   
18    0.002938  0.002938  0.002938  0.429741  0.002938  0.002938  0.002938   
19    0.002063  0.002063  0.002063  0.002063  0.036414  0.002063  0.002063   
20    0.003885  0.003885  0.003885  0.003885  0.003885  0.003885  0.003885   
21    0.003219  0.003219  0.003219  0.003219  0.003219  0.003219  0.003219   
22    0.002504  0.002504  0.002504  0.002504  0.030912  0.002504  0.002504   
23    0.002330  0.002330  0.002330  0.002330  0.002330  0.002330  0.002330   
24    0.003021  0.003021  0.003021  0.003021  0.003021  0.003021  0.003021   
25    0.002600  0.002600  0.002600  0.002600  0.002600  0.002600  0.002600   
26    0.001746  0.001746  0.001746  0.001746  0.001746  0.001746  0.001746   
27    0.003122  0.003122  0.003122  0.003122  0.003122  0.003122  0.053555   
28    0.003681  0.003681  0.003681  0.003681  0.003681  0.003681  0.003681   
29    0.002112  0.002112  0.002112  0.002112  0.002112  0.002112  0.002112   
...        ...       ...       ...       ...       ...       ...       ...   
1870  0.002261  0.002261  0.002261  0.002261  0.002261  0.002261  0.002261   
1871  0.003377  0.003377  0.003377  0.003377  0.003377  0.003377  0.003377   
1872  0.002016  0.002016  0.002016  0.002016  0.002016  0.002016  0.020725   
1873  0.002681  0.002681  0.002681  0.002681  0.002681  0.002681  0.002681   
1874  0.003126  0.003126  0.003126  0.003126  0.003126  0.003126  0.003126   
1875  0.002446  0.002446  0.002446  0.002446  0.002446  0.002446  0.002446   
1876  0.003049  0.003049  0.003049  0.003049  0.003049  0.003049  0.003049   
1877  0.002742  0.002742  0.002742  0.002742  0.002742  0.002742  0.002742   
1878  0.001995  0.001995  0.001995  0.001995  0.001995  0.001995  0.001995   
1879  0.002194  0.002194  0.002194  0.002194  0.086430  0.002194  0.002194   
1880  0.002848  0.002848  0.002848  0.002848  0.002848  0.002848  0.002848   
1881  0.002742  0.002742  0.002742  0.002742  0.002742  0.002742  0.002742   
1882  0.003865  0.003865  0.003865  0.003865  0.003865  0.003865  0.003865   
1883  0.002616  0.002616  0.002616  0.002616  0.002616  0.002616  0.002616   
1884  0.002296  0.002296  0.002296  0.002296  0.002296  0.002296  0.002296   
1885  0.002613  0.002613  0.002613  0.002613  0.002613  0.002613  0.002613   
1886  0.002582  0.002582  0.002582  0.002582  0.002582  0.002582  0.002582   
1887  0.002324  0.002324  0.002324  0.036850  0.002324  0.002324  0.002324   
1888  0.002547  0.002547  0.002547  0.002547  0.002547  0.002547  0.002547   
1889  0.002133  0.002133  0.002133 





CPU times: user 22.1 s, sys: 1min 6s, total: 1min 28s
Wall time: 12.2 s


###### SVM classifier(BOW+TFIDF+LDA)

In [105]:
%%time

# Step 5: Training

# if 'TFIDF' == modelChoice:
#     #train
#     X_train = df['train'].drop('class', axis=1)
#     y_train = df['train']['class']
#     #test
#     X_test = df['test'].drop('class', axis=1)
#     y_test_true = df['test']['class']
# else:

#train
X_train = df_new['train']['x']
y_train = df_new['train']['y']
#test
X_test = df_new['test']['x']
y_test_true = df_new['test']['y']
    
clf = LinearSVC()
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 100 ms, sys: 0 ns, total: 100 ms
Wall time: 99.3 ms


In [106]:
%%time

# Step 6: Evaluate

y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

0.564736842105
0.540679398081
0.564736842105
CPU times: user 16 ms, sys: 0 ns, total: 16 ms
Wall time: 14.6 ms


###### GaussianNB classifier(BOW+TFIDF+LDA)

In [107]:
%%time

from sklearn.naive_bayes import GaussianNB

# if 'TFIDF' == modelChoice:
#     #train
#     X_train = df['train'].drop('class', axis=1)
#     y_train = df['train']['class']
#     #test
#     X_test = df['test'].drop('class', axis=1)
#     y_test_true = df['test']['class']
# else:

#train
X_train = df_new['train']['x']
y_train = df_new['train']['y']
#test
X_test = df_new['test']['x']
y_test_true = df_new['test']['y']

clf = GaussianNB()
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 4 ms, sys: 4 ms, total: 8 ms
Wall time: 5.46 ms


In [108]:
%%time

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

# print f1_score(y_test_true, tensorPredCls, average='micro')

0.417894736842
0.410272794888
0.417894736842
CPU times: user 16 ms, sys: 0 ns, total: 16 ms
Wall time: 14.4 ms


###### RF classifier(BOW+TFIDF+LDA)

In [109]:
%%time

from sklearn.ensemble import RandomForestClassifier

# if 'TFIDF' == modelChoice:
#     #train
#     X_train = df['train'].drop('class', axis=1)
#     y_train = df['train']['class']
#     #test
#     X_test = df['test'].drop('class', axis=1)
#     y_test_true = df['test']['class']
# else:

#train
X_train = df_new['train']['x']
y_train = df_new['train']['y']
#test
X_test = df_new['test']['x']
y_test_true = df_new['test']['y']

clf = RandomForestClassifier(random_state=19, n_estimators=15)
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 240 ms, sys: 4 ms, total: 244 ms
Wall time: 237 ms


In [110]:
%%time

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

# print f1_score(y_test_true, tensorPredCls, average='micro')

0.538421052632
0.531065596414
0.538421052632
CPU times: user 32 ms, sys: 0 ns, total: 32 ms
Wall time: 28.9 ms


### 3.2 Word2Vec 表示法

In [3]:
paths['dir.modelroot'] = os.path.join(paths['dir.dataroot'], '..', 'models')
for modeltool in ['gensim', 'TensorFlow']:
    for embedsource in ['text8', 'corpus']:
        dname = os.path.join(paths['dir.modelroot'], '{}.{}'.format(modeltool, embedsource))
        if not os.path.isdir(dname):
            os.mkdir(dname)
        paths['dir.{}.{}'.format(modeltool, embedsource)] = dname

#### 3.2.1 gensim 训练

In [104]:
# Step 0: Import modules

modelFrom = 'gensim'

print("Step 0 succeed.")

Step 0 succeed.


##### 3.2.1.1 基于 text8 建模

In [6]:
%%time

# Step 1: preprocess the data

# import stoplist
stopwords = ""

pathtemp_TFIDF = os.path.join(paths['dir.dataroot'], 'stoplist-baseTFIDF.txt')
with open(pathtemp_TFIDF, 'r') as stoplistfile:
    stopwords = stoplistfile.read()
stopwords = stopwords.split()

pathtemp_web = os.path.join(paths['dir.dataroot'], 'stoplist-web.txt')
with open(pathtemp_web, 'r') as stoplistfile2:
    stopwords2 = stoplistfile2.read()
    stopwords2 = stopwords2.split('\n')
    stopwords = set(stopwords)
    stopwords = list(stopwords.union(set(stopwords)))
    
print("Read stop words successfully.")

Read stop words successfully.
CPU times: user 4 ms, sys: 8 ms, total: 12 ms
Wall time: 23.2 ms


In [7]:
%%time
   
trimmer = lambda word, count, min_count: gensim.utils.RULE_DISCARD if word in stopwords else gensim.utils.RULE_KEEP

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 5.01 µs


In [8]:
%%time

embedFrom = 'text8'
text8fname = os.path.join(paths['dir.dataroot'], 'text8')
sentences = gensim.models.word2vec.Text8Corpus(text8fname)

vecsize = 784
model = gensim.models.word2vec.Word2Vec(iter=15, size=vecsize, sg=1, window=5, workers=12)
model.build_vocab(sentences=sentences, trim_rule=trimmer)
model.train(sentences=sentences)

CPU times: user 2h 13min 36s, sys: 8.62 s, total: 2h 13min 45s
Wall time: 31min 56s


In [15]:
%%time

# save model

calander = datetime.date.today().timetuple()

modelpath = os.path.join(
    paths['dir.{}.{}'.format(modelFrom, embedFrom)],
    '{}.{}.{}{}{}'.format(modelFrom, embedFrom, calander.tm_year, calander.tm_mon, calander.tm_mday)
)
model.save(modelpath)

print("save model finished")

save model finished
CPU times: user 2.58 s, sys: 228 ms, total: 2.81 s
Wall time: 12.5 s


In [17]:
%%time

# Step 2: read data and save it in data['vec.train'] 和 data['vec.test']

data = {}
data['vec.train'] = {'w2v.mean':[], 'class':[]}
data['vec.test'] = {'w2v.mean':[], 'class':[]}

for tpart in ['train', 'test']:
    dirpath = paths['dir.{}'.format(tpart)]
    for (ind, cls) in enumerate(os.listdir(dirpath)):
        clspath = os.path.join(dirpath, cls)
        files = os.listdir(clspath)
        for f in files:
            fpath = os.path.join(clspath, f)
            with open(fpath, 'r') as readf:
                tokens = [token for token in readf.read().split()] # if token not in stopwords]#readf.read().split()#
                # Word2Vec representation
                # begin
                vec = np.array([0.0 for i in range(vecsize)])
                expectationVal = np.array([0.0 for i in range(vecsize)])
                countvec = 0
                for token in tokens:
                    try:
                        vec += model[token]
                        countvec += 1
                    except:
                        vec += expectationVal
                vec = vec / float(countvec)#float(len(tokens))
                 # end
            data['vec.{}'.format(tpart)]['w2v.mean'].append(vec)
            data['vec.{}'.format(tpart)]['class'].append(cls)

    tmp = data['vec.{}'.format(tpart)]
    ind = (random.sample(range(len(tmp['class'])), 1))[0]
    print("sample(transformed) from {}[{}]:\n[corpus]\n {}\n[class]\n{}".format(
            tpart, ind, tmp['w2v.mean'][ind], tmp['class'][ind]
        )
    )
    print()
    
print("Step 2 Succeed")

sample(transformed) from train[1294]:
[corpus]
 [  1.42176096e-01   1.62430700e-01  -8.79922659e-02   5.35091242e-02
   8.59380437e-02   2.62035794e-04   7.22310296e-02   2.61135434e-02
  -2.16664064e-02   5.44147822e-02   1.06476713e-01  -5.75761132e-02
  -1.10888660e-01  -2.65366570e-02  -1.12344211e-01   7.02185809e-02
   2.53348814e-02   1.30706466e-01  -1.04799571e-01   4.39703308e-02
  -9.66833411e-03   1.64926087e-02   7.21110973e-02   4.64726405e-02
   1.42359131e-01   2.71736607e-02  -1.44038068e-03  -3.01274558e-02
  -1.66951142e-01  -1.89049134e-01  -1.28849644e-01   1.76089907e-01
   7.72865493e-02  -3.66129199e-02  -1.38183594e-02   2.13841639e-02
   1.38888888e-02   1.29469739e-01   1.23148409e-01  -1.73164004e-01
   2.79120405e-02  -7.15156136e-02  -1.03259663e-02   6.85949264e-03
   5.14812296e-03  -1.38993850e-01  -2.75248113e-02   5.88013921e-02
  -1.28485937e-02   2.55639031e-02  -5.69223881e-03   6.49880191e-03
   1.56568261e-02  -3.84757851e-02  -4.55514945e-02  -5

sample(transformed) from test[1009]:
[corpus]
 [  1.57098071e-01   1.53154620e-01  -9.61496837e-02   7.66679577e-02
   9.88287428e-02   2.56884951e-02   4.97653553e-02   1.61335431e-02
  -4.28836131e-02   8.93512531e-02   8.97204755e-02  -4.42556309e-02
  -1.20880319e-01  -3.39067199e-02  -1.21989825e-01   6.05836994e-02
   2.43342272e-02   1.07924186e-01  -7.54850704e-02   2.36673727e-02
  -1.31180015e-02   3.76038207e-02   5.74989647e-02   4.92838261e-02
   1.01037374e-01   3.15683201e-02   2.09713250e-02  -1.74226246e-02
  -1.54403559e-01  -1.89296066e-01  -1.21736109e-01   1.71895260e-01
   5.00430703e-02  -5.84864492e-02  -1.67442754e-02   1.83596857e-02
   2.22139320e-02   1.44453748e-01   1.37844339e-01  -1.70359024e-01
   1.47091010e-02  -7.39391100e-02  -1.53880306e-02   6.87595693e-03
   1.30805930e-02  -1.23579607e-01  -2.07829833e-02   3.87572804e-02
  -2.03224753e-02   2.31136564e-02  -3.07712576e-02   1.17793162e-02
   9.60251690e-03  -2.09789647e-02  -2.84358605e-02  -3.

In [19]:
%%time

# Step 3: Save in Pandas.DataFrame
#
# 将 data['matrix.train'] 与 data['matrix.test'] 转换成 Pandas.DataFrame 格式，保存到 df['train'] 和 df['test'] 中（df 为字典格式：String -> DataFrame）

df = {}
csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')
for tpart in ['train', 'test']:
    datadict = {}
    datadict['class'] = data['vec.{}'.format(tpart)]['class']
    datavec = np.array(data['vec.{}'.format(tpart)]['w2v.mean'])
    for col in range(vecsize):
        datadict[col]= datavec[:, col]

    df[tpart] = pd.DataFrame(data=datadict)
    print("See df[{}]".format(tpart))
    display(df[tpart])
    print("\n\n\n")
    # write data in DataFrame into CSV
    csvpath = os.path.join(csvpath_root, '{}-w2v-{}-{}.csv'.format(tpart, embedFrom, modelFrom))
    df[tpart].to_csv(csvpath, columns=df[tpart].columns)
    
print("Step 3 Succeed.")

# 繁琐点：研究如何把 CSR 矩阵中的数据规整好放到 DataFrame 中，并与 Class 一一对应

See df[train]


0         1         2         3         4         5         6  \
0     0.147760  0.191871 -0.123469  0.066009  0.132763 -0.006644  0.044266   
1     0.178941  0.187470 -0.079834  0.107205  0.166234  0.019693  0.040066   
2     0.202831  0.170065 -0.097257  0.128243  0.140756  0.013609  0.016742   
3     0.208845  0.245270 -0.103284  0.091380  0.157237  0.048984  0.036000   
4     0.185805  0.200608 -0.090226  0.083986  0.157810  0.045228  0.077690   
5     0.105656  0.135173 -0.043216  0.047694  0.105946 -0.001172  0.115349   
6     0.178755  0.182410 -0.090002  0.091815  0.152302  0.048337  0.032308   
7     0.090505  0.109543 -0.060146  0.057255  0.110668 -0.001868  0.093157   
8     0.111884  0.144636 -0.063390  0.072714  0.108716  0.017135  0.085774   
9     0.135486  0.172539 -0.071040  0.081852  0.130687  0.036760  0.045177   
10    0.162095  0.172058 -0.088721  0.077929  0.146985  0.070191  0.054317   
11    0.222626  0.216064 -0.127515  0.104405  0.160959  0.029589  0.064679   
12    0.154504  0.169176 -0.059434  0.055910  0.185943  0.045174  0.079897   
13    0.152342  0.188716 -0.112604  0.121225  0.139806  0.015135  0.083964   
14    0.172577  0.221478 -0.110161  0.058599  0.134431  0.042521  0.077642   
15    0.131379  0.129465 -0.121818  0.092100  0.144549  0.029272  0.085845   
16    0.140511  0.142286 -0.068152  0.108739  0.119766 -0.004535  0.048747   
17    0.122910  0.143813 -0.092348  0.092174  0.124191  0.023471  0.139143   
18    0.177640  0.191123 -0.094911  0.075975  0.152818  0.014798  0.068086   
19    0.142610  0.176793 -0.062559  0.066552  0.110619  0.039602  0.058616   
20    0.211895  0.250124 -0.115707  0.118031  0.161877  0.047215  0.010363   
21    0.181085  0.190281 -0.095513  0.093271  0.155093  0.020474  0.047834   
22    0.177891  0.242455 -0.139848  0.078169  0.167423  0.056014 -0.045467   
23    0.078446  0.126936 -0.023998  0.065351  0.071569 -0.012314  0.153840   
24    0.193238  0.176844 -0.079434  0.108053  0.141662  0.009577  0.030864   
25    0.137151  0.195863 -0.071267  0.091254  0.137261  0.025312  0.043402   
26    0.135823  0.171097 -0.065986  0.119198  0.112083  0.020418  0.065303   
27    0.128629  0.187485 -0.114251  0.078050  0.142588  0.044282  0.063183   
28    0.194795  0.231499 -0.102752  0.093682  0.176355  0.059626  0.049665   
29    0.155941  0.221754 -0.117797  0.084991  0.145090  0.068779  0.074112   
...        ...       ...       ...       ...       ...       ...       ...   
2825  0.071271  0.113390 -0.077952  0.079021  0.064822  0.020891  0.107882   
2826  0.058302  0.156030 -0.091380  0.037381  0.118860  0.030108  0.063615   
2827  0.198039  0.152258 -0.119355  0.051209  0.127293 -0.009148  0.040107   
2828  0.021865  0.024779 -0.061108  0.074593  0.028340 -0.040167  0.154038   
2829  0.129839  0.194295 -0.043000  0.050693  0.082227  0.041639  0.085732   
2830  0.170705  0.194907 -0.065708  0.058695  0.134268  0.049534  0.044103   
2831  0.172744  0.243823 -0.100837  0.061038  0.121385  0.039872  0.046400   
2832  0.162433  0.170713 -0.113378  0.043762  0.116479  0.019905  0.029361   
2833  0.181663  0.207865 -0.116587  0.046881  0.139307 -0.017782  0.039065   
2834  0.059306  0.133735 -0.093277  0.027343  0.070099  0.004548  0.127238   
2835  0.137362  0.142111 -0.083411  0.071114  0.128261  0.024801  0.042113   
2836  0.154419  0.102545 -0.106527  0.038236  0.152139  0.013717  0.076000   
2837  0.093639  0.146624 -0.055606  0.037904  0.073534  0.022987  0.097103   
2838  0.192681  0.181971 -0.081961  0.052159  0.101714  0.048268  0.049469   
2839  0.148440  0.163994 -0.103210  0.074050  0.115084  0.054684  0.063263   
2840  0.127055  0.103201 -0.083405  0.109374  0.086221  0.019461  0.121827   
2841  0.185625  0.171394 -0.088689  0.049941  0.136087  0.008373  0.097199   
2842  0.193263  0.192556 -0.099069  0.071241  0.121544  0.021540  0.049824   
2843  0.180480  0.221816 -0.139741  0.071917  0.107563  0.011498  0.066763   
2844  0.193388  0.201054 -0.017912 





See df[test]


0         1         2         3         4         5         6  \
0     0.181281  0.228398 -0.075890  0.098953  0.124880  0.040266  0.058507   
1     0.166943  0.141915 -0.058615  0.072855  0.123155  0.022023  0.037875   
2     0.146988  0.125112 -0.043065  0.094749  0.106156  0.000753  0.046489   
3     0.131239  0.177776 -0.054687  0.067915  0.103457  0.034679  0.087555   
4     0.160831  0.223853 -0.106787  0.097534  0.147625  0.072289  0.030739   
5     0.212691  0.201205 -0.110092  0.121360  0.171044  0.069911  0.012311   
6     0.171318  0.173036 -0.055780  0.084935  0.139292  0.023904  0.041544   
7     0.179166  0.204333 -0.074029  0.094361  0.138624  0.024829  0.047687   
8     0.194129  0.174792 -0.083872  0.109072  0.140045  0.016814  0.043043   
9     0.135488  0.154116 -0.044559  0.073116  0.123987  0.040695  0.047806   
10    0.149890  0.160048 -0.076857  0.102619  0.156779  0.008365  0.041224   
11    0.168216  0.201354 -0.078389  0.072127  0.156415  0.032315  0.063408   
12    0.141200  0.139243 -0.063592  0.073705  0.143937  0.035392  0.053566   
13    0.192610  0.215701 -0.094337  0.116624  0.161552  0.041789  0.031412   
14    0.182753  0.250389 -0.105763  0.113689  0.140383  0.061041  0.060622   
15    0.159528  0.194087 -0.046207  0.093266  0.131431  0.054907  0.041467   
16    0.177169  0.214569 -0.077326  0.104346  0.151844  0.023041  0.033982   
17    0.169791  0.178564 -0.083783  0.102050  0.132602  0.030950  0.050054   
18    0.114981  0.162886 -0.067040  0.053411  0.136987  0.081957  0.066787   
19    0.202178  0.207319 -0.100093  0.102510  0.137419  0.035322  0.020692   
20    0.179737  0.205979 -0.110711  0.081983  0.125541  0.032909  0.037508   
21    0.096436  0.194829 -0.088135  0.032717  0.141311  0.019195  0.073993   
22    0.199468  0.168032 -0.082349  0.109168  0.171094  0.024342  0.046611   
23    0.150471  0.192546 -0.063968  0.067679  0.119811  0.047731  0.061057   
24    0.194139  0.191041 -0.127643  0.086269  0.135014  0.027086 -0.000101   
25    0.136200  0.208137 -0.056846  0.076029  0.108096 -0.027683  0.054063   
26    0.110678  0.179432 -0.089891  0.075500  0.119552  0.048627  0.072044   
27    0.063569  0.082086 -0.071906  0.065001  0.049270 -0.013082  0.102855   
28    0.156534  0.195353 -0.072159  0.062962  0.116792  0.028029  0.066263   
29    0.183987  0.188483 -0.061170  0.105340  0.072515  0.061259  0.089648   
...        ...       ...       ...       ...       ...       ...       ...   
1870  0.148789  0.132446 -0.033796  0.055329  0.086632  0.010159  0.045082   
1871  0.100076  0.194514 -0.044546 -0.006824  0.167447  0.065927  0.123246   
1872  0.157254  0.193971 -0.097019  0.025098  0.148397  0.027434  0.037771   
1873  0.131812  0.134859 -0.075134  0.081538  0.065448 -0.014160  0.059577   
1874  0.196787  0.187597 -0.107342  0.071219  0.106727  0.002655  0.038339   
1875  0.162975  0.133288 -0.093159  0.061982  0.166610  0.006201 -0.012648   
1876  0.113823  0.144234 -0.029475  0.033407  0.095782  0.059701  0.094755   
1877  0.140071  0.165126 -0.036385  0.048649  0.116078  0.023650  0.116735   
1878  0.125150  0.144529 -0.054766  0.033559  0.104399  0.005031  0.078652   
1879  0.157576  0.184515 -0.073030  0.017603  0.137401  0.040459  0.043383   
1880  0.180685  0.272234 -0.131311  0.076371  0.137425  0.005786  0.044911   
1881  0.084474  0.211032 -0.132641  0.048395  0.077387 -0.053563  0.037660   
1882 -0.003077  0.028294  0.011205  0.091322  0.017548 -0.029394  0.174474   
1883  0.027663  0.094470 -0.048278  0.057297  0.095340 -0.015298  0.146122   
1884  0.205928  0.194644 -0.095999  0.096824  0.129357  0.041130  0.055286   
1885  0.177872  0.216221 -0.145886  0.070507  0.122922  0.000701  0.077278   
1886  0.195437  0.171918 -0.049702  0.072552  0.121258  0.034261  0.039014   
1887  0.127866  0.130091 -0.098764  0.051038  0.097774 -0.037771  0.049867   
1888  0.062684  0.106540 -0.012121  0.073004  0.059651 -0.004999  0.121160   
1889  0.100528  0.140299 -0.043936 





Step 3 Succeed.
CPU times: user 2.07 s, sys: 56 ms, total: 2.12 s
Wall time: 2.17 s


In [107]:
%%time

# if wanna read data from CSV file

df = {}

for tpart in ['train', 'test']:
    csvpath = os.path.join(
        csvpath_root, '{}-w2v-{}-{}.csv'.format(
            tpart, embedFrom, modelFrom
        )
    )
    if os.path.exists(csvpath):
        df[tpart] = pd.DataFrame.from_csv(csvpath)
        df[tpart] = df[tpart].sample(frac=1)
        df[tpart].reset_index(drop=True, inplace=True)
        print("read {} successfully".format(tpart))
        display(df[tpart])

read train successfully


0         1         2         3         4         5         6  \
0     0.177065  0.220111 -0.144173  0.102411  0.097858  0.019923  0.061870   
1     0.150134  0.171049 -0.060894  0.035372  0.127200  0.028285  0.075184   
2     0.112585  0.129564 -0.096344  0.075622  0.157670  0.073118  0.048869   
3     0.168117  0.169154 -0.078624  0.084069  0.112711  0.024250  0.064745   
4     0.141454  0.179205 -0.080936  0.077810  0.106397  0.034038  0.074566   
5     0.113995  0.096731 -0.069479  0.079731  0.107044 -0.034205  0.068047   
6     0.205406  0.228389 -0.157220  0.121508  0.150480  0.032163  0.029472   
7     0.091921  0.119454 -0.075911  0.022086  0.119876  0.031191  0.005383   
8     0.136040  0.130605 -0.019988  0.053304  0.095861  0.036624  0.086791   
9     0.175618  0.133833 -0.115383  0.085493  0.079358 -0.024408  0.049117   
10    0.117902  0.194525 -0.056931  0.027035  0.091891 -0.005668  0.005692   
11    0.130591  0.164588 -0.050166  0.061378  0.059213  0.030862  0.098686   
12    0.108645  0.130373 -0.108323  0.093349  0.086862  0.000883  0.067182   
13    0.126230  0.146033 -0.052469  0.079792  0.149858  0.025801  0.067134   
14   -0.011213 -0.009534 -0.014114  0.060394 -0.033664 -0.060154  0.176163   
15    0.184901  0.209987 -0.109861  0.078069  0.124914  0.060678  0.074243   
16    0.151931  0.126264 -0.080399  0.053873  0.119058 -0.017706  0.027886   
17    0.154924  0.171981 -0.072188  0.079456  0.088260  0.038808  0.079939   
18    0.179767  0.218787 -0.090974  0.118157  0.163987  0.040373  0.065020   
19    0.208550  0.246874 -0.126726  0.100538  0.165595  0.071685  0.066860   
20    0.039129  0.110735 -0.027092  0.051592  0.027833 -0.015104  0.132636   
21    0.109007  0.136777 -0.085659 -0.009826  0.123189  0.043271  0.059475   
22    0.145895  0.137752 -0.063687  0.069757  0.089283  0.008931  0.080513   
23    0.168451  0.214298 -0.070676  0.093134  0.133606  0.024364  0.060528   
24    0.183014  0.226249 -0.117933  0.097446  0.158779  0.048783  0.019838   
25    0.085521  0.101473 -0.056685  0.091466  0.079772 -0.028800  0.107575   
26    0.189399  0.257119 -0.104258  0.069586  0.147726  0.044171  0.043588   
27    0.102460  0.167259 -0.065114 -0.021404  0.093348  0.079948  0.084512   
28    0.146615  0.132083 -0.061436  0.065074  0.139474 -0.018222  0.086363   
29    0.132726  0.202794 -0.108171  0.063919  0.124490  0.035510  0.062949   
...        ...       ...       ...       ...       ...       ...       ...   
2825  0.094576  0.117498 -0.045228  0.059639  0.067065  0.026102  0.112855   
2826  0.136039  0.175921 -0.094485  0.068387  0.084464  0.018209  0.065720   
2827  0.091710  0.084212 -0.030525  0.062610  0.074783 -0.035449  0.096438   
2828  0.130656  0.185552 -0.087018  0.080786  0.115367  0.007847  0.083633   
2829  0.095492  0.108791 -0.063974  0.076104  0.056237 -0.004990  0.089673   
2830  0.135778  0.153317 -0.075192  0.071002  0.105122  0.033143  0.049158   
2831  0.104240  0.113733 -0.090184  0.086599  0.067312 -0.004696  0.046830   
2832  0.125844  0.111124 -0.071720  0.075755  0.105312 -0.029168  0.066679   
2833  0.139172  0.170530 -0.063397  0.103264  0.115035  0.021188  0.067695   
2834  0.141889  0.155178 -0.071288  0.105881  0.140904  0.021315  0.077836   
2835 -0.002252  0.063490 -0.044209  0.044727  0.112427  0.041107  0.080649   
2836  0.192704  0.273443 -0.108419  0.066027  0.058256  0.018449  0.056844   
2837  0.150111  0.161882 -0.085860  0.061144  0.126276  0.007136  0.040628   
2838  0.222862  0.211019 -0.110036  0.115564  0.168499  0.044787  0.036275   
2839  0.147888  0.168499 -0.051498  0.087781  0.145556  0.037855  0.068117   
2840  0.173505  0.174000 -0.092658  0.120069  0.144129  0.018138  0.033606   
2841  0.178111  0.179582 -0.113234  0.061666  0.131081  0.025490  0.020585   
2842  0.043601  0.040622 -0.016110  0.052550  0.002340 -0.021993  0.135136   
2843  0.173464  0.186848 -0.090403  0.087853  0.110594  0.038847  0.060332   
2844  0.092034  0.217844 -0.053449 

read test successfully


0         1         2         3         4         5         6  \
0     0.055221  0.074701 -0.059779  0.047216  0.091813 -0.038038  0.093739   
1     0.123648  0.142640 -0.050926  0.069142  0.085433  0.033125  0.103106   
2     0.213773  0.273997 -0.092123  0.057986  0.163515  0.074589  0.058103   
3     0.157166  0.165131 -0.074020  0.041901  0.103741 -0.003904  0.070539   
4     0.157254  0.193971 -0.097019  0.025098  0.148397  0.027434  0.037771   
5     0.094931  0.158852 -0.083298  0.036415  0.061289  0.039578  0.131851   
6     0.071874  0.081405 -0.021858  0.022914  0.056762 -0.018064  0.104337   
7     0.042522  0.043513 -0.066467  0.065892  0.002371 -0.048086  0.099314   
8     0.183396  0.187342 -0.087993  0.083409  0.112866  0.055050  0.091043   
9     0.033685  0.095458 -0.030138  0.075265  0.045467  0.012184  0.143523   
10    0.169013  0.193968 -0.089646  0.056835  0.117422  0.031641  0.095195   
11    0.132552  0.190877 -0.075341  0.084076  0.131842  0.028114  0.081712   
12    0.207274  0.232362 -0.104213  0.102210  0.147955  0.054353  0.046147   
13    0.181634  0.177800 -0.110879  0.098486  0.171617  0.029683  0.035103   
14    0.064629  0.145026 -0.031852  0.025517  0.083390 -0.001740  0.128579   
15    0.161037  0.193690 -0.059920  0.044147  0.090642  0.034255  0.070634   
16    0.130575  0.154724 -0.063731  0.038252  0.120476  0.026758  0.041037   
17    0.190946  0.252354 -0.092499  0.066758  0.157232  0.079162  0.079522   
18    0.164138  0.166768 -0.099780  0.053194  0.115419  0.033119  0.053676   
19    0.180330  0.181459 -0.069861  0.122279  0.120084  0.029709  0.027765   
20    0.132502  0.153184 -0.057914  0.078943  0.128044  0.024293  0.082131   
21    0.166329  0.207806 -0.083375  0.068519  0.141447  0.053457  0.074817   
22    0.197846  0.247212 -0.083797  0.075598  0.162293  0.073360  0.066177   
23    0.049107  0.137533 -0.100332 -0.021621  0.049791 -0.009962  0.113164   
24    0.102445  0.154623 -0.047008  0.064018  0.091999  0.024409  0.093220   
25    0.032051  0.091975 -0.050946  0.059247  0.076503 -0.027892  0.131071   
26    0.140249  0.152874 -0.096590  0.073693  0.101828  0.031067  0.032603   
27    0.113356  0.119794 -0.070080  0.048572  0.108092  0.012252  0.074870   
28    0.209196  0.191052 -0.177077  0.144669  0.081272  0.104138  0.013191   
29    0.091357  0.097420 -0.064005  0.081468  0.055704 -0.024642  0.068056   
...        ...       ...       ...       ...       ...       ...       ...   
1870  0.117762  0.124517 -0.041857  0.024963  0.108873  0.009382  0.101277   
1871  0.120553  0.132416 -0.043591  0.081193  0.095935  0.005574  0.061061   
1872  0.221389  0.224979 -0.147323  0.113984  0.177654  0.057523  0.007882   
1873  0.173994  0.237144 -0.101062  0.038168  0.147270  0.064654  0.077468   
1874  0.190682  0.157505 -0.060240  0.095377  0.071730  0.029962  0.059201   
1875  0.118946  0.134260 -0.076084  0.025078  0.084583  0.004520  0.052954   
1876  0.168808  0.215087 -0.096526  0.105796  0.133693  0.057351  0.040471   
1877  0.057631  0.067463 -0.025655  0.094824  0.063173 -0.017570  0.113562   
1878  0.055609  0.114078 -0.092452  0.007427  0.098883  0.005676  0.067568   
1879  0.138128  0.140918 -0.067286  0.091543  0.113272  0.003037  0.057171   
1880  0.053934  0.101909 -0.056073  0.059978  0.085074 -0.024453  0.127287   
1881  0.188916  0.201498 -0.069979  0.113334  0.133969  0.053789  0.036570   
1882  0.203412  0.165657 -0.100915  0.103722  0.147109  0.025777  0.028914   
1883  0.206107  0.198907 -0.089224  0.091568  0.103317  0.026266  0.026493   
1884  0.150471  0.192546 -0.063968  0.067679  0.119811  0.047731  0.061057   
1885  0.148239  0.183223 -0.084541  0.057551  0.132042  0.033958  0.074643   
1886  0.200826  0.234957 -0.082695  0.093878  0.170609  0.054823  0.032368   
1887  0.032559  0.203913 -0.055399  0.022435  0.069162 -0.025985  0.182403   
1888  0.127819  0.119433 -0.049642  0.067636  0.074255 -0.004000  0.066163   
1889  0.204929  0.259567 -0.082867 

CPU times: user 944 ms, sys: 0 ns, total: 944 ms
Wall time: 944 ms


###### SVM classifier(gensim + text8)

In [108]:
%%time

# Step 5.1.1: SVM

# if 'TFIDF' == modelChoice:

#train
X_train = df['train'].drop('class', axis=1)
y_train = df['train']['class']
#test
X_test = df['test'].drop('class', axis=1)
y_test_true = df['test']['class']

# else:
#     #train
#     X_train = df_new['train']['x']
#     y_train = df_new['train']['y']
#     #test
#     X_test = df_new['test']['x']
#     y_test_true = df_new['test']['y']

clf = LinearSVC()
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 1.99 s, sys: 0 ns, total: 1.99 s
Wall time: 1.99 s


In [109]:
%%time
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

0.830526315789
0.827658664987
0.830526315789
CPU times: user 24 ms, sys: 0 ns, total: 24 ms
Wall time: 21.3 ms


###### DNN classifier(gensim + text8)

In [110]:
%%time

# Step 4: One-hot representation for labels

csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')

lb = LabelBinarizer()
lb.fit(df['train']['class'])

df_new = {}
for tpart in ['train', 'test']:
    labels = lb.transform(df[tpart]['class'])
    labelsDf = pd.DataFrame(labels, columns=["class-{}".format(i) for i in range(len(lb.classes_))])
    df_new[tpart] = {}
    df_new[tpart]['y'] = labelsDf
    df_new[tpart]['x'] = df[tpart].drop('class', axis=1)
    df_new[tpart]['all'] = df_new[tpart]['x'].join(df_new[tpart]['y'])
    #save in CSV
    for subpart in ['x', 'y', 'all']:
        csvpath = os.path.join(csvpath_root, "{}-cleanLabels-{}-{}.csv".format(tpart, subpart, modelFrom))
        df_new[tpart][subpart].to_csv(csvpath)
    
print("label cleaning succussfully")

label cleaning succussfully
CPU times: user 3.64 s, sys: 108 ms, total: 3.75 s
Wall time: 3.75 s


In [111]:
%%time

## Step 5 : Train the classifier

COL_OUTCOME = 'class'
COL_FEATURE = [str(col) for col in list(df['train'].columns) if col != COL_OUTCOME]

cls2num = {cls:ind for (ind, cls) in enumerate(df['train']['class'].unique())}

def my_input_fn(dataset):
    # Save dataset in tf format
    feature_cols = {
        str(col): tf.constant(
            df[dataset][str(col)].values
        )
        for col in COL_FEATURE
    }
    labels = tf.constant([cls2num[labelname] for labelname in df[dataset][COL_OUTCOME].values])
    # Returns the feature columns and labels in tf format
    return feature_cols, labels

feature_columns = [tf.contrib.layers.real_valued_column(column_name=str(col)) for col in COL_FEATURE]
clf = tf.contrib.learn.DNNClassifier(
    feature_columns=feature_columns, 
    hidden_units=[512], 
    n_classes=len(df['train']['class'].unique())
)

clf.fit(input_fn=lambda: my_input_fn('train'), steps=2000)

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_num_ps_replicas': 0, '_keep_checkpoint_max': 5, '_tf_random_seed': None, '_task_type': None, '_environment': 'local', '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f152ac0e1d0>, '_tf_config': gpu_options {
  per_process_gpu_memory_fraction: 1.0
}
, '_task_id': 0, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_evaluation_master': '', '_keep_checkpoint_every_n_hours': 10000, '_master': ''}


Instructions for updating:
Please switch to tf.summary.scalar. Note that tf.summary.scalar uses the node name instead of the tag. This means that TensorFlow will automatically de-duplicate summary names based on the scope they are created in. Also, passing a tensor or list of tags to a scalar summary op is no longer supported.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/tmp26dqmD/model.ckpt.
INFO:tensorflow:loss = 1.61282, step = 1
INFO:tensorflow:global_step/sec: 11.1793
INFO:tensorflow:loss = 1.36607, step = 101
INFO:tensorflow:global_step/sec: 11.0008
INFO:tensorflow:loss = 1.15435, step = 201
INFO:tensorflow:global_step/sec: 10.8384
INFO:tensorflow:loss = 0.987877, step = 301
INFO:tensorflow:global_step/sec: 11.5904
INFO:tensorflow:loss = 0.858602, step = 401
INFO:tensorflow:global_step/sec: 11.781
INFO:tensorflow:loss = 0.762772, step = 501
INFO:tensorflow:global_step/sec: 11.7706
INFO:tensorflow:loss = 0.690341, step = 601
INFO:t

In [112]:
%%time

## Step 6: Evaluate

accuracy_score = clf.evaluate(input_fn=lambda: my_input_fn('test'), steps=df['test'].shape[0])['accuracy']
print("Test Accuracy by TensorFlow: {}".format(accuracy_score))

X_tensor_test, yt = my_input_fn('test')
tensorPredCls = list(clf.predict(input_fn=lambda: my_input_fn('test')))
num2cls = {v:k for (k, v) in cls2num.items()}
tensorPredClsStr = [num2cls[i] for i in tensorPredCls]
y_test_true = df['test']['class']
print('Test Accuracy by Scikit-learn: ', f1_score(y_test_true, tensorPredClsStr, average='micro'))

Instructions for updating:
Please switch to tf.summary.scalar. Note that tf.summary.scalar uses the node name instead of the tag. This means that TensorFlow will automatically de-duplicate summary names based on the scope they are created in. Also, passing a tensor or list of tags to a scalar summary op is no longer supported.
INFO:tensorflow:Starting evaluation at 2017-05-13-10:00:32
INFO:tensorflow:Evaluation [1/1900]
INFO:tensorflow:Evaluation [2/1900]
INFO:tensorflow:Evaluation [3/1900]
INFO:tensorflow:Evaluation [4/1900]
INFO:tensorflow:Evaluation [5/1900]
INFO:tensorflow:Evaluation [6/1900]
INFO:tensorflow:Evaluation [7/1900]
INFO:tensorflow:Evaluation [8/1900]
INFO:tensorflow:Evaluation [9/1900]
INFO:tensorflow:Evaluation [10/1900]
INFO:tensorflow:Evaluation [11/1900]
INFO:tensorflow:Evaluation [12/1900]
INFO:tensorflow:Evaluation [13/1900]
INFO:tensorflow:Evaluation [14/1900]
INFO:tensorflow:Evaluation [15/1900]
INFO:tensorflow:Evaluation [16/1900]
INFO:tensorflow:Evaluation [1

INFO:tensorflow:Evaluation [73/1900]
INFO:tensorflow:Evaluation [74/1900]
INFO:tensorflow:Evaluation [75/1900]
INFO:tensorflow:Evaluation [76/1900]
INFO:tensorflow:Evaluation [77/1900]
INFO:tensorflow:Evaluation [78/1900]
INFO:tensorflow:Evaluation [79/1900]
INFO:tensorflow:Evaluation [80/1900]
INFO:tensorflow:Evaluation [81/1900]
INFO:tensorflow:Evaluation [82/1900]
INFO:tensorflow:Evaluation [83/1900]
INFO:tensorflow:Evaluation [84/1900]
INFO:tensorflow:Evaluation [85/1900]
INFO:tensorflow:Evaluation [86/1900]
INFO:tensorflow:Evaluation [87/1900]
INFO:tensorflow:Evaluation [88/1900]
INFO:tensorflow:Evaluation [89/1900]
INFO:tensorflow:Evaluation [90/1900]
INFO:tensorflow:Evaluation [91/1900]
INFO:tensorflow:Evaluation [92/1900]
INFO:tensorflow:Evaluation [93/1900]
INFO:tensorflow:Evaluation [94/1900]
INFO:tensorflow:Evaluation [95/1900]
INFO:tensorflow:Evaluation [96/1900]
INFO:tensorflow:Evaluation [97/1900]
INFO:tensorflow:Evaluation [98/1900]
INFO:tensorflow:Evaluation [99/1900]
I

INFO:tensorflow:Evaluation [290/1900]
INFO:tensorflow:Evaluation [291/1900]
INFO:tensorflow:Evaluation [292/1900]
INFO:tensorflow:Evaluation [293/1900]
INFO:tensorflow:Evaluation [294/1900]
INFO:tensorflow:Evaluation [295/1900]
INFO:tensorflow:Evaluation [296/1900]
INFO:tensorflow:Evaluation [297/1900]
INFO:tensorflow:Evaluation [298/1900]
INFO:tensorflow:Evaluation [299/1900]
INFO:tensorflow:Evaluation [300/1900]
INFO:tensorflow:Evaluation [301/1900]
INFO:tensorflow:Evaluation [302/1900]
INFO:tensorflow:Evaluation [303/1900]
INFO:tensorflow:Evaluation [304/1900]
INFO:tensorflow:Evaluation [305/1900]
INFO:tensorflow:Evaluation [306/1900]
INFO:tensorflow:Evaluation [307/1900]
INFO:tensorflow:Evaluation [308/1900]
INFO:tensorflow:Evaluation [309/1900]
INFO:tensorflow:Evaluation [310/1900]
INFO:tensorflow:Evaluation [311/1900]
INFO:tensorflow:Evaluation [312/1900]
INFO:tensorflow:Evaluation [313/1900]
INFO:tensorflow:Evaluation [314/1900]
INFO:tensorflow:Evaluation [315/1900]
INFO:tensorf

INFO:tensorflow:Evaluation [506/1900]
INFO:tensorflow:Evaluation [507/1900]
INFO:tensorflow:Evaluation [508/1900]
INFO:tensorflow:Evaluation [509/1900]
INFO:tensorflow:Evaluation [510/1900]
INFO:tensorflow:Evaluation [511/1900]
INFO:tensorflow:Evaluation [512/1900]
INFO:tensorflow:Evaluation [513/1900]
INFO:tensorflow:Evaluation [514/1900]
INFO:tensorflow:Evaluation [515/1900]
INFO:tensorflow:Evaluation [516/1900]
INFO:tensorflow:Evaluation [517/1900]
INFO:tensorflow:Evaluation [518/1900]
INFO:tensorflow:Evaluation [519/1900]
INFO:tensorflow:Evaluation [520/1900]
INFO:tensorflow:Evaluation [521/1900]
INFO:tensorflow:Evaluation [522/1900]
INFO:tensorflow:Evaluation [523/1900]
INFO:tensorflow:Evaluation [524/1900]
INFO:tensorflow:Evaluation [525/1900]
INFO:tensorflow:Evaluation [526/1900]
INFO:tensorflow:Evaluation [527/1900]
INFO:tensorflow:Evaluation [528/1900]
INFO:tensorflow:Evaluation [529/1900]
INFO:tensorflow:Evaluation [530/1900]
INFO:tensorflow:Evaluation [531/1900]
INFO:tensorf

INFO:tensorflow:Evaluation [722/1900]
INFO:tensorflow:Evaluation [723/1900]
INFO:tensorflow:Evaluation [724/1900]
INFO:tensorflow:Evaluation [725/1900]
INFO:tensorflow:Evaluation [726/1900]
INFO:tensorflow:Evaluation [727/1900]
INFO:tensorflow:Evaluation [728/1900]
INFO:tensorflow:Evaluation [729/1900]
INFO:tensorflow:Evaluation [730/1900]
INFO:tensorflow:Evaluation [731/1900]
INFO:tensorflow:Evaluation [732/1900]
INFO:tensorflow:Evaluation [733/1900]
INFO:tensorflow:Evaluation [734/1900]
INFO:tensorflow:Evaluation [735/1900]
INFO:tensorflow:Evaluation [736/1900]
INFO:tensorflow:Evaluation [737/1900]
INFO:tensorflow:Evaluation [738/1900]
INFO:tensorflow:Evaluation [739/1900]
INFO:tensorflow:Evaluation [740/1900]
INFO:tensorflow:Evaluation [741/1900]
INFO:tensorflow:Evaluation [742/1900]
INFO:tensorflow:Evaluation [743/1900]
INFO:tensorflow:Evaluation [744/1900]
INFO:tensorflow:Evaluation [745/1900]
INFO:tensorflow:Evaluation [746/1900]
INFO:tensorflow:Evaluation [747/1900]
INFO:tensorf

...

INFO:tensorflow:Evaluation [1150/1900]
INFO:tensorflow:Evaluation [1151/1900]
INFO:tensorflow:Evaluation [1152/1900]
INFO:tensorflow:Evaluation [1153/1900]
INFO:tensorflow:Evaluation [1154/1900]
INFO:tensorflow:Evaluation [1155/1900]
INFO:tensorflow:Evaluation [1156/1900]
INFO:tensorflow:Evaluation [1157/1900]
INFO:tensorflow:Evaluation [1158/1900]
INFO:tensorflow:Evaluation [1159/1900]
INFO:tensorflow:Evaluation [1160/1900]
INFO:tensorflow:Evaluation [1161/1900]
INFO:tensorflow:Evaluation [1162/1900]
INFO:tensorflow:Evaluation [1163/1900]
INFO:tensorflow:Evaluation [1164/1900]
INFO:tensorflow:Evaluation [1165/1900]
INFO:tensorflow:Evaluation [1166/1900]
INFO:tensorflow:Evaluation [1167/1900]
INFO:tensorflow:Evaluation [1168/1900]
INFO:tensorflow:Evaluation [1169/1900]
INFO:tensorflow:Evaluation [1170/1900]
INFO:tensorflow:Evaluation [1171/1900]
INFO:tensorflow:Evaluation [1172/1900]
INFO:tensorflow:Evaluation [1173/1900]
INFO:tensorflow:Evaluation [1174/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1361/1900]
INFO:tensorflow:Evaluation [1362/1900]
INFO:tensorflow:Evaluation [1363/1900]
INFO:tensorflow:Evaluation [1364/1900]
INFO:tensorflow:Evaluation [1365/1900]
INFO:tensorflow:Evaluation [1366/1900]
INFO:tensorflow:Evaluation [1367/1900]
INFO:tensorflow:Evaluation [1368/1900]
INFO:tensorflow:Evaluation [1369/1900]
INFO:tensorflow:Evaluation [1370/1900]
INFO:tensorflow:Evaluation [1371/1900]
INFO:tensorflow:Evaluation [1372/1900]
INFO:tensorflow:Evaluation [1373/1900]
INFO:tensorflow:Evaluation [1374/1900]
INFO:tensorflow:Evaluation [1375/1900]
INFO:tensorflow:Evaluation [1376/1900]
INFO:tensorflow:Evaluation [1377/1900]
INFO:tensorflow:Evaluation [1378/1900]
INFO:tensorflow:Evaluation [1379/1900]
INFO:tensorflow:Evaluation [1380/1900]
INFO:tensorflow:Evaluation [1381/1900]
INFO:tensorflow:Evaluation [1382/1900]
INFO:tensorflow:Evaluation [1383/1900]
INFO:tensorflow:Evaluation [1384/1900]
INFO:tensorflow:Evaluation [1385/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1572/1900]
INFO:tensorflow:Evaluation [1573/1900]
INFO:tensorflow:Evaluation [1574/1900]
INFO:tensorflow:Evaluation [1575/1900]
INFO:tensorflow:Evaluation [1576/1900]
INFO:tensorflow:Evaluation [1577/1900]
INFO:tensorflow:Evaluation [1578/1900]
INFO:tensorflow:Evaluation [1579/1900]
INFO:tensorflow:Evaluation [1580/1900]
INFO:tensorflow:Evaluation [1581/1900]
INFO:tensorflow:Evaluation [1582/1900]
INFO:tensorflow:Evaluation [1583/1900]
INFO:tensorflow:Evaluation [1584/1900]
INFO:tensorflow:Evaluation [1585/1900]
INFO:tensorflow:Evaluation [1586/1900]
INFO:tensorflow:Evaluation [1587/1900]
INFO:tensorflow:Evaluation [1588/1900]
INFO:tensorflow:Evaluation [1589/1900]
INFO:tensorflow:Evaluation [1590/1900]
INFO:tensorflow:Evaluation [1591/1900]
INFO:tensorflow:Evaluation [1592/1900]
INFO:tensorflow:Evaluation [1593/1900]
INFO:tensorflow:Evaluation [1594/1900]
INFO:tensorflow:Evaluation [1595/1900]
INFO:tensorflow:Evaluation [1596/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1783/1900]
INFO:tensorflow:Evaluation [1784/1900]
INFO:tensorflow:Evaluation [1785/1900]
INFO:tensorflow:Evaluation [1786/1900]
INFO:tensorflow:Evaluation [1787/1900]
INFO:tensorflow:Evaluation [1788/1900]
INFO:tensorflow:Evaluation [1789/1900]
INFO:tensorflow:Evaluation [1790/1900]
INFO:tensorflow:Evaluation [1791/1900]
INFO:tensorflow:Evaluation [1792/1900]
INFO:tensorflow:Evaluation [1793/1900]
INFO:tensorflow:Evaluation [1794/1900]
INFO:tensorflow:Evaluation [1795/1900]
INFO:tensorflow:Evaluation [1796/1900]
INFO:tensorflow:Evaluation [1797/1900]
INFO:tensorflow:Evaluation [1798/1900]
INFO:tensorflow:Evaluation [1799/1900]
INFO:tensorflow:Evaluation [1800/1900]
INFO:tensorflow:Evaluation [1801/1900]
INFO:tensorflow:Evaluation [1802/1900]
INFO:tensorflow:Evaluation [1803/1900]
INFO:tensorflow:Evaluation [1804/1900]
INFO:tensorflow:Evaluation [1805/1900]
INFO:tensorflow:Evaluation [1806/1900]
INFO:tensorflow:Evaluation [1807/1900]
INFO:tensorflow:Evaluatio

Test Accuracy by Scikit-learn:  0.809473684211
CPU times: user 9min 3s, sys: 50 s, total: 9min 53s
Wall time: 1min 45s


###### CNN classifier(gensim + text8)

In [69]:
%%time

import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

sess = tf.InteractiveSession()

COL_OUTCOME = 'class'
COL_FEATURE = [col for col in list(df['train'].columns) if col != COL_OUTCOME]

# cls2num = {cls:ind for (ind, cls) in enumerate(df['train']['class'].unique())}

count_feature = len(COL_FEATURE)
count_class = len(df['train']['class'].unique())

x = tf.placeholder(tf.float32, shape=[None, 784], name='x')
y_ = tf.placeholder(tf.float32, shape=[None, count_class], name='y_')

W = tf.Variable(tf.zeros([count_feature, count_class]))
b = tf.Variable(tf.zeros([count_class]))
y = tf.matmul(x, W) + b

# cross_entropy = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=y_, logits=y))

def weight_variable(shape):
    initial = tf.truncated_normal(shape, stddev=0.1)
    return tf.Variable(initial)

def bias_variable(shape):
    initial = tf.constant(0.1, shape=shape)
    return tf.Variable(initial)

def conv2d(x, W):
    return tf.nn.conv2d(x, W, strides=[1, 1, 1, 1], padding='SAME')

def max_pool_2x2(x):
    return tf.nn.max_pool(x, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')

W_conv1 = weight_variable([5, 5, 1, 32])
b_conv1 = bias_variable([32])
x_text = tf.reshape(x, [-1, 28, 28, 1])
h_conv1 = tf.nn.relu(conv2d(x_text, W_conv1) + b_conv1)
h_pool1 = max_pool_2x2(h_conv1)

W_conv2 = weight_variable([5, 5, 32, 64])
b_conv2 = bias_variable([64])
h_conv2 = tf.nn.relu(conv2d(h_pool1, W_conv2) + b_conv2)
h_pool2 = max_pool_2x2(h_conv2)

W_fc1 = weight_variable([7 * 7 * 64, 1024])
b_fc1 = bias_variable([1024])

h_pool2_flat = tf.reshape(h_pool2, [-1, 7 * 7 * 64])
h_fc1 = tf.nn.relu(tf.matmul(h_pool2_flat, W_fc1) + b_fc1)

keep_prob = tf.placeholder(tf.float32, name='keep_prob')
h_fc1_drop = tf.nn.dropout(h_fc1, keep_prob)

W_fc2 = weight_variable([1024, count_class])
b_fc2 = bias_variable([count_class])

y_conv = tf.matmul(h_fc1_drop, W_fc2) + b_fc2

print("CNN initialization finished")

CNN initialization finished
CPU times: user 36 ms, sys: 0 ns, total: 36 ms
Wall time: 36.7 ms


In [70]:
%%time

### Start to traini and evaluate the model

cross_entropy = tf.reduce_mean(
    tf.nn.softmax_cross_entropy_with_logits(labels=y_, logits=y_conv))
train_step = tf.train.AdamOptimizer(1e-4).minimize(cross_entropy)
correct_prediction = tf.equal(tf.argmax(y_conv, 1), tf.argmax(y_, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

sess.run(tf.global_variables_initializer())

x_input = df_new['train']['x']
x_input = [np.array([
            np.float32(x_input.iloc[i].values)
        ])
    for i in range(x_input.shape[0])]
y_input = df_new['train']['y']
y_input = [np.array([
            np.float32(y_input.iloc[i].values)
        ])
    for i in range(y_input.shape[0])]
# y_input = [np.array([y_input.iloc[i].values]) for i in range(y_input.shape[0])]

# not use random input

for i in range(df['train'].shape[0] - 50):
    if 0 == i % 100:
        train_accuracy = []
        for j in range(50):
            train_accuracy.append(accuracy.eval(feed_dict={
                    keep_prob: 1,
                    x:  np.array([elem[0] for elem in x_input[i+j:i+j+50]]),#x_input.iloc[i+j].values, #
                    y_: np.array([elem[0] for elem in y_input[i+j:i+j+50]])#y_input.iloc[i+j].values #
                })
            )
        print("step {}, training accuracy {}".format(i, np.mean(train_accuracy)))
    train_step.run(feed_dict={
        keep_prob: 0.5,
        x:  np.array([elem[0] for elem in x_input[i:i+50]]),#x_input.iloc[i].values, #
        y_: np.array([elem[0] for elem in y_input[i:i+50]])#y_input.iloc[i].values#
    })

print("CNN training finished")

step 0, training accuracy 0.211600005627
step 100, training accuracy 0.321599990129
step 200, training accuracy 0.512800037861
step 300, training accuracy 0.61879992485
step 400, training accuracy 0.57279998064
step 500, training accuracy 0.709200084209
step 600, training accuracy 0.688800036907
step 700, training accuracy 0.630800008774
step 800, training accuracy 0.652400076389
step 900, training accuracy 0.734400093555
step 1000, training accuracy 0.644799947739
step 1100, training accuracy 0.745999932289
step 1200, training accuracy 0.767199933529
step 1300, training accuracy 0.762399971485
step 1400, training accuracy 0.737200081348
step 1500, training accuracy 0.761199951172
step 1600, training accuracy 0.827199995518
step 1700, training accuracy 0.82959997654
step 1800, training accuracy 0.682000100613
step 1900, training accuracy 0.841599881649
step 2000, training accuracy 0.853199899197
step 2100, training accuracy 0.77480006218
step 2200, training accuracy 0.798800051212
step

In [71]:
%%time

# Evaluate

x_input = df_new['test']['x']#df_new['test']['x']
x_input = [np.array([
            np.float32(x_input.iloc[i].values)
        ])
    for i in range(x_input.shape[0])]
y_input = df_new['test']['y']#df_new['test']['y']
y_input = [np.array([
            np.float32(y_input.iloc[i].values)
        ])
    for i in range(y_input.shape[0])]

for i in range(df['test'].shape[0] - 50):
    if 0 == i % 100:
        train_accuracy = []
        for j in range(50):
            train_accuracy.append(accuracy.eval(feed_dict={
                    keep_prob: 1,
                    x:  np.array([elem[0] for elem in x_input[i+j:i+j+50]]),#x_input.iloc[i+j].values, #
                    y_: np.array([elem[0] for elem in y_input[i+j:i+j+50]])#y_input.iloc[i+j].values #
                })
            )
        print("step {}, testing accuracy {}".format(i, np.mean(train_accuracy)))

        
print("CNN testing finished")

step 0, testing accuracy 0.712000131607
step 100, testing accuracy 0.715600073338
step 200, testing accuracy 0.726800024509
step 300, testing accuracy 0.857200026512
step 400, testing accuracy 0.729999899864
step 500, testing accuracy 0.82439994812
step 600, testing accuracy 0.726400017738
step 700, testing accuracy 0.704400002956
step 800, testing accuracy 0.795599997044
step 900, testing accuracy 0.645599961281
step 1000, testing accuracy 0.723200082779
step 1100, testing accuracy 0.737999975681
step 1200, testing accuracy 0.807200074196
step 1300, testing accuracy 0.759599983692
step 1400, testing accuracy 0.709999978542
step 1500, testing accuracy 0.768800020218
step 1600, testing accuracy 0.777999937534
step 1700, testing accuracy 0.814000070095
step 1800, testing accuracy 0.771599888802
CNN testing finished
CPU times: user 2min 40s, sys: 10.1 s, total: 2min 51s
Wall time: 26 s


##### 3.2.1.2 只用待学习语料建模

In [4]:
embedFrom = 'corpus'

In [5]:
%%time

# collect sentences from raw data
sentences = {}
pathtmp = {}
pathtmp['root'] = os.path.join(paths['dir.dataroot'], 'trialdata')
for tpart in ['train', 'test']:
    pathtmp[tpart] = os.path.join(pathtmp['root'], tpart)
    sentences[tpart] = []
    folderList = os.listdir(pathtmp[tpart])
    for folder in folderList:
        fileList = os.listdir(os.path.join(pathtmp[tpart], folder))
        for eachf in fileList:
            fpathtmp = os.path.join(pathtmp[tpart], folder, eachf)
            with open(fpathtmp, 'r') as f:
                sentences[tpart].append(f.read())
      #save sentences in file
        sentencePath = os.path.join(pathtmp['root'], 'sentences-{}'.format(tpart))
        with open(sentencePath, 'w') as f:
            for sentence in sentences[tpart]:
                f.write(sentence)
                f.write('\n')

pathtmp = os.path.join(pathtmp['root'], 'sentences-train')
sentences = []
with open(pathtmp, 'r') as f:
    buff = f.read()
    sentencesBuffer = buff.split('\n')
    sentences = [stcbuffer.split() for stcbuffer in sentencesBuffer]

print('get sentences from training corpus successfully')
print('example:')
print(sentences[random.randrange(len(sentences))])

get sentences from training corpus successfully
example:
['from', 'vlasis', 'cybernet', 'cse', 'fau', 'edu', 'vlasis', 'theodore', 'subject', 're', 'warning', 'please', 'read', 'organization', 'cybernet', 'bbs', 'boca', 'raton', 'florida', 'lines', 'two', 'zero', 'neilson', 'seoul', 'mpr', 'ca', 'robert', 'neilson', 'writes', 'sorry', 'for', 'the', 'zero', 'auto', 'content', 'but', 'that', 'is', 'why', 'low', 'abiding', 'citizens', 'should', 'have', 'the', 'power', 'to', 'protect', 'themselve', 'and', 'their', 'property', 'using', 'deadly', 'force', 'if', 'necessary', 'anywhere', 'a', 'threat', 'is', 'imminent', 'steve', 'heracleous', 'you', 'do', 'have', 'the', 'power', 'steve', 'you', 'can', 'do', 'it', 'why', 'don', 't', 'you', 'why', 'don', 't', 'you', 'go', 'shoot', 'some', 'kids', 'who', 'are', 'tossing', 'rocks', 'onto', 'cars', 'make', 'sure', 'you', 'do', 'a', 'good', 'job', 'though', 'don', 't', 'miss', 'cause', 'like', 'they', 'have', 'big', 'rocks', 'and', 'take', 'it', 'fr

In [87]:
%%time

vecsize = 784
model = gensim.models.word2vec.Word2Vec(iter=15, size=vecsize, sg=1, window=5, workers=12)
print("Model created.")

Model created.
CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 238 µs


In [88]:
%%time
   
trimmer = lambda word, count, min_count: gensim.utils.RULE_DISCARD if word in stopwords else gensim.utils.RULE_KEEP

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 6.91 µs


In [89]:
%%time

model.build_vocab(sentences=sentences, trim_rule=trimmer)

print("Vocabulary creation finished.")

Vocabulary creation finished.
CPU times: user 5.72 s, sys: 20 ms, total: 5.74 s
Wall time: 5.64 s


In [90]:
%%time

model.train(sentences=sentences)

print('Training finished.')

Training finished.
CPU times: user 3min 27s, sys: 56 ms, total: 3min 27s
Wall time: 26.8 s


In [91]:
%%time

# save model

calander = datetime.date.today().timetuple()

modelpath = os.path.join(
    paths['dir.{}.{}'.format(modelFrom, embedFrom)],
    '{}.{}.{}{}{}'.format(modelFrom, embedFrom, calander.tm_year, calander.tm_mon, calander.tm_mday)
)
model.save(modelpath)

print("save model finished")

save model finished
CPU times: user 8 ms, sys: 4 ms, total: 12 ms
Wall time: 12.4 ms


In [92]:
%%time

# Step 2: read data and save it in data['vec.train'] 和 data['vec.test']

data = {}
data['vec.train'] = {'w2v.mean':[], 'class':[]}
data['vec.test'] = {'w2v.mean':[], 'class':[]}

for tpart in ['train', 'test']:
    dirpath = paths['dir.{}'.format(tpart)]
    for (ind, cls) in enumerate(os.listdir(dirpath)):
        clspath = os.path.join(dirpath, cls)
        files = os.listdir(clspath)
        for f in files:
            fpath = os.path.join(clspath, f)
            with open(fpath, 'r') as readf:
                tokens = [token for token in readf.read().split()] # if token not in stopwords]#readf.read().split()#
                # Word2Vec representation
                # begin
                vec = np.array([0.0 for i in range(vecsize)])
                expectationVal = np.array([0.0 for i in range(vecsize)])
                countvec = 0
                for token in tokens:
                    try:
                        vec += model[token]
                        countvec += 1
                    except:
                        vec += expectationVal
                vec = vec / float(countvec)#float(len(tokens))
                 # end
            data['vec.{}'.format(tpart)]['w2v.mean'].append(vec)
            data['vec.{}'.format(tpart)]['class'].append(cls)

    tmp = data['vec.{}'.format(tpart)]
    ind = (random.sample(range(len(tmp['class'])), 1))[0]
    print("sample(transformed) from {}[{}]:\n[corpus]\n {}\n[class]\n{}".format(
            tpart, ind, tmp['w2v.mean'][ind], tmp['class'][ind]
        )
    )
    print()
    
print("Step 2 Succeed")

sample(transformed) from train[2137]:
[corpus]
 [ -6.92075080e-02  -1.10341109e-02  -1.57756309e-03  -4.38288346e-02
  -2.56870093e-03  -1.91868105e-02   2.59707384e-02  -1.38480009e-02
   4.66735698e-02   1.22320529e-02  -4.48232980e-03   3.01153942e-02
   4.60493026e-03   3.00879649e-02   4.19246667e-02   1.45628062e-02
  -5.77818627e-02   2.03765628e-02   2.11208692e-03   1.31738036e-02
   1.65932280e-03  -1.35084295e-02  -2.44918113e-02  -3.92084046e-02
  -5.48109850e-03  -4.01681491e-03   1.42943723e-02  -2.04842861e-03
   8.92381919e-03  -1.54173397e-02  -1.73201344e-04  -3.68162232e-02
   8.38746933e-03   1.47829359e-02   1.49441627e-03   1.45780508e-02
  -3.15133147e-02  -3.66009132e-02  -1.93746889e-02  -1.80645023e-02
  -6.49417490e-02  -2.29584450e-02  -2.50614714e-02  -1.47653579e-02
  -4.99981898e-04  -5.59790347e-02   2.02353659e-02   1.19156180e-03
  -6.45340259e-04  -6.39465189e-03  -4.33630103e-03   4.03514177e-03
   2.22452323e-02   7.41300533e-03  -7.16117787e-03  -5

sample(transformed) from test[1103]:
[corpus]
 [-0.11811182 -0.03760944  0.00637991 -0.10428453  0.02088733 -0.00743363
  0.00273809  0.00321351  0.07759132  0.02099297  0.06763557  0.07964662
  0.04184821  0.11546032  0.05451436 -0.00761499 -0.09659691  0.01623226
  0.00857963  0.02312686 -0.03373558  0.03801262 -0.01173902 -0.07968408
 -0.01005026 -0.01140222 -0.00076246  0.0052872   0.01264707 -0.04825866
  0.01448141 -0.0767749   0.07888501  0.05307805  0.00290516 -0.0237392
 -0.05275487 -0.0825643  -0.01165215 -0.06120615 -0.10834015 -0.03880486
 -0.02553512 -0.02379313 -0.00265643 -0.01575326  0.02981099 -0.05304489
 -0.03617571 -0.01693243 -0.01640014  0.00522742  0.01684704  0.09463365
  0.02964319  0.01782001  0.07333235  0.00321156  0.02612249 -0.03638247
  0.01153358  0.02508477  0.04155179  0.01252466  0.01814196  0.04597889
 -0.03922394  0.01359904 -0.00491344 -0.00076291  0.02965598 -0.04829625
 -0.03138166 -0.01471911 -0.01941514 -0.01868932  0.00892622 -0.0564291
  0.03

In [93]:
%%time

# Step 3: Save in Pandas.DataFrame
#
# 将 data['matrix.train'] 与 data['matrix.test'] 转换成 Pandas.DataFrame 格式，保存到 df['train'] 和 df['test'] 中（df 为字典格式：String -> DataFrame）

df = {}
csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')
for tpart in ['train', 'test']:
    datadict = {}
    datadict['class'] = data['vec.{}'.format(tpart)]['class']
    datavec = np.array(data['vec.{}'.format(tpart)]['w2v.mean'])
    for col in range(vecsize):
        datadict[col]= datavec[:, col]

    df[tpart] = pd.DataFrame(data=datadict)
    print("See df[{}]".format(tpart))
    display(df[tpart])
    print("\n\n\n")
    # write data in DataFrame into CSV
    csvpath = os.path.join(csvpath_root, '{}-w2v-{}-{}.csv'.format(tpart, embedFrom, modelFrom))
    df[tpart].to_csv(csvpath, columns=df[tpart].columns)
    
print("Step 3 Succeed.")

# 繁琐点：研究如何把 CSR 矩阵中的数据规整好放到 DataFrame 中，并与 Class 一一对应

See df[train]


0         1         2         3         4         5         6  \
0    -0.079730 -0.023649 -0.000637 -0.058202  0.000308 -0.016652  0.023493   
1    -0.056762  0.012930  0.021774 -0.066071 -0.015854 -0.005939  0.023844   
2    -0.041504 -0.028601 -0.020247 -0.063503 -0.017398 -0.028696  0.034888   
3    -0.070549 -0.022650  0.004644 -0.057970 -0.013228 -0.018406  0.027923   
4    -0.051495 -0.002146 -0.001128 -0.039290  0.003812 -0.021420  0.038133   
5    -0.078105  0.016148  0.027750 -0.095598 -0.005802 -0.008280  0.010347   
6    -0.069843 -0.013937 -0.007243 -0.041216 -0.010258 -0.023068  0.035144   
7    -0.065727  0.025335  0.012322 -0.068324  0.001057  0.013478  0.009310   
8    -0.094956  0.002193  0.023108 -0.090306  0.003462 -0.021560  0.012234   
9    -0.062736 -0.001663  0.000600 -0.045071  0.000152 -0.020807  0.039427   
10   -0.075000 -0.003243  0.006936 -0.061991  0.009173  0.001173  0.027918   
11   -0.066858 -0.016447  0.000206 -0.038104 -0.002816 -0.021432  0.030656   
12   -0.081796 -0.031617  0.001943 -0.073743  0.005593 -0.013694  0.039972   
13   -0.064067 -0.003964  0.003893 -0.041869  0.004278  0.011335  0.026413   
14   -0.055768 -0.037181 -0.015094 -0.040463  0.000918 -0.009995  0.034205   
15   -0.058682  0.014572  0.000837 -0.072605 -0.012322  0.015993 -0.007740   
16   -0.082856 -0.011766  0.002488 -0.081816 -0.000820 -0.003508  0.015916   
17   -0.064626  0.022578  0.012173 -0.072060  0.008877 -0.019762 -0.004892   
18   -0.062781 -0.008918 -0.007563 -0.056728 -0.003932 -0.010731  0.042162   
19   -0.068557 -0.030587  0.001662 -0.062009 -0.002339 -0.009119  0.024184   
20   -0.050719 -0.017473 -0.010132 -0.040716 -0.014209 -0.027186  0.043906   
21   -0.070924 -0.014364 -0.012133 -0.042792  0.000860 -0.009407  0.022130   
22   -0.053274 -0.007877 -0.015801 -0.042940  0.007413 -0.020022  0.051772   
23   -0.109520  0.001983  0.013166 -0.142121  0.012509  0.009278 -0.007300   
24   -0.071790 -0.023734 -0.004028 -0.042071 -0.003833 -0.037987  0.022428   
25   -0.062947 -0.004180  0.005168 -0.062454 -0.002855 -0.009146  0.023354   
26   -0.057232 -0.002633  0.013141 -0.055465 -0.001814 -0.015648  0.018301   
27   -0.086129 -0.027497  0.005078 -0.075149 -0.005495 -0.008442  0.035589   
28   -0.038227  0.013916 -0.011001 -0.037258 -0.014237 -0.018170  0.052302   
29   -0.053148 -0.010302  0.006509 -0.061800  0.002964 -0.005645  0.026044   
...        ...       ...       ...       ...       ...       ...       ...   
2825 -0.172301 -0.049578  0.031699 -0.129025  0.012436  0.023200  0.023532   
2826 -0.179349 -0.019614  0.001812 -0.121889  0.023463  0.000710  0.033576   
2827 -0.092268  0.020180 -0.005413 -0.087039 -0.010902  0.013886 -0.008756   
2828 -0.134253 -0.003457  0.001656 -0.155318  0.038540  0.042551 -0.026788   
2829 -0.083648 -0.019074  0.002759 -0.062266  0.008801 -0.020732  0.034446   
2830 -0.100456 -0.013934  0.002840 -0.060821 -0.009928 -0.003715  0.028812   
2831 -0.126726 -0.056341 -0.031205 -0.105847  0.025386  0.004722  0.042362   
2832 -0.103297 -0.040854 -0.021574 -0.074100  0.020766 -0.017267  0.039870   
2833 -0.088236 -0.046393 -0.021163 -0.034572 -0.015255 -0.013010  0.045470   
2834 -0.163035 -0.028219 -0.007305 -0.152433  0.067307  0.065821  0.042915   
2835 -0.097374 -0.026484 -0.007209 -0.053736  0.003916 -0.023404  0.024980   
2836 -0.136137 -0.020048  0.000113 -0.087690  0.020146 -0.008814  0.032598   
2837 -0.112457 -0.017434 -0.006988 -0.079746 -0.007259 -0.013000  0.021383   
2838 -0.101334 -0.013471 -0.006869 -0.060874  0.017857 -0.003002  0.031645   
2839 -0.089431 -0.042641 -0.029406 -0.042955  0.017951 -0.006119  0.026283   
2840 -0.144549 -0.038677  0.014203 -0.094985  0.002414  0.001175  0.009395   
2841 -0.098134  0.001073 -0.024111 -0.113945  0.011640  0.015005  0.045051   
2842 -0.085905 -0.003033  0.028285 -0.109860  0.010555  0.008537  0.006917   
2843 -0.134955 -0.005022  0.008424 -0.096662  0.019514 -0.007956  0.030303   
2844 -0.138116 -0.019692 -0.021774 





See df[test]


0         1         2         3         4         5         6  \
0    -0.062496 -0.003992  0.009274 -0.059166  0.002295 -0.010985  0.022264   
1    -0.087414 -0.038249  0.007048 -0.076555  0.021722 -0.045024  0.028561   
2    -0.061214 -0.011331  0.005822 -0.036661  0.003768 -0.026180  0.026175   
3    -0.072991  0.003276  0.025641 -0.074216  0.004734  0.011358  0.000940   
4    -0.069047 -0.025650 -0.014127 -0.039385 -0.000390 -0.016138  0.033307   
5    -0.053782 -0.001994 -0.000659 -0.049186 -0.004210 -0.010316  0.034825   
6    -0.078397 -0.027214 -0.019220 -0.039719  0.000998 -0.026669  0.037096   
7    -0.054396 -0.024790 -0.005471 -0.054194 -0.001723 -0.003584  0.037532   
8    -0.046941 -0.021817 -0.002797 -0.035273 -0.014086 -0.034321  0.030448   
9    -0.063387 -0.027813 -0.007046 -0.044512 -0.000325 -0.018768  0.028955   
10   -0.041138  0.008599  0.013570 -0.057371 -0.011819 -0.003017  0.020035   
11   -0.069749 -0.027606 -0.008342 -0.063539  0.010063 -0.021807  0.043141   
12   -0.060361 -0.014670 -0.001286 -0.041261 -0.011091 -0.031988  0.038021   
13   -0.044145 -0.008208 -0.006333 -0.048423 -0.006252 -0.016213  0.033317   
14   -0.040785 -0.000608  0.018112 -0.038775 -0.007181 -0.001302  0.035405   
15   -0.079533 -0.037165 -0.001079 -0.032814  0.001412 -0.025352  0.039243   
16   -0.091986 -0.017113  0.000010 -0.058703 -0.001572 -0.026244  0.035176   
17   -0.049567  0.005527  0.011796 -0.061295 -0.014799  0.003317  0.025446   
18   -0.076598 -0.010684  0.013164 -0.067574 -0.004941 -0.010111  0.010310   
19   -0.060220  0.005183  0.018527 -0.051123 -0.009122 -0.009329  0.028574   
20   -0.060314 -0.014567 -0.010008 -0.044317 -0.002593 -0.024683  0.047827   
21   -0.106390 -0.007227  0.001171 -0.090523 -0.005887  0.000035  0.023234   
22   -0.076234 -0.069450 -0.001250 -0.029200  0.029640 -0.044820  0.015897   
23   -0.071834 -0.014305 -0.005397 -0.057064  0.005394 -0.008789  0.035541   
24   -0.078233 -0.020596 -0.018912 -0.067140 -0.007225 -0.001687  0.035987   
25   -0.035283  0.028081  0.039778 -0.102394  0.001273  0.015324  0.001790   
26   -0.072582 -0.033157  0.004409 -0.073125  0.001051 -0.013961  0.027620   
27   -0.093942  0.006394  0.018851 -0.103956 -0.021772  0.019870 -0.013408   
28   -0.062215 -0.028299 -0.014100 -0.022588 -0.001843 -0.028799  0.024221   
29   -0.061538 -0.008205  0.032022 -0.101335 -0.006014  0.033769  0.022387   
...        ...       ...       ...       ...       ...       ...       ...   
1870 -0.111420 -0.028490 -0.032832 -0.076901  0.015984 -0.013233  0.012503   
1871 -0.109326 -0.042393 -0.011757 -0.055045 -0.010537  0.003395 -0.025934   
1872 -0.120235 -0.037582  0.010485 -0.068248  0.021491 -0.019391  0.020768   
1873 -0.111342 -0.004142 -0.008359 -0.079434 -0.001398 -0.007893  0.003493   
1874 -0.090968 -0.004456 -0.019310 -0.055331 -0.002858 -0.025555  0.023701   
1875 -0.106965 -0.068524 -0.015730 -0.039229  0.016090  0.005992  0.015510   
1876 -0.133367 -0.027307  0.015403 -0.103689  0.005762 -0.003156  0.007935   
1877 -0.118754 -0.020609  0.003412 -0.068199 -0.014900 -0.021808  0.019640   
1878 -0.134078 -0.008829  0.015991 -0.103083  0.010748  0.014069  0.010380   
1879 -0.093815 -0.008767 -0.009552 -0.070272 -0.006882  0.001399  0.021086   
1880 -0.122900 -0.018836 -0.000837 -0.052973  0.012074 -0.029872  0.045112   
1881 -0.146335 -0.032060 -0.012954 -0.090645 -0.001915  0.005467  0.026133   
1882 -0.123360  0.010743  0.026553 -0.141256  0.009481  0.022091 -0.008485   
1883 -0.121282 -0.000974 -0.004984 -0.130949  0.010903  0.012504 -0.022240   
1884 -0.070621 -0.011602 -0.015114 -0.049116 -0.023735 -0.017380  0.003815   
1885 -0.129499 -0.018507 -0.018618 -0.080980 -0.008071 -0.011148 -0.000458   
1886 -0.109524 -0.040247 -0.005071 -0.068145  0.021773 -0.026360  0.049168   
1887 -0.126285  0.007606 -0.009337 -0.116779  0.008242  0.016358  0.015593   
1888 -0.106141  0.010537  0.027132 -0.093220 -0.011282 -0.011261  0.002446   
1889 -0.085233 -0.027378  0.003628 





Step 3 Succeed.
CPU times: user 2.12 s, sys: 32 ms, total: 2.16 s
Wall time: 2.16 s


In [94]:
# if wanna read data from CSV file

df = {}

for tpart in ['train', 'test']:
    csvpath = os.path.join(
        csvpath_root, '{}-w2v-{}-{}.csv'.format(
            tpart, embedFrom, modelFrom
        )
    )
    if os.path.exists(csvpath):
        df[tpart] = pd.DataFrame.from_csv(csvpath)
        df[tpart] = df[tpart].sample(frac=1)
        df[tpart].reset_index(drop=True, inplace=True)
        print("read {} successfully".format(tpart))
        display(df[tpart])
        print('\n\n\n')

read train successfully


0         1         2         3         4         5         6  \
0    -0.041930 -0.037320 -0.013703 -0.031316  0.000647 -0.041839  0.020111   
1    -0.053875 -0.037723 -0.001289 -0.044911 -0.009387 -0.031085  0.022400   
2    -0.082996 -0.006368  0.012487 -0.101907  0.026058 -0.006897  0.030774   
3    -0.079253 -0.038878 -0.018226 -0.040129  0.012973 -0.007393  0.042378   
4    -0.098658 -0.062071 -0.013294 -0.096206  0.023424 -0.006853  0.051590   
5    -0.133948 -0.026668  0.026274 -0.126822  0.013906 -0.018019  0.007832   
6    -0.125721 -0.017746  0.000925 -0.110393  0.008402  0.008770  0.000420   
7    -0.046582 -0.008309 -0.013047 -0.034686 -0.013737 -0.023121  0.038858   
8    -0.104960 -0.037653  0.011340 -0.054826  0.034294 -0.034874  0.031261   
9    -0.141489 -0.066759  0.001601 -0.105917  0.021009  0.006697  0.014165   
10   -0.068209 -0.005272  0.011967 -0.044596 -0.010373 -0.024364  0.033177   
11   -0.060647 -0.023252  0.000609 -0.045365 -0.004904 -0.030581  0.023112   
12   -0.179451 -0.023478 -0.014902 -0.143163  0.029067  0.018874  0.047300   
13   -0.049789 -0.022443 -0.013456 -0.027207 -0.010807 -0.025030  0.033284   
14   -0.054669 -0.025944 -0.006784 -0.031775  0.001319 -0.008839  0.046608   
15   -0.127173 -0.029647 -0.015626 -0.127873 -0.023972  0.022964 -0.046710   
16   -0.124555 -0.009180  0.029609 -0.125635  0.020449  0.017418  0.015447   
17   -0.107722 -0.034189 -0.005810 -0.067848  0.024561 -0.024971  0.037353   
18   -0.060201 -0.050627 -0.014177 -0.060132  0.020792 -0.004117 -0.002219   
19   -0.073471 -0.007033  0.001380 -0.038777 -0.014336 -0.018386  0.005035   
20   -0.069265 -0.023677 -0.000320 -0.047642  0.008696 -0.032641  0.042892   
21   -0.082434 -0.001372  0.030760 -0.087800 -0.013737 -0.005428  0.007451   
22   -0.055768 -0.037181 -0.015094 -0.040463  0.000918 -0.009995  0.034205   
23   -0.111985 -0.063346 -0.014643 -0.080861  0.022370 -0.035420  0.032856   
24   -0.100260 -0.047241 -0.002659 -0.082789  0.000412 -0.010155  0.027211   
25   -0.074399 -0.004171  0.014993 -0.096964  0.010416 -0.020674 -0.002048   
26   -0.089084  0.000281  0.007712 -0.072274  0.002094 -0.003406  0.007066   
27   -0.073550 -0.122757 -0.070040 -0.054099  0.031197 -0.066585  0.051248   
28   -0.051909 -0.006943  0.027599 -0.060327 -0.018711 -0.027794  0.032517   
29   -0.063337 -0.001914  0.023261 -0.044668 -0.004485 -0.009424 -0.010192   
...        ...       ...       ...       ...       ...       ...       ...   
2825 -0.092330 -0.047529  0.004847 -0.037556  0.009957 -0.048062  0.043821   
2826 -0.102880 -0.008091  0.014107 -0.095269  0.000603 -0.016433  0.017996   
2827 -0.104643 -0.054262 -0.017741 -0.075152  0.018212 -0.022726  0.041290   
2828 -0.138116 -0.019692 -0.021774 -0.106108  0.040900 -0.014281  0.051974   
2829 -0.153288  0.011619  0.040349 -0.154091  0.009571  0.020980  0.039481   
2830 -0.098421 -0.013227  0.022289 -0.116181  0.010394  0.000173 -0.002242   
2831 -0.152854 -0.006984 -0.018631 -0.093017 -0.004931 -0.000802 -0.021394   
2832 -0.052978  0.003496 -0.005553 -0.069468  0.003588  0.001640  0.022779   
2833 -0.067633 -0.029527 -0.003944 -0.041196 -0.001854 -0.019530  0.026754   
2834 -0.096951 -0.062685 -0.007284 -0.080283  0.023998 -0.045069  0.022313   
2835 -0.097983  0.001606  0.030379 -0.136032  0.019479  0.019055  0.005793   
2836 -0.108319 -0.025196  0.007831 -0.085793  0.013026 -0.007158  0.031974   
2837 -0.147596 -0.038557 -0.026392 -0.141016  0.002753  0.048960  0.027963   
2838 -0.107609 -0.001645  0.037455 -0.101118  0.008553 -0.000723  0.008822   
2839 -0.088743 -0.043668 -0.001258 -0.062300  0.014797 -0.026272  0.029965   
2840 -0.122798 -0.014862  0.027252 -0.098911 -0.005131 -0.014400  0.010052   
2841 -0.081135 -0.028138 -0.007032 -0.045618  0.008120 -0.002780  0.017143   
2842 -0.068512 -0.004044  0.001787 -0.055925  0.000314 -0.019885  0.035867   
2843 -0.047826  0.000771  0.011631 -0.044208 -0.010772 -0.011859  0.032550   
2844 -0.050499 -0.027613 -0.039271 





read test successfully


0         1         2         3         4         5         6  \
0    -0.081731 -0.004764 -0.012101 -0.069220 -0.001379 -0.015316  0.022999   
1    -0.097792 -0.017958  0.001700 -0.055562  0.003669 -0.033278  0.033678   
2    -0.116530  0.008329  0.016162 -0.132806  0.017821  0.018096 -0.004903   
3    -0.106671 -0.017298 -0.018855 -0.059363  0.005475 -0.018509  0.002709   
4    -0.065294 -0.013719 -0.000415 -0.044229 -0.001409 -0.023134  0.024657   
5    -0.097884 -0.034024  0.035295 -0.085874  0.019200 -0.004469  0.028108   
6    -0.125321 -0.017656  0.024158 -0.124819  0.014406  0.013520 -0.003531   
7    -0.087147 -0.012321  0.000941 -0.064898  0.009898 -0.007535  0.034204   
8    -0.088266  0.009463  0.006250 -0.092894  0.022079  0.011474  0.011496   
9    -0.087879 -0.023612  0.004497 -0.080114  0.024681 -0.007263  0.026019   
10   -0.061355  0.017289  0.028212 -0.070635 -0.003494  0.007862  0.002878   
11   -0.140591 -0.041713 -0.061825 -0.111931  0.010845 -0.008299  0.024843   
12   -0.090322 -0.002824  0.025883 -0.090516 -0.021280  0.021731 -0.004170   
13   -0.079585 -0.001811  0.005228 -0.087890  0.003254  0.009081  0.007639   
14   -0.111142 -0.031968  0.007985 -0.069793 -0.008262 -0.023679  0.007427   
15   -0.078008  0.002144  0.008835 -0.058259  0.004259 -0.013138  0.022905   
16   -0.060832 -0.033166 -0.000767 -0.038270 -0.003277 -0.030149  0.033979   
17   -0.055807 -0.003073 -0.003401 -0.041041 -0.010604 -0.011118  0.034298   
18   -0.085232 -0.061125  0.020974 -0.128905  0.019596 -0.013998  0.022557   
19   -0.099541  0.019306  0.018578 -0.081871 -0.006483 -0.000248  0.013516   
20   -0.074759 -0.034709 -0.003455 -0.063391  0.010483 -0.016765  0.031985   
21   -0.061723 -0.034245 -0.019492 -0.030626 -0.008071 -0.031578  0.024744   
22   -0.077316 -0.022752  0.007668 -0.069866 -0.016459 -0.024388  0.026934   
23   -0.172010  0.038545  0.073909 -0.220823  0.025814  0.048593 -0.033384   
24   -0.122148 -0.013791  0.025205 -0.114288  0.034377  0.022322 -0.001449   
25   -0.086529 -0.000226 -0.014119 -0.042479 -0.010498 -0.011970  0.015455   
26   -0.090316  0.005686  0.007555 -0.126344  0.012943  0.002945  0.019916   
27   -0.045735 -0.005720 -0.005844 -0.041431  0.000046 -0.011795  0.033051   
28   -0.075430 -0.028680  0.003624 -0.056230  0.005125 -0.019621  0.043953   
29   -0.118220 -0.022428  0.024925 -0.075574  0.012062 -0.004639  0.017477   
...        ...       ...       ...       ...       ...       ...       ...   
1870 -0.079383 -0.031466 -0.004902 -0.053493  0.010669 -0.028412  0.035799   
1871 -0.088889 -0.050074 -0.023385 -0.041696  0.012076 -0.027944  0.035693   
1872 -0.094509 -0.007592 -0.001407 -0.101304  0.032826 -0.010278  0.047460   
1873 -0.086564 -0.017218  0.011087 -0.054681 -0.005190 -0.019954  0.020585   
1874 -0.101129 -0.002555 -0.004038 -0.045716 -0.010866  0.007998  0.040727   
1875 -0.067943  0.000358 -0.011544 -0.065977 -0.002111 -0.004718  0.009078   
1876 -0.062957  0.009959  0.014206 -0.065030 -0.005111  0.000100  0.047526   
1877 -0.071110 -0.018530  0.006900 -0.049876  0.007786 -0.006050  0.031677   
1878 -0.051051 -0.020683  0.040884 -0.163568  0.014113  0.029873  0.010869   
1879 -0.109241 -0.026279  0.031850 -0.093667  0.006004 -0.006430  0.018915   
1880 -0.115488 -0.017670 -0.006289 -0.071744 -0.000619 -0.026944  0.032480   
1881 -0.109622 -0.039463  0.012770 -0.095392  0.015457 -0.006522  0.020562   
1882 -0.123448  0.000372  0.031185 -0.114740 -0.006394  0.007653 -0.018625   
1883 -0.110907 -0.050412 -0.032092 -0.098823  0.046195  0.016664 -0.001719   
1884 -0.111589 -0.009250  0.019226 -0.087333  0.021716 -0.009729  0.026509   
1885 -0.057424 -0.011885 -0.004421 -0.030042 -0.010919 -0.020113  0.034318   
1886 -0.085359 -0.019300  0.023055 -0.086882 -0.009422  0.000303 -0.022044   
1887 -0.083627 -0.013864  0.010922 -0.068513  0.010943 -0.002813  0.036576   
1888 -0.092584 -0.025786  0.000972 -0.052391  0.006328 -0.013807  0.017053   
1889 -0.139652  0.000782  0.040889 

In [95]:
%%time

# if wanna read data from CSV file

df = {}

for tpart in ['train', 'test']:
    csvpath = os.path.join(
        csvpath_root, '{}-w2v-{}-{}.csv'.format(
            tpart, embedFrom, modelFrom
        )
    )
    if os.path.exists(csvpath):
        df[tpart] = pd.DataFrame.from_csv(csvpath)
        df[tpart] = df[tpart].sample(frac=1)
        df[tpart].reset_index(drop=True, inplace=True)
        print("read {} successfully".format(tpart))
        display(df[tpart])

read train successfully


0         1         2         3         4         5         6  \
0    -0.094903 -0.033396  0.023281 -0.068885  0.012803 -0.020081  0.043820   
1    -0.098500  0.003244  0.054230 -0.109855  0.010125  0.003442 -0.017964   
2    -0.139683 -0.053830 -0.005676 -0.095735  0.025591 -0.004752  0.049037   
3    -0.112694 -0.026646  0.039184 -0.098880  0.024492  0.005924  0.010822   
4    -0.102097  0.016169  0.027686 -0.136797  0.000690  0.017346 -0.021475   
5    -0.070430 -0.021697  0.025177 -0.088297  0.017552 -0.004928 -0.013037   
6    -0.179349 -0.019614  0.001812 -0.121889  0.023463  0.000710  0.033576   
7    -0.127285 -0.005624  0.015655 -0.119179  0.031591  0.046910  0.003071   
8    -0.089965 -0.017877  0.020218 -0.060343  0.010492 -0.026772  0.019693   
9    -0.078160 -0.023529  0.002218 -0.040569 -0.012595 -0.004889  0.015876   
10   -0.087696 -0.012514  0.009142 -0.074572  0.005348 -0.002714  0.035634   
11   -0.060079 -0.028880  0.016397 -0.042920 -0.000494 -0.031732  0.044627   
12   -0.085646 -0.044207 -0.024756 -0.030085 -0.000421 -0.032695  0.030734   
13   -0.077186 -0.026407 -0.005049 -0.044574  0.007952 -0.033566  0.057242   
14   -0.103297 -0.040854 -0.021574 -0.074100  0.020766 -0.017267  0.039870   
15   -0.044056  0.009670 -0.002475 -0.047381 -0.010079 -0.015594  0.018901   
16   -0.064626  0.022578  0.012173 -0.072060  0.008877 -0.019762 -0.004892   
17   -0.149648  0.030503  0.057368 -0.117153 -0.004084  0.018305 -0.013756   
18   -0.087865 -0.015744  0.004565 -0.099775 -0.003943 -0.005646  0.021227   
19   -0.093056 -0.013930  0.011386 -0.087752 -0.004999 -0.009727  0.010410   
20   -0.110389  0.009511  0.033371 -0.139080  0.018873  0.012950  0.005260   
21   -0.123952 -0.065385  0.012733 -0.092334  0.014757 -0.007414  0.028703   
22   -0.108992 -0.005515 -0.002961 -0.099232  0.033173 -0.024127  0.019465   
23   -0.068963 -0.027289  0.002880 -0.054431  0.002284 -0.018883  0.017932   
24   -0.074023 -0.031023  0.002479 -0.053217 -0.000925 -0.025851  0.027845   
25   -0.092982  0.007928  0.041669 -0.099350  0.002856  0.008689 -0.014038   
26   -0.104811 -0.000583  0.036369 -0.093764  0.002496 -0.005433  0.018385   
27   -0.123008 -0.084937 -0.000366 -0.120315  0.034129 -0.009971  0.013312   
28   -0.101598  0.001451  0.034833 -0.117372  0.008672  0.008468 -0.002858   
29   -0.093501 -0.003922  0.003313 -0.083976  0.001897 -0.006220  0.007215   
...        ...       ...       ...       ...       ...       ...       ...   
2825 -0.054822  0.005756  0.005950 -0.050932 -0.012330 -0.003933  0.021408   
2826 -0.103251 -0.012574  0.029782 -0.096955 -0.019888  0.013734 -0.011516   
2827 -0.104524 -0.025851 -0.005753 -0.070351  0.001222 -0.023667  0.007113   
2828 -0.114171 -0.028708  0.020272 -0.087235 -0.002018 -0.014419 -0.001932   
2829 -0.075650 -0.118730 -0.056060 -0.053299  0.027177 -0.039511  0.047023   
2830 -0.129452 -0.032085  0.013650 -0.098783  0.025873 -0.000626  0.026366   
2831 -0.136753 -0.026344  0.009871 -0.092530 -0.004843 -0.005618  0.020884   
2832 -0.096138 -0.036106  0.010782 -0.066504  0.003697 -0.029821  0.004596   
2833 -0.081849 -0.039008 -0.011533 -0.055504  0.016368 -0.033987  0.031652   
2834 -0.124555 -0.009180  0.029609 -0.125635  0.020449  0.017418  0.015447   
2835 -0.111588 -0.024904  0.057354 -0.070948  0.004964  0.007370  0.008752   
2836 -0.099569 -0.048786 -0.003498 -0.065964 -0.005407  0.005106  0.015165   
2837 -0.110757 -0.014933  0.011356 -0.075664  0.005868 -0.016228  0.038241   
2838 -0.134601 -0.016664 -0.004067 -0.106566 -0.003013  0.009672  0.015574   
2839 -0.201591 -0.018476  0.038362 -0.164464  0.044344  0.025646 -0.003450   
2840 -0.153907 -0.094621 -0.004425 -0.117687  0.068168  0.023919  0.042099   
2841 -0.096811 -0.028893 -0.023622 -0.061385  0.004664 -0.023587  0.031670   
2842 -0.129411 -0.007795  0.028323 -0.118069  0.009498 -0.012212  0.000986   
2843 -0.115985 -0.006376  0.008187 -0.094868  0.002788 -0.006666  0.017961   
2844 -0.098475  0.008540  0.010642 

read test successfully


0         1         2         3         4         5         6  \
0    -0.117148 -0.021425  0.000099 -0.113312  0.024052  0.004719  0.000188   
1    -0.102021 -0.037374  0.000158 -0.067116  0.005629 -0.028177  0.034275   
2    -0.089513 -0.022315 -0.005322 -0.054825 -0.000899 -0.023198  0.032110   
3    -0.102370 -0.018573  0.005848 -0.061515  0.010681 -0.016677  0.038279   
4    -0.061355  0.017289  0.028212 -0.070635 -0.003494  0.007862  0.002878   
5    -0.069710 -0.007212  0.012999 -0.063925 -0.010738 -0.016342 -0.000341   
6    -0.105284 -0.018029  0.001020 -0.062485 -0.005475 -0.023145  0.021618   
7    -0.090577 -0.045687 -0.028171 -0.042403  0.011147 -0.036393  0.021754   
8    -0.067873 -0.023985 -0.012259 -0.046345  0.004283 -0.012247  0.035525   
9    -0.113428 -0.046355 -0.011424 -0.061250  0.017173 -0.013115  0.021826   
10   -0.097319 -0.010698 -0.016330 -0.077961 -0.003818 -0.010657  0.010647   
11   -0.133814 -0.007933  0.019449 -0.114248  0.014397  0.018487 -0.000558   
12   -0.090030  0.008444  0.018861 -0.079624 -0.008922  0.003551  0.010146   
13   -0.154853 -0.049727 -0.008967 -0.126112  0.047851 -0.008974  0.054274   
14   -0.072759 -0.019514 -0.020210 -0.064285 -0.002563  0.003284  0.006883   
15   -0.133556 -0.022862  0.040346 -0.138881 -0.003679  0.037555  0.005502   
16   -0.117157 -0.031119  0.006494 -0.078744  0.016021 -0.018800  0.022709   
17   -0.100566 -0.012031  0.009607 -0.078735  0.004250 -0.002193  0.018150   
18   -0.065208 -0.016801 -0.013442 -0.026981  0.002609 -0.039045  0.039655   
19   -0.056174 -0.027976 -0.019956 -0.027807  0.000547 -0.013433  0.022333   
20   -0.043831  0.013599  0.007794 -0.045587 -0.012639 -0.002552  0.028404   
21   -0.097282 -0.012309  0.017236 -0.080495 -0.002142 -0.006604  0.022667   
22   -0.101766 -0.037636  0.019740 -0.064940  0.016276 -0.028196  0.012645   
23   -0.040376 -0.007990  0.003060 -0.047786 -0.001680 -0.005756  0.017780   
24   -0.075595 -0.035574  0.002327 -0.060867  0.006883 -0.040289  0.030442   
25   -0.107958 -0.027356  0.016961 -0.094913  0.029610 -0.018555  0.026747   
26   -0.101417 -0.008404  0.047734 -0.100743  0.000214  0.000309 -0.021234   
27   -0.079530 -0.015979  0.012369 -0.083595 -0.001292 -0.009198  0.006065   
28   -0.069281 -0.034745 -0.017171 -0.045984 -0.004094 -0.001080  0.026888   
29   -0.071291  0.010526  0.021444 -0.060936  0.005387 -0.018636  0.006337   
...        ...       ...       ...       ...       ...       ...       ...   
1870 -0.086290 -0.020480 -0.007039 -0.054249  0.007318 -0.033724  0.045048   
1871 -0.113364 -0.035927 -0.000956 -0.034872  0.009311 -0.040820 -0.005329   
1872 -0.062125 -0.011150 -0.009306 -0.043399  0.001954 -0.014730  0.033922   
1873 -0.092562 -0.007460 -0.013806 -0.045986  0.004840 -0.031393  0.002725   
1874 -0.097363 -0.001556  0.025907 -0.081762 -0.012293 -0.015440 -0.005752   
1875 -0.077316 -0.022752  0.007668 -0.069866 -0.016459 -0.024388  0.026934   
1876 -0.132050 -0.042758  0.012529 -0.121136  0.027641  0.022245  0.011332   
1877 -0.083834 -0.011443 -0.000003 -0.059868 -0.000743 -0.016948  0.021128   
1878 -0.122569 -0.018242  0.023278 -0.083057  0.011287 -0.012707  0.021364   
1879 -0.139925  0.000018  0.033816 -0.121712 -0.001782  0.002987 -0.003519   
1880 -0.112684 -0.032925  0.026457 -0.079994  0.027265 -0.024231  0.019640   
1881 -0.128261  0.011907  0.044254 -0.103552  0.005507 -0.000979 -0.001897   
1882 -0.101524 -0.012411  0.017799 -0.089457  0.010984 -0.019038  0.035108   
1883 -0.099667 -0.013779  0.011781 -0.084785  0.031042  0.008742  0.014488   
1884 -0.081610 -0.034732 -0.003122 -0.094235  0.025305 -0.015390  0.019276   
1885 -0.108503 -0.057156  0.000416 -0.124084  0.022886  0.005246  0.003605   
1886 -0.094003 -0.013961  0.002529 -0.071422 -0.000650 -0.007482  0.018748   
1887 -0.076933 -0.020872 -0.018171 -0.053566  0.004527 -0.017377  0.025940   
1888 -0.107997  0.001089  0.014355 -0.113782  0.019196  0.014545  0.018906   
1889 -0.100394 -0.013567  0.018952 

CPU times: user 864 ms, sys: 16 ms, total: 880 ms
Wall time: 877 ms


###### SVM classifier(gensim + corpus)

In [96]:
%%time

# Step 5.1.1: SVM

# if 'TFIDF' == modelChoice:

#train
X_train = df['train'].drop('class', axis=1)
y_train = df['train']['class']
#test
X_test = df['test'].drop('class', axis=1)
y_test_true = df['test']['class']

# else:
#     #train
#     X_train = df_new['train']['x']
#     y_train = df_new['train']['y']
#     #test
#     X_test = df_new['test']['x']
#     y_test_true = df_new['test']['y']

clf = LinearSVC()
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 1.24 s, sys: 4 ms, total: 1.25 s
Wall time: 1.25 s


In [97]:
%%time
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

0.827368421053
0.823115546239
0.827368421053
CPU times: user 20 ms, sys: 0 ns, total: 20 ms
Wall time: 19.7 ms


###### DNN classifier(gensim + corpus)

In [98]:
%%time

# Step 4: One-hot representation for labels

csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')

lb = LabelBinarizer()
lb.fit(df['train']['class'])

df_new = {}
for tpart in ['train', 'test']:
    labels = lb.transform(df[tpart]['class'])
    labelsDf = pd.DataFrame(labels, columns=["class-{}".format(i) for i in range(len(lb.classes_))])
    df_new[tpart] = {}
    df_new[tpart]['y'] = labelsDf
    df_new[tpart]['x'] = df[tpart].drop('class', axis=1)
    df_new[tpart]['all'] = df_new[tpart]['x'].join(df_new[tpart]['y'])
    #save in CSV
    for subpart in ['x', 'y', 'all']:
        csvpath = os.path.join(csvpath_root, "{}-cleanLabels-{}-{}.csv".format(tpart, subpart, modelFrom))
        df_new[tpart][subpart].to_csv(csvpath)
    
print("label cleaning succussfully")

label cleaning succussfully
CPU times: user 3.7 s, sys: 52 ms, total: 3.75 s
Wall time: 3.75 s


In [99]:
%%time

## Step 5 : Train the classifier

COL_OUTCOME = 'class'
COL_FEATURE = [str(col) for col in list(df['train'].columns) if col != COL_OUTCOME]

cls2num = {cls:ind for (ind, cls) in enumerate(df['train']['class'].unique())}

def my_input_fn(dataset):
    # Save dataset in tf format
    feature_cols = {
        str(col): tf.constant(
            df[dataset][str(col)].values
        )
        for col in COL_FEATURE
    }
    labels = tf.constant([cls2num[labelname] for labelname in df[dataset][COL_OUTCOME].values])
    # Returns the feature columns and labels in tf format
    return feature_cols, labels

feature_columns = [tf.contrib.layers.real_valued_column(column_name=str(col)) for col in COL_FEATURE]
clf = tf.contrib.learn.DNNClassifier(
    feature_columns=feature_columns, 
    hidden_units=[512], 
    n_classes=len(df['train']['class'].unique())
)

clf.fit(input_fn=lambda: my_input_fn('train'), steps=2000)

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_num_ps_replicas': 0, '_keep_checkpoint_max': 5, '_tf_random_seed': None, '_task_type': None, '_environment': 'local', '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f1464dfc2d0>, '_tf_config': gpu_options {
  per_process_gpu_memory_fraction: 1.0
}
, '_task_id': 0, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_evaluation_master': '', '_keep_checkpoint_every_n_hours': 10000, '_master': ''}


Instructions for updating:
Please switch to tf.summary.scalar. Note that tf.summary.scalar uses the node name instead of the tag. This means that TensorFlow will automatically de-duplicate summary names based on the scope they are created in. Also, passing a tensor or list of tags to a scalar summary op is no longer supported.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/tmpjRXwq8/model.ckpt.
INFO:tensorflow:loss = 1.60779, step = 1
INFO:tensorflow:global_step/sec: 11.3903
INFO:tensorflow:loss = 1.3959, step = 101
INFO:tensorflow:global_step/sec: 11.525
INFO:tensorflow:loss = 1.21157, step = 201
INFO:tensorflow:global_step/sec: 11.6707
INFO:tensorflow:loss = 1.07089, step = 301
INFO:tensorflow:global_step/sec: 11.8325
INFO:tensorflow:loss = 0.954396, step = 401
INFO:tensorflow:global_step/sec: 11.7476
INFO:tensorflow:loss = 0.863967, step = 501
INFO:tensorflow:global_step/sec: 11.6798
INFO:tensorflow:loss = 0.794398, step = 601
INFO:ten

In [100]:
%%time

## Step 6: Evaluate

accuracy_score = clf.evaluate(input_fn=lambda: my_input_fn('test'), steps=df['test'].shape[0])['accuracy']
print("Test Accuracy by TensorFlow: {}".format(accuracy_score))

X_tensor_test, yt = my_input_fn('test')
tensorPredCls = list(clf.predict(input_fn=lambda: my_input_fn('test')))
num2cls = {v:k for (k, v) in cls2num.items()}
tensorPredClsStr = [num2cls[i] for i in tensorPredCls]
y_test_true = df['test']['class']
print('Test Accuracy by Scikit-learn: ', f1_score(y_test_true, tensorPredClsStr, average='micro'))

Instructions for updating:
Please switch to tf.summary.scalar. Note that tf.summary.scalar uses the node name instead of the tag. This means that TensorFlow will automatically de-duplicate summary names based on the scope they are created in. Also, passing a tensor or list of tags to a scalar summary op is no longer supported.
INFO:tensorflow:Starting evaluation at 2017-05-13-09:41:54
INFO:tensorflow:Evaluation [1/1900]
INFO:tensorflow:Evaluation [2/1900]
INFO:tensorflow:Evaluation [3/1900]
INFO:tensorflow:Evaluation [4/1900]
INFO:tensorflow:Evaluation [5/1900]
INFO:tensorflow:Evaluation [6/1900]
INFO:tensorflow:Evaluation [7/1900]
INFO:tensorflow:Evaluation [8/1900]
INFO:tensorflow:Evaluation [9/1900]
INFO:tensorflow:Evaluation [10/1900]
INFO:tensorflow:Evaluation [11/1900]
INFO:tensorflow:Evaluation [12/1900]
INFO:tensorflow:Evaluation [13/1900]
INFO:tensorflow:Evaluation [14/1900]
INFO:tensorflow:Evaluation [15/1900]
INFO:tensorflow:Evaluation [16/1900]
INFO:tensorflow:Evaluation [1

INFO:tensorflow:Evaluation [73/1900]
INFO:tensorflow:Evaluation [74/1900]
INFO:tensorflow:Evaluation [75/1900]
INFO:tensorflow:Evaluation [76/1900]
INFO:tensorflow:Evaluation [77/1900]
INFO:tensorflow:Evaluation [78/1900]
INFO:tensorflow:Evaluation [79/1900]
INFO:tensorflow:Evaluation [80/1900]
INFO:tensorflow:Evaluation [81/1900]
INFO:tensorflow:Evaluation [82/1900]
INFO:tensorflow:Evaluation [83/1900]
INFO:tensorflow:Evaluation [84/1900]
INFO:tensorflow:Evaluation [85/1900]
INFO:tensorflow:Evaluation [86/1900]
INFO:tensorflow:Evaluation [87/1900]
INFO:tensorflow:Evaluation [88/1900]
INFO:tensorflow:Evaluation [89/1900]
INFO:tensorflow:Evaluation [90/1900]
INFO:tensorflow:Evaluation [91/1900]
INFO:tensorflow:Evaluation [92/1900]
INFO:tensorflow:Evaluation [93/1900]
INFO:tensorflow:Evaluation [94/1900]
INFO:tensorflow:Evaluation [95/1900]
INFO:tensorflow:Evaluation [96/1900]
INFO:tensorflow:Evaluation [97/1900]
INFO:tensorflow:Evaluation [98/1900]
INFO:tensorflow:Evaluation [99/1900]
I

INFO:tensorflow:Evaluation [290/1900]
INFO:tensorflow:Evaluation [291/1900]
INFO:tensorflow:Evaluation [292/1900]
INFO:tensorflow:Evaluation [293/1900]
INFO:tensorflow:Evaluation [294/1900]
INFO:tensorflow:Evaluation [295/1900]
INFO:tensorflow:Evaluation [296/1900]
INFO:tensorflow:Evaluation [297/1900]
INFO:tensorflow:Evaluation [298/1900]
INFO:tensorflow:Evaluation [299/1900]
INFO:tensorflow:Evaluation [300/1900]
INFO:tensorflow:Evaluation [301/1900]
INFO:tensorflow:Evaluation [302/1900]
INFO:tensorflow:Evaluation [303/1900]
INFO:tensorflow:Evaluation [304/1900]
INFO:tensorflow:Evaluation [305/1900]
INFO:tensorflow:Evaluation [306/1900]
INFO:tensorflow:Evaluation [307/1900]
INFO:tensorflow:Evaluation [308/1900]
INFO:tensorflow:Evaluation [309/1900]
INFO:tensorflow:Evaluation [310/1900]
INFO:tensorflow:Evaluation [311/1900]
INFO:tensorflow:Evaluation [312/1900]
INFO:tensorflow:Evaluation [313/1900]
INFO:tensorflow:Evaluation [314/1900]
INFO:tensorflow:Evaluation [315/1900]
INFO:tensorf

INFO:tensorflow:Evaluation [506/1900]
INFO:tensorflow:Evaluation [507/1900]
INFO:tensorflow:Evaluation [508/1900]
INFO:tensorflow:Evaluation [509/1900]
INFO:tensorflow:Evaluation [510/1900]
INFO:tensorflow:Evaluation [511/1900]
INFO:tensorflow:Evaluation [512/1900]
INFO:tensorflow:Evaluation [513/1900]
INFO:tensorflow:Evaluation [514/1900]
INFO:tensorflow:Evaluation [515/1900]
INFO:tensorflow:Evaluation [516/1900]
INFO:tensorflow:Evaluation [517/1900]
INFO:tensorflow:Evaluation [518/1900]
INFO:tensorflow:Evaluation [519/1900]
INFO:tensorflow:Evaluation [520/1900]
INFO:tensorflow:Evaluation [521/1900]
INFO:tensorflow:Evaluation [522/1900]
INFO:tensorflow:Evaluation [523/1900]
INFO:tensorflow:Evaluation [524/1900]
INFO:tensorflow:Evaluation [525/1900]
INFO:tensorflow:Evaluation [526/1900]
INFO:tensorflow:Evaluation [527/1900]
INFO:tensorflow:Evaluation [528/1900]
INFO:tensorflow:Evaluation [529/1900]
INFO:tensorflow:Evaluation [530/1900]
INFO:tensorflow:Evaluation [531/1900]
INFO:tensorf

INFO:tensorflow:Evaluation [722/1900]
INFO:tensorflow:Evaluation [723/1900]
INFO:tensorflow:Evaluation [724/1900]
INFO:tensorflow:Evaluation [725/1900]
INFO:tensorflow:Evaluation [726/1900]
INFO:tensorflow:Evaluation [727/1900]
INFO:tensorflow:Evaluation [728/1900]
INFO:tensorflow:Evaluation [729/1900]
INFO:tensorflow:Evaluation [730/1900]
INFO:tensorflow:Evaluation [731/1900]
INFO:tensorflow:Evaluation [732/1900]
INFO:tensorflow:Evaluation [733/1900]
INFO:tensorflow:Evaluation [734/1900]
INFO:tensorflow:Evaluation [735/1900]
INFO:tensorflow:Evaluation [736/1900]
INFO:tensorflow:Evaluation [737/1900]
INFO:tensorflow:Evaluation [738/1900]
INFO:tensorflow:Evaluation [739/1900]
INFO:tensorflow:Evaluation [740/1900]
INFO:tensorflow:Evaluation [741/1900]
INFO:tensorflow:Evaluation [742/1900]
INFO:tensorflow:Evaluation [743/1900]
INFO:tensorflow:Evaluation [744/1900]
INFO:tensorflow:Evaluation [745/1900]
INFO:tensorflow:Evaluation [746/1900]
INFO:tensorflow:Evaluation [747/1900]
INFO:tensorf

...

INFO:tensorflow:Evaluation [1150/1900]
INFO:tensorflow:Evaluation [1151/1900]
INFO:tensorflow:Evaluation [1152/1900]
INFO:tensorflow:Evaluation [1153/1900]
INFO:tensorflow:Evaluation [1154/1900]
INFO:tensorflow:Evaluation [1155/1900]
INFO:tensorflow:Evaluation [1156/1900]
INFO:tensorflow:Evaluation [1157/1900]
INFO:tensorflow:Evaluation [1158/1900]
INFO:tensorflow:Evaluation [1159/1900]
INFO:tensorflow:Evaluation [1160/1900]
INFO:tensorflow:Evaluation [1161/1900]
INFO:tensorflow:Evaluation [1162/1900]
INFO:tensorflow:Evaluation [1163/1900]
INFO:tensorflow:Evaluation [1164/1900]
INFO:tensorflow:Evaluation [1165/1900]
INFO:tensorflow:Evaluation [1166/1900]
INFO:tensorflow:Evaluation [1167/1900]
INFO:tensorflow:Evaluation [1168/1900]
INFO:tensorflow:Evaluation [1169/1900]
INFO:tensorflow:Evaluation [1170/1900]
INFO:tensorflow:Evaluation [1171/1900]
INFO:tensorflow:Evaluation [1172/1900]
INFO:tensorflow:Evaluation [1173/1900]
INFO:tensorflow:Evaluation [1174/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1361/1900]
INFO:tensorflow:Evaluation [1362/1900]
INFO:tensorflow:Evaluation [1363/1900]
INFO:tensorflow:Evaluation [1364/1900]
INFO:tensorflow:Evaluation [1365/1900]
INFO:tensorflow:Evaluation [1366/1900]
INFO:tensorflow:Evaluation [1367/1900]
INFO:tensorflow:Evaluation [1368/1900]
INFO:tensorflow:Evaluation [1369/1900]
INFO:tensorflow:Evaluation [1370/1900]
INFO:tensorflow:Evaluation [1371/1900]
INFO:tensorflow:Evaluation [1372/1900]
INFO:tensorflow:Evaluation [1373/1900]
INFO:tensorflow:Evaluation [1374/1900]
INFO:tensorflow:Evaluation [1375/1900]
INFO:tensorflow:Evaluation [1376/1900]
INFO:tensorflow:Evaluation [1377/1900]
INFO:tensorflow:Evaluation [1378/1900]
INFO:tensorflow:Evaluation [1379/1900]
INFO:tensorflow:Evaluation [1380/1900]
INFO:tensorflow:Evaluation [1381/1900]
INFO:tensorflow:Evaluation [1382/1900]
INFO:tensorflow:Evaluation [1383/1900]
INFO:tensorflow:Evaluation [1384/1900]
INFO:tensorflow:Evaluation [1385/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1572/1900]
INFO:tensorflow:Evaluation [1573/1900]
INFO:tensorflow:Evaluation [1574/1900]
INFO:tensorflow:Evaluation [1575/1900]
INFO:tensorflow:Evaluation [1576/1900]
INFO:tensorflow:Evaluation [1577/1900]
INFO:tensorflow:Evaluation [1578/1900]
INFO:tensorflow:Evaluation [1579/1900]
INFO:tensorflow:Evaluation [1580/1900]
INFO:tensorflow:Evaluation [1581/1900]
INFO:tensorflow:Evaluation [1582/1900]
INFO:tensorflow:Evaluation [1583/1900]
INFO:tensorflow:Evaluation [1584/1900]
INFO:tensorflow:Evaluation [1585/1900]
INFO:tensorflow:Evaluation [1586/1900]
INFO:tensorflow:Evaluation [1587/1900]
INFO:tensorflow:Evaluation [1588/1900]
INFO:tensorflow:Evaluation [1589/1900]
INFO:tensorflow:Evaluation [1590/1900]
INFO:tensorflow:Evaluation [1591/1900]
INFO:tensorflow:Evaluation [1592/1900]
INFO:tensorflow:Evaluation [1593/1900]
INFO:tensorflow:Evaluation [1594/1900]
INFO:tensorflow:Evaluation [1595/1900]
INFO:tensorflow:Evaluation [1596/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1783/1900]
INFO:tensorflow:Evaluation [1784/1900]
INFO:tensorflow:Evaluation [1785/1900]
INFO:tensorflow:Evaluation [1786/1900]
INFO:tensorflow:Evaluation [1787/1900]
INFO:tensorflow:Evaluation [1788/1900]
INFO:tensorflow:Evaluation [1789/1900]
INFO:tensorflow:Evaluation [1790/1900]
INFO:tensorflow:Evaluation [1791/1900]
INFO:tensorflow:Evaluation [1792/1900]
INFO:tensorflow:Evaluation [1793/1900]
INFO:tensorflow:Evaluation [1794/1900]
INFO:tensorflow:Evaluation [1795/1900]
INFO:tensorflow:Evaluation [1796/1900]
INFO:tensorflow:Evaluation [1797/1900]
INFO:tensorflow:Evaluation [1798/1900]
INFO:tensorflow:Evaluation [1799/1900]
INFO:tensorflow:Evaluation [1800/1900]
INFO:tensorflow:Evaluation [1801/1900]
INFO:tensorflow:Evaluation [1802/1900]
INFO:tensorflow:Evaluation [1803/1900]
INFO:tensorflow:Evaluation [1804/1900]
INFO:tensorflow:Evaluation [1805/1900]
INFO:tensorflow:Evaluation [1806/1900]
INFO:tensorflow:Evaluation [1807/1900]
INFO:tensorflow:Evaluatio

Test Accuracy by Scikit-learn:  0.818421052632
CPU times: user 9min 1s, sys: 50.7 s, total: 9min 51s
Wall time: 1min 45s


###### CNN classifier(gensim + corpus)

In [101]:
%%time

import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

sess = tf.InteractiveSession()

COL_OUTCOME = 'class'
COL_FEATURE = [col for col in list(df['train'].columns) if col != COL_OUTCOME]

# cls2num = {cls:ind for (ind, cls) in enumerate(df['train']['class'].unique())}

count_feature = len(COL_FEATURE)
count_class = len(df['train']['class'].unique())

x = tf.placeholder(tf.float32, shape=[None, 784], name='x')
y_ = tf.placeholder(tf.float32, shape=[None, count_class], name='y_')

W = tf.Variable(tf.zeros([count_feature, count_class]))
b = tf.Variable(tf.zeros([count_class]))
y = tf.matmul(x, W) + b

# cross_entropy = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=y_, logits=y))

def weight_variable(shape):
    initial = tf.truncated_normal(shape, stddev=0.1)
    return tf.Variable(initial)

def bias_variable(shape):
    initial = tf.constant(0.1, shape=shape)
    return tf.Variable(initial)

def conv2d(x, W):
    return tf.nn.conv2d(x, W, strides=[1, 1, 1, 1], padding='SAME')

def max_pool_2x2(x):
    return tf.nn.max_pool(x, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')

W_conv1 = weight_variable([5, 5, 1, 32])
b_conv1 = bias_variable([32])
x_text = tf.reshape(x, [-1, 28, 28, 1])
h_conv1 = tf.nn.relu(conv2d(x_text, W_conv1) + b_conv1)
h_pool1 = max_pool_2x2(h_conv1)

W_conv2 = weight_variable([5, 5, 32, 64])
b_conv2 = bias_variable([64])
h_conv2 = tf.nn.relu(conv2d(h_pool1, W_conv2) + b_conv2)
h_pool2 = max_pool_2x2(h_conv2)

W_fc1 = weight_variable([7 * 7 * 64, 1024])
b_fc1 = bias_variable([1024])

h_pool2_flat = tf.reshape(h_pool2, [-1, 7 * 7 * 64])
h_fc1 = tf.nn.relu(tf.matmul(h_pool2_flat, W_fc1) + b_fc1)

keep_prob = tf.placeholder(tf.float32, name='keep_prob')
h_fc1_drop = tf.nn.dropout(h_fc1, keep_prob)

W_fc2 = weight_variable([1024, count_class])
b_fc2 = bias_variable([count_class])

y_conv = tf.matmul(h_fc1_drop, W_fc2) + b_fc2

print("CNN initialization finished")

CNN initialization finished
CPU times: user 36 ms, sys: 4 ms, total: 40 ms
Wall time: 39 ms


In [102]:
%%time

### Start to traini and evaluate the model

cross_entropy = tf.reduce_mean(
    tf.nn.softmax_cross_entropy_with_logits(labels=y_, logits=y_conv))
train_step = tf.train.AdamOptimizer(1e-4).minimize(cross_entropy)
correct_prediction = tf.equal(tf.argmax(y_conv, 1), tf.argmax(y_, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

sess.run(tf.global_variables_initializer())

x_input = df_new['train']['x']
x_input = [np.array([
            np.float32(x_input.iloc[i].values)
        ])
    for i in range(x_input.shape[0])]
y_input = df_new['train']['y']
y_input = [np.array([
            np.float32(y_input.iloc[i].values)
        ])
    for i in range(y_input.shape[0])]
# y_input = [np.array([y_input.iloc[i].values]) for i in range(y_input.shape[0])]

# not use random input

for i in range(df['train'].shape[0] - 50):
    if 0 == i % 100:
        train_accuracy = []
        for j in range(50):
            train_accuracy.append(accuracy.eval(feed_dict={
                    keep_prob: 1,
                    x:  np.array([elem[0] for elem in x_input[i+j:i+j+50]]),#x_input.iloc[i+j].values, #
                    y_: np.array([elem[0] for elem in y_input[i+j:i+j+50]])#y_input.iloc[i+j].values #
                })
            )
        print("step {}, training accuracy {}".format(i, np.mean(train_accuracy)))
    train_step.run(feed_dict={
        keep_prob: 0.5,
        x:  np.array([elem[0] for elem in x_input[i:i+50]]),#x_input.iloc[i].values, #
        y_: np.array([elem[0] for elem in y_input[i:i+50]])#y_input.iloc[i].values#
    })

print("CNN training finished")

step 0, training accuracy 0.175200000405
step 100, training accuracy 0.474399983883
step 200, training accuracy 0.585599958897
step 300, training accuracy 0.564399957657
step 400, training accuracy 0.557599961758
step 500, training accuracy 0.614799976349
step 600, training accuracy 0.706399977207
step 700, training accuracy 0.64359998703
step 800, training accuracy 0.70759999752
step 900, training accuracy 0.7675999403
step 1000, training accuracy 0.782399892807
step 1100, training accuracy 0.740800023079
step 1200, training accuracy 0.716000080109
step 1300, training accuracy 0.711199998856
step 1400, training accuracy 0.87640017271
step 1500, training accuracy 0.841600060463
step 1600, training accuracy 0.770799994469
step 1700, training accuracy 0.743200004101
step 1800, training accuracy 0.870800018311
step 1900, training accuracy 0.76239991188
step 2000, training accuracy 0.836400151253
step 2100, training accuracy 0.773999929428
step 2200, training accuracy 0.790799915791
step 2

In [103]:
%%time

# Evaluate

x_input = df_new['test']['x']#df_new['test']['x']
x_input = [np.array([
            np.float32(x_input.iloc[i].values)
        ])
    for i in range(x_input.shape[0])]
y_input = df_new['test']['y']#df_new['test']['y']
y_input = [np.array([
            np.float32(y_input.iloc[i].values)
        ])
    for i in range(y_input.shape[0])]

for i in range(df['test'].shape[0] - 50):
    if 0 == i % 100:
        train_accuracy = []
        for j in range(50):
            train_accuracy.append(accuracy.eval(feed_dict={
                    keep_prob: 1,
                    x:  np.array([elem[0] for elem in x_input[i+j:i+j+50]]),#x_input.iloc[i+j].values, #
                    y_: np.array([elem[0] for elem in y_input[i+j:i+j+50]])#y_input.iloc[i+j].values #
                })
            )
        print("step {}, testing accuracy {}".format(i, np.mean(train_accuracy)))

        
print("CNN testing finished")

step 0, testing accuracy 0.698399960995
step 100, testing accuracy 0.814400017262
step 200, testing accuracy 0.720800101757
step 300, testing accuracy 0.780399918556
step 400, testing accuracy 0.846400022507
step 500, testing accuracy 0.793200075626
step 600, testing accuracy 0.743200063705
step 700, testing accuracy 0.833999931812
step 800, testing accuracy 0.732000052929
step 900, testing accuracy 0.76919990778
step 1000, testing accuracy 0.717200040817
step 1100, testing accuracy 0.86000007391
step 1200, testing accuracy 0.784800112247
step 1300, testing accuracy 0.80119997263
step 1400, testing accuracy 0.761600017548
step 1500, testing accuracy 0.79239988327
step 1600, testing accuracy 0.782799899578
step 1700, testing accuracy 0.815999925137
step 1800, testing accuracy 0.792400062084
CNN testing finished
CPU times: user 2min 43s, sys: 10 s, total: 2min 53s
Wall time: 27.1 s


#### 3.2.2 TensorFlow 训练

In [6]:
import tensorflow as tf

modelFrom = 'TensorFlow'

In [7]:
%%time

import sys
sys.path.append(os.path.abspath('../'))

from modules.embedding.w2v_opt_full_01 import *

CPU times: user 16 ms, sys: 0 ns, total: 16 ms
Wall time: 35.1 ms


##### 3.2.1.1 基于 text8 建模

In [6]:
%%time

embedFrom = 'text8'

FLAGS.train_data = os.path.join(paths['dir.dataroot'], 'trialdata', embedFrom) #embedFrom #
FLAGS.eval_data = os.path.join(paths['dir.dataroot'], 'trialdata', 'questions-words.txt') #'questions-words.txt' #
FLAGS.save_path = paths['dir.{}.{}'.format(modelFrom, embedFrom)]
FLAGS.epochs_to_train = 15
FLAGS.embedding_size = vecsize

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 121 µs


In [7]:
%%time

!cat ../modules/embedding/w2v_opt_full_02.py

import tensorflow as tf

session = tf.InteractiveSession()
"""Train a word2vec model."""
if not FLAGS.train_data or not FLAGS.eval_data or not FLAGS.save_path:
  print("--train_data --eval_data and --save_path must be specified.")
  sys.exit(1)
opts = Options()
#with tf.Graph().as_default() as session:
with tf.device("/cpu:0"):
  model = Word2Vec(opts, session)
  model.read_analogies() # Read analogy questions
for _ in xrange(opts.epochs_to_train):
  model.train()  # Process one epoch
  model.eval()  # Eval analogies.
# Perform a final save.
model.saver.save(session, os.path.join(opts.save_path, "model.ckpt"),
                 global_step=model.global_step)
if FLAGS.interactive:
  # E.g.,
  # [0]: model.analogy(b'france', b'paris', b'russia')
  # [1]: model.nearby([b'proton', b'elephant', b'maxwell'])
  _start_shell(locals())

CPU times: user 4 ms, sys: 4 ms, total: 8 ms
Wall time: 110 ms


In [8]:
%%time

session = tf.InteractiveSession()
"""Train a word2vec model."""
if not FLAGS.train_data or not FLAGS.eval_data or not FLAGS.save_path:
    print("--train_data --eval_data and --save_path must be specified.")
    sys.exit(1)
opts = Options()
#with tf.Graph().as_default() as session:
with tf.device("/cpu:0"):
    model = Word2Vec(opts, session)
    model.read_analogies() # Read analogy questions
for _ in xrange(opts.epochs_to_train):
    model.train()  # Process one epoch
    model.eval()  # Eval analogies.
# Perform a final save.
model.saver.save(session, os.path.join(opts.save_path, "model-{}.ckpt".format(embedFrom)),
                 global_step=model.global_step)
if FLAGS.interactive:
    # E.g.,
    # [0]: model.analogy(b'france', b'paris', b'russia')
    # [1]: model.nearby([b'proton', b'elephant', b'maxwell'])
    _start_shell(locals())

Data file:  /home/sushangjun/gits/Udacity/MLND/capstone.now/proposal/new/notebooks/../data/trialdata/text8
Vocab size:  71290  + UNK
Words per epoch:  17005207
Initialization:  [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 ..., 
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
Eval analogy file:  /home/sushangjun/gits/Udacity/MLND/capstone.now/proposal/new/notebooks/../data/trialdata/questions-words.txt
Questions:  17827
Skipped:  1717
Epoch    1 Step   150890: lr = 0.024 words/sec =      401
Eval 1329/17827 accuracy =  7.5%
Epoch    2 Step   301789: lr = 0.023 words/sec =     3514
Eval 1551/17827 accuracy =  8.7%
Epoch    3 Step   452711: lr = 0.021 words/sec =     2312
Eval 1711/17827 accuracy =  9.6%
Epoch    4 Step   603641: lr = 0.020 words/sec =    11345
Eval 1705/17827 accuracy =  9.6%
Epoch    5 Step   754523: lr = 0.019 words/sec =    12016
Eval 1938/17827 accuracy = 10.9%
Epoch 

In [12]:
tmpemb = model._w_out.eval()

In [9]:
# from scipy.spatial.distance import cosine

# # tmma=model._w_in.eval()
# # tmma
tmpemb = model._w_out.eval()
# # print(len(tmpemb[model._word2id['slow']]))
# # print(tmpemb[model._word2id['slowly']])
# print(cosine(tmpemb[model._word2id['slow']], tmpemb[model._word2id['slowly']]))
# # print(cosine(tmpemb[model._word2id['man']], tmpemb[model._word2id['men']]))
# # print(cosine(tmpemb[model._word2id['woman']], tmpemb[model._word2id['women']]))
# # print(cosine(tmpemb[model._word2id['woman']], tmpemb[model._word2id['woman']]))
# # print(tmpemb[model._word2id['UNK']])
# print(cosine([1,1], [1.1, 1.3]))

In [13]:
%%time

# Step 1: preprocess the data

# import stoplist
stopwords = ""

pathtemp_TFIDF = os.path.join(paths['dir.dataroot'], 'stoplist-baseTFIDF.txt')
with open(pathtemp_TFIDF, 'r') as stoplistfile:
    stopwords = stoplistfile.read()
stopwords = stopwords.split()

pathtemp_web = os.path.join(paths['dir.dataroot'], 'stoplist-web.txt')
with open(pathtemp_web, 'r') as stoplistfile2:
    stopwords2 = stoplistfile2.read()
    stopwords2 = stopwords2.split('\n')
    stopwords = set(stopwords)
    stopwords = list(stopwords.union(set(stopwords)))
    
print("Read stop words successfully.")

Read stop words successfully.
CPU times: user 8 ms, sys: 0 ns, total: 8 ms
Wall time: 8.73 ms


In [14]:
%%time

# Step 2: read data and save it in data['vec.train'] 和 data['vec.test']

data = {}
data['vec.train'] = {'w2v.mean':[], 'class':[]}
data['vec.test'] = {'w2v.mean':[], 'class':[]}

for tpart in ['train', 'test']:
    dirpath = paths['dir.{}'.format(tpart)]
    for (ind, cls) in enumerate(os.listdir(dirpath)):
        clspath = os.path.join(dirpath, cls)
        files = os.listdir(clspath)
        for f in files:
            fpath = os.path.join(clspath, f)
            with open(fpath, 'r') as readf:
                tokens = [token for token in readf.read().split() if token not in stopwords]#readf.read().split()#
                # Word2Vec representation
                # begin
                vec = np.array([0.0 for i in range(vecsize)])
                expectationVal = np.array([0.0 for i in range(vecsize)])
                countvec = 0
                for token in tokens:
                    try:
                        vec += tmpemb[model._word2id[token]] #model[token]
                        countvec += 1
                    except:
                        vec += tmpemb[model._word2id['UNK']]
                vec = vec / float(countvec)
                 # end
            data['vec.{}'.format(tpart)]['w2v.mean'].append(vec)
            data['vec.{}'.format(tpart)]['class'].append(cls)

    tmp = data['vec.{}'.format(tpart)]
    ind = (random.sample(range(len(tmp['class'])), 1))[0]
    print("sample(transformed) from {}[{}]:\n[corpus]\n {}\n[class]\n{}".format(tpart, ind, tmp['w2v.mean'][ind], tmp['class'][ind]))
    print()
    
print("Step 2 Succeed")

sample(transformed) from train[2661]:
[corpus]
 [  8.46570395e-02   7.36237078e-02   1.32261657e-01   2.42277544e-02
   9.60568581e-02   3.41597420e-02   5.52674287e-02   5.79880733e-02
   1.70605378e-02   6.43584932e-02   1.05966809e-02   1.43605644e-01
   1.01392743e-01   5.19162987e-02   8.23761015e-03  -2.49761805e-02
  -8.45924780e-02  -1.26947688e-01   5.07993037e-02   7.71085503e-02
   1.15967649e-01   8.66751594e-02  -6.66078503e-02   1.36506479e-02
   2.37388999e-02  -1.30873696e-02   9.68263756e-02  -3.50473743e-02
   3.20062190e-02   2.02545940e-02   2.20419404e-02   1.59319619e-03
  -6.85059609e-02  -9.00481725e-02  -6.20998098e-02  -5.15684579e-02
  -3.17938032e-02  -9.55823207e-02   1.70515235e-03   1.44638132e-02
   6.13906177e-02   7.05932208e-02  -2.51527901e-02  -2.81220766e-02
  -1.09073998e-01  -5.16547825e-02   9.56733968e-02   1.10167416e-02
   2.32058995e-01  -6.51337253e-03  -9.23938254e-02  -1.17940848e-01
  -7.90318274e-03   8.19548033e-03   1.37587986e-01  -2

sample(transformed) from test[651]:
[corpus]
 [  9.74833070e-02   4.23970169e-02   3.67105146e-02   1.74515989e-03
   3.11324405e-02   5.90613023e-02   6.82406573e-02   3.90106181e-02
  -9.53443857e-03   1.58865967e-02  -4.16683453e-03   7.32182225e-02
   8.47009622e-02   5.62714611e-02  -1.24069736e-02   4.87446666e-03
  -3.79335714e-02  -5.19797594e-02   3.30873996e-02   3.39552721e-02
   4.89651866e-02  -7.36314240e-03  -3.34633185e-02   2.20646390e-02
  -1.29560433e-02  -1.27452000e-02   8.16669153e-02  -2.38157651e-02
   6.00953616e-03  -2.85678578e-02  -8.11775160e-03  -1.13694831e-02
  -2.85005584e-02  -2.88415463e-02  -2.69777316e-02  -7.10060637e-02
   1.83694389e-03  -8.46152310e-02  -2.89519262e-02  -1.84651369e-02
   2.34928442e-02   4.43280096e-02  -8.96961384e-03  -3.02855709e-02
  -6.74380582e-02  -2.37416479e-02   1.15353437e-01  -9.14098326e-04
   2.12484601e-01  -4.41711383e-03  -8.39062302e-02  -4.84036350e-02
  -2.19562266e-02  -1.57801125e-03   5.48035436e-02  -3.3

In [15]:
%%time

# Step 3: Save in Pandas.DataFrame
#
# 将 data['matrix.train'] 与 data['matrix.test'] 转换成 Pandas.DataFrame 格式，保存到 df['train'] 和 df['test'] 中（df 为字典格式：String -> DataFrame）

df = {}
csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')
for tpart in ['train', 'test']:
    datadict = {}
    datadict['class'] = data['vec.{}'.format(tpart)]['class']
    datavec = np.array(data['vec.{}'.format(tpart)]['w2v.mean'])
    for col in range(vecsize):
        datadict[col]= datavec[:, col]

    df[tpart] = pd.DataFrame(data=datadict)
    print("See df[{}]".format(tpart))
    display(df[tpart])
    print("\n\n\n")
    # write data in DataFrame into CSV
    csvpath = os.path.join(csvpath_root, '{}-w2v-{}-{}.csv'.format(tpart, embedFrom, modelFrom))
    df[tpart].to_csv(csvpath, columns=df[tpart].columns)
    
print("Step 3 Succeed.")

# 繁琐点：研究如何把 CSR 矩阵中的数据规整好放到 DataFrame 中，并与 Class 一一对应

See df[train]


0         1         2         3         4         5         6  \
0     0.134146  0.022816  0.066525  0.007707  0.029824  0.096088  0.093319   
1     0.107871  0.064544  0.052942  0.003278  0.027287  0.056178  0.062242   
2     0.095657  0.051399  0.018503 -0.005954  0.027298  0.077769  0.099237   
3     0.111935  0.078724  0.077525 -0.008086  0.048611  0.071447  0.072657   
4     0.111703  0.051782  0.052727  0.003354  0.015282  0.057832  0.053438   
5     0.067998  0.100077  0.092834 -0.001377  0.088411  0.046322  0.097584   
6     0.098015  0.047765  0.035567  0.009889  0.022270  0.077850  0.070782   
7     0.084301  0.036999  0.056305 -0.008189  0.063838  0.048782  0.075776   
8     0.084280  0.060034  0.081205 -0.007184  0.088481  0.043801  0.079380   
9     0.086600  0.029505  0.047890 -0.014373  0.039605  0.059812  0.072303   
10    0.095753  0.062318  0.057978 -0.022335  0.032029  0.047816  0.089661   
11    0.102034  0.057406  0.044845  0.015056  0.025129  0.078913  0.091081   
12    0.089234  0.012806  0.034197 -0.015346  0.021144  0.016658  0.077112   
13    0.098451  0.067792  0.044685 -0.012485  0.071347  0.045164  0.060071   
14    0.122136  0.046034  0.065377  0.008630  0.010120  0.089074  0.063550   
15    0.085066  0.041642  0.056309 -0.005547  0.045639  0.057811  0.083167   
16    0.086571  0.077163  0.061588  0.009818  0.051008  0.049632  0.079109   
17    0.064116  0.026965  0.097361  0.015052  0.052081 -0.005354  0.074377   
18    0.111744  0.035598  0.053881  0.001477  0.022731  0.070695  0.076135   
19    0.076588  0.090777  0.085437  0.005106  0.063133  0.057261  0.043378   
20    0.094462  0.058480  0.043949  0.003267  0.026609  0.084275  0.078081   
21    0.111985  0.056859  0.053670 -0.000950  0.048608  0.055140  0.066590   
22    0.090021  0.000797  0.065600 -0.004079  0.039247  0.055505  0.059208   
23    0.077725  0.108350  0.130648  0.012638  0.108280  0.040237  0.080372   
24    0.112646  0.099387  0.034847  0.007252  0.045684  0.093012  0.091260   
25    0.110177  0.067817  0.049367 -0.003928  0.050462  0.047047  0.074961   
26    0.102160  0.052344  0.050577  0.009493  0.015363  0.060285  0.068472   
27    0.101624  0.091548  0.059636  0.011360  0.053395  0.055870  0.076383   
28    0.105040  0.044208  0.040370 -0.007501  0.026823  0.055019  0.084324   
29    0.100281  0.057821  0.071111 -0.002291  0.026458  0.052120  0.074256   
...        ...       ...       ...       ...       ...       ...       ...   
2825  0.101694  0.097508  0.088789 -0.000103  0.102298  0.050050  0.062017   
2826  0.095931  0.048941  0.125858  0.003177  0.122741  0.075358  0.067863   
2827  0.142968  0.077054  0.081840 -0.017409  0.091383  0.079297  0.073882   
2828  0.068512  0.121783  0.157620  0.003976  0.141651  0.020499  0.093041   
2829  0.103942  0.054336  0.082197  0.033385  0.045576  0.081126  0.093634   
2830  0.129431  0.101617  0.092937  0.001475  0.071613  0.110912  0.057390   
2831  0.100415  0.124325  0.025314 -0.011478  0.073158  0.147658  0.083098   
2832  0.097415  0.053990  0.072506 -0.027383  0.060180  0.114141  0.101363   
2833  0.093881  0.076560  0.017834  0.007732  0.049290  0.114639  0.101616   
2834  0.115705  0.154551  0.135038 -0.013597  0.177980  0.117735  0.030263   
2835  0.092431  0.092001  0.058678 -0.005286  0.057295  0.088919  0.092808   
2836  0.074861  0.095895  0.085149  0.008741  0.057160  0.081594  0.092510   
2837  0.083592  0.098346  0.094782  0.009039  0.102458  0.074862  0.065507   
2838  0.078952  0.052260  0.062902  0.028483  0.068359  0.082048  0.085502   
2839  0.098525  0.032535  0.053226 -0.016150  0.038357  0.104326  0.062622   
2840  0.072793  0.079658  0.100872 -0.002179  0.163569  0.059939  0.079824   
2841  0.091713  0.049198  0.050738  0.031504  0.069842  0.062359  0.034252   
2842  0.132088  0.052559  0.106696  0.012287  0.113415  0.074788  0.024556   
2843  0.068391  0.085669  0.114765 -0.006293  0.104560  0.072217  0.078521   
2844  0.134505  0.100794  0.101978 





See df[test]


0         1         2         3         4         5         6  \
0     0.110485  0.076890  0.057855  0.012231  0.049497  0.061829  0.066813   
1     0.102775  0.060050  0.049024  0.020366  0.016539  0.059448  0.072511   
2     0.105506  0.060274  0.042150  0.014763  0.014441  0.064229  0.070469   
3     0.076986  0.073713  0.067770  0.023753  0.076873  0.068330  0.082283   
4     0.101776  0.061938  0.048182  0.001988  0.023946  0.099151  0.080874   
5     0.112959  0.061753  0.040814  0.004103  0.029559  0.061828  0.064817   
6     0.091827  0.069278  0.045527  0.030545  0.063067  0.079223  0.084670   
7     0.100764  0.074997  0.043477  0.005520  0.037178  0.048865  0.055046   
8     0.102471  0.065341  0.041814  0.008526  0.001753  0.079280  0.063998   
9     0.098533  0.083798  0.061102  0.013452  0.036864  0.050892  0.082929   
10    0.088674  0.062192  0.039362  0.000170  0.020916  0.043666  0.076764   
11    0.101662  0.073832  0.057428 -0.009572  0.030266  0.056713  0.061192   
12    0.091080  0.051963  0.046524  0.012742  0.033041  0.072432  0.066405   
13    0.105478  0.063985  0.052646 -0.000464  0.019013  0.066925  0.079051   
14    0.105427  0.066699  0.048185  0.001209  0.029899  0.060495  0.050307   
15    0.103923  0.098845  0.061549  0.024084  0.048545  0.070461  0.065329   
16    0.119271  0.050182  0.053579 -0.021254  0.029799  0.063518  0.054454   
17    0.094187  0.057788  0.044186  0.002758  0.026600  0.058618  0.064833   
18    0.123224  0.097001  0.095584  0.005508  0.032924  0.029883  0.073192   
19    0.091150  0.061358  0.035161 -0.008215  0.029285  0.077062  0.064208   
20    0.106059  0.063382  0.053309  0.007489  0.024038  0.097509  0.066680   
21    0.099641  0.033500  0.050292 -0.035096  0.060050  0.045145  0.073919   
22    0.134631  0.100014  0.061209  0.036412  0.017126  0.102429  0.082423   
23    0.119406  0.061156  0.056375  0.004984  0.039029  0.062783  0.083917   
24    0.109855  0.087262  0.045317  0.039877  0.049111  0.107629  0.069968   
25    0.079532  0.042452  0.088041  0.015275  0.045642  0.043514  0.064629   
26    0.105535  0.091513  0.064022  0.018854  0.060348  0.050573  0.099442   
27    0.135435  0.068230  0.127689  0.034306  0.098309  0.008376  0.089281   
28    0.127444  0.034728  0.051924  0.034903  0.047185  0.084349  0.068608   
29    0.116087  0.103540  0.072814 -0.021435  0.050774  0.076884  0.062666   
...        ...       ...       ...       ...       ...       ...       ...   
1870  0.098079  0.122749  0.107594  0.022587  0.098468  0.088984  0.083328   
1871  0.181358  0.097664  0.063202  0.043447  0.112709  0.094316  0.049311   
1872  0.158286  0.081719  0.099682  0.013718  0.082380  0.115677  0.058615   
1873  0.096231  0.111280  0.074659 -0.010792  0.083342  0.061531  0.066921   
1874  0.106594  0.089951  0.078364  0.007076  0.046274  0.084130  0.060075   
1875  0.093391  0.053737  0.063218  0.017301  0.091551  0.022832  0.077198   
1876  0.097211  0.077279  0.107169  0.030636  0.104509  0.060231  0.061663   
1877  0.127006  0.072599  0.105705  0.011977  0.084705  0.051929  0.078023   
1878  0.103069  0.133831  0.146182 -0.000132  0.127913  0.081366  0.057752   
1879  0.091760  0.069998  0.063496  0.019355  0.031920  0.052734  0.077328   
1880  0.107736  0.062553  0.045398  0.011203  0.051386  0.088617  0.087798   
1881  0.114915  0.088664  0.032685  0.024852  0.037155  0.006221  0.058021   
1882  0.042417  0.080530  0.133084  0.028095  0.146646  0.015518  0.110722   
1883  0.094746  0.099886  0.143748  0.024008  0.114654  0.042562  0.066385   
1884  0.109812  0.043077  0.058183  0.008350  0.059701  0.079071  0.070931   
1885  0.081920  0.082273  0.100822  0.025680  0.098358  0.055320  0.052516   
1886  0.107310  0.088401  0.075916  0.006427  0.069974  0.087054  0.052976   
1887  0.082936  0.130288  0.116098 -0.016474  0.112383  0.043531  0.052114   
1888  0.058786  0.096078  0.104901  0.021213  0.103170  0.040307  0.075551   
1889  0.140520  0.105951  0.123461 





Step 3 Succeed.
CPU times: user 2.06 s, sys: 108 ms, total: 2.17 s
Wall time: 2.3 s


In [16]:
%%time

# if wanna read data from CSV file

df = {}

for tpart in ['train', 'test']:
    csvpath = os.path.join(
        csvpath_root, '{}-w2v-{}-{}.csv'.format(
            tpart, embedFrom, modelFrom
        )
    )
    if os.path.exists(csvpath):
        df[tpart] = pd.DataFrame.from_csv(csvpath)
        df[tpart] = df[tpart].sample(frac=1)
        df[tpart].reset_index(drop=True, inplace=True)
        print("read {} successfully".format(tpart))
        display(df[tpart])

read train successfully


0         1         2         3         4         5         6  \
0     0.127984  0.076412  0.064878  0.005265  0.021043  0.114090  0.089406   
1     0.098776  0.108790  0.075741  0.024994  0.081831  0.063912  0.023676   
2     0.073719  0.100003  0.126635  0.040235  0.105649  0.050493  0.082930   
3     0.125205  0.059806  0.069671  0.023853  0.071112  0.107931  0.050343   
4     0.098426  0.079489  0.069951  0.013256  0.071235  0.074772  0.069283   
5     0.101362  0.071269  0.058881  0.008350  0.022206  0.095703  0.071307   
6     0.096613  0.079027  0.127487 -0.006836  0.108117  0.064367  0.072061   
7     0.068703  0.107065  0.071342  0.001432  0.087323  0.075902  0.081688   
8     0.094560  0.052768  0.078472  0.017860  0.068003  0.084606  0.075889   
9     0.105227  0.031220  0.048805  0.015805  0.031977  0.042322  0.043163   
10    0.112368  0.049604  0.063017 -0.002837  0.031144  0.059428  0.068829   
11    0.093794  0.082411  0.123460  0.019782  0.114877  0.068321  0.067287   
12    0.114173  0.077162  0.052217 -0.021469  0.050432  0.094897  0.054179   
13    0.084477  0.091151  0.101326  0.010876  0.140730  0.079124  0.086391   
14    0.063779  0.108500  0.117656  0.011613  0.098864  0.071516  0.078560   
15    0.084853  0.081122  0.110244 -0.000810  0.125817  0.054918  0.068592   
16    0.079374  0.097139  0.078441  0.034796  0.062491  0.094961  0.053431   
17    0.081692  0.094390  0.091171  0.003996  0.058461  0.075236  0.083668   
18    0.064979  0.098201  0.117942  0.034366  0.106552  0.043453  0.082332   
19    0.118996  0.049787  0.043818 -0.013058  0.028579  0.053755  0.058227   
20    0.068707  0.061558  0.087240  0.035635  0.028391  0.155472  0.065125   
21    0.098321  0.083865  0.068750 -0.000027  0.066627  0.079342  0.073412   
22    0.103061  0.067445  0.061182  0.010836  0.032272  0.075385  0.068303   
23    0.150166  0.074542  0.041254  0.015051  0.055690  0.135722  0.073978   
24    0.125109  0.071800  0.052545 -0.004132  0.119666  0.080960  0.025650   
25    0.078394  0.089451  0.077931 -0.007371  0.052853  0.108188  0.080421   
26    0.072804  0.048062  0.063593 -0.036816  0.056363  0.066608  0.061881   
27    0.111849  0.055943  0.102365  0.005982  0.060476  0.066453  0.083879   
28    0.109456  0.060724  0.053220  0.009329  0.041502  0.065686  0.063910   
29    0.034047  0.101040  0.172799  0.028017  0.186938  0.050852  0.054355   
...        ...       ...       ...       ...       ...       ...       ...   
2825  0.093757  0.053976  0.097673 -0.019118  0.085517  0.098336  0.057372   
2826  0.067493  0.088975  0.101780  0.036938  0.089678  0.114564  0.044135   
2827  0.103737  0.045544  0.029751  0.016015  0.042273  0.087741  0.083020   
2828  0.090715  0.050879  0.043834  0.020196  0.036688  0.045558  0.060595   
2829  0.111632  0.067284  0.054611 -0.007535  0.029163  0.051265  0.072648   
2830  0.086976  0.088429  0.114877  0.022478  0.107371  0.065510  0.110956   
2831  0.068749  0.042788  0.110176  0.012273  0.088706  0.070695  0.084957   
2832  0.130344  0.049734  0.101965 -0.025357  0.035170  0.102050  0.063023   
2833  0.112315  0.068736  0.073432 -0.016360  0.011999  0.089607  0.068720   
2834  0.087393  0.070776  0.092623  0.011115  0.065256  0.092210  0.063059   
2835  0.125933  0.085231  0.088027 -0.001263  0.055010  0.078065  0.087122   
2836  0.149977  0.113155  0.154863 -0.004229  0.145082  0.109006  0.048500   
2837  0.091716  0.099960  0.077876  0.012536  0.105325  0.072054  0.051977   
2838  0.088787  0.067718  0.065829  0.017554  0.059730  0.073134  0.078618   
2839  0.094642  0.096959  0.128098 -0.002276  0.117248  0.066282  0.085416   
2840  0.109222  0.073078  0.090912  0.011246  0.055737  0.060593  0.084649   
2841  0.109268  0.078864  0.071883  0.019151  0.040911  0.068033  0.064097   
2842  0.100415  0.124325  0.025314 -0.011478  0.073158  0.147658  0.083098   
2843  0.111761  0.112492  0.110017 -0.003714  0.053929  0.097974  0.054525   
2844  0.098831  0.089095  0.074774 

read test successfully


0         1         2         3         4         5         6  \
0     0.117156  0.035972  0.051845 -0.016052  0.025539  0.059983  0.075014   
1     0.110975  0.056041  0.046167  0.026555  0.043311  0.051204  0.067518   
2     0.117398  0.095205  0.039972  0.008898  0.101191  0.079308  0.076313   
3     0.132051  0.106423  0.062343 -0.008911  0.026505  0.095809  0.078950   
4     0.090719  0.020754  0.051352 -0.005778  0.047525  0.038247  0.069040   
5     0.078234  0.084377  0.086052 -0.012879  0.071573  0.058403  0.100723   
6     0.104393  0.083400  0.076264  0.012222  0.062848  0.094782  0.044602   
7     0.045179  0.137863  0.160788 -0.014989  0.117497  0.110442  0.043135   
8     0.120538  0.057498  0.060115  0.025863  0.056038  0.060599  0.050110   
9     0.114986  0.080171  0.062245  0.014584  0.050199  0.102513  0.040670   
10    0.056882  0.121101  0.153654 -0.001793  0.116113  0.031550  0.067246   
11    0.112126  0.088932  0.082491  0.000139  0.062364  0.087663  0.087136   
12    0.109585  0.042491  0.066494 -0.002846  0.040315  0.080517  0.079437   
13    0.105538  0.064148  0.073929  0.003868  0.037172  0.066487  0.057571   
14    0.124055  0.089340  0.065350 -0.000401  0.060429  0.093901  0.063348   
15    0.091201  0.063990  0.050604  0.011265  0.045043  0.055539  0.081108   
16    0.071428  0.121462  0.125053 -0.002355  0.112433  0.038139  0.063602   
17    0.108818  0.078249  0.061574  0.000746  0.028961  0.083764  0.079985   
18    0.083015  0.081119  0.088674  0.028777  0.073578  0.066056  0.052663   
19    0.059940  0.100414  0.128305  0.022589  0.105980  0.035280  0.067970   
20    0.065819  0.147449  0.136519  0.020021  0.103102  0.023604  0.074858   
21    0.043676  0.115581  0.164114  0.033358  0.152694  0.043958  0.083815   
22    0.126317  0.107038  0.101653  0.005694  0.123289  0.062728  0.052061   
23    0.097393  0.037642  0.072477 -0.004055  0.031888  0.044651  0.086130   
24    0.110574  0.050603  0.043319  0.011366  0.021243  0.058901  0.069596   
25    0.088585  0.110839  0.073140  0.013179  0.076323  0.079596  0.038845   
26    0.125377  0.076877  0.054191  0.010764  0.033802  0.090794  0.073704   
27    0.102015  0.076643  0.059639  0.047346  0.072719  0.059432  0.064873   
28    0.091120  0.082080  0.084652 -0.005316  0.053738  0.037582  0.068042   
29    0.120081  0.029163  0.034891  0.017932  0.069168  0.051440  0.057637   
...        ...       ...       ...       ...       ...       ...       ...   
1870  0.104336  0.099500  0.128726  0.015386  0.077870  0.097116  0.048347   
1871  0.093168  0.108875  0.083693  0.010662  0.076562  0.052137  0.078142   
1872  0.088446  0.059448  0.073296  0.005913  0.048828  0.064779  0.078616   
1873  0.093411  0.102481  0.056083  0.044268  0.086859  0.131354  0.058137   
1874  0.104053  0.116999  0.090055  0.028502  0.076787  0.055335  0.066420   
1875  0.071194  0.048779  0.061096 -0.012468  0.061297  0.040650  0.075357   
1876  0.095542  0.132465  0.052281  0.030761  0.111353  0.088151  0.076289   
1877  0.111655  0.078504  0.096879  0.002167  0.079166  0.089565  0.067768   
1878  0.115800  0.065931  0.050865  0.011941  0.045174  0.076355  0.065072   
1879  0.115392  0.053178  0.067865  0.015899  0.057137  0.094389  0.075262   
1880  0.084620  0.113107  0.095292  0.026485  0.112047  0.068881  0.049553   
1881  0.052351  0.101841  0.132690  0.007395  0.095733  0.067598  0.082571   
1882  0.112134  0.078670  0.073100 -0.009942  0.025739  0.068845  0.072755   
1883  0.109899  0.063847  0.064206  0.016458  0.063796  0.101838  0.077669   
1884  0.097281  0.093568  0.077965  0.020875  0.066122  0.068779  0.079935   
1885  0.078292  0.090299  0.097601  0.022099  0.084830  0.052200  0.071269   
1886  0.077569  0.097586  0.139226  0.001183  0.104258  0.047160  0.046289   
1887  0.073708  0.083394  0.102604  0.002688  0.097645  0.045785  0.098396   
1888  0.088431  0.068243  0.058877  0.004496  0.048470  0.082055  0.065090   
1889  0.069647  0.116011  0.106187 

CPU times: user 876 ms, sys: 12 ms, total: 888 ms
Wall time: 885 ms


###### SVM classifier(TensorFlow + text8)

In [17]:
%%time

# Step 5.1.1: SVM

# if 'TFIDF' == modelChoice:

#train
X_train = df['train'].drop('class', axis=1)
y_train = df['train']['class']
#test
X_test = df['test'].drop('class', axis=1)
y_test_true = df['test']['class']

# else:
#     #train
#     X_train = df_new['train']['x']
#     y_train = df_new['train']['y']
#     #test
#     X_test = df_new['test']['x']
#     y_test_true = df_new['test']['y']

clf = LinearSVC()
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 2.18 s, sys: 8 ms, total: 2.19 s
Wall time: 2.19 s


In [18]:
%%time
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

0.844210526316
0.841730403892
0.844210526316
CPU times: user 20 ms, sys: 4 ms, total: 24 ms
Wall time: 47.5 ms


###### DNN classifier(TensorFlow + text8)

In [19]:
%%time

# Step 4: One-hot representation for labels

csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')

lb = LabelBinarizer()
lb.fit(df['train']['class'])

df_new = {}
for tpart in ['train', 'test']:
    labels = lb.transform(df[tpart]['class'])
    labelsDf = pd.DataFrame(labels, columns=["class-{}".format(i) for i in range(len(lb.classes_))])
    df_new[tpart] = {}
    df_new[tpart]['y'] = labelsDf
    df_new[tpart]['x'] = df[tpart].drop('class', axis=1)
    df_new[tpart]['all'] = df_new[tpart]['x'].join(df_new[tpart]['y'])
    #save in CSV
    for subpart in ['x', 'y', 'all']:
        csvpath = os.path.join(csvpath_root, "{}-cleanLabels-{}-{}.csv".format(tpart, subpart, modelFrom))
        df_new[tpart][subpart].to_csv(csvpath)
    
print("label cleaning succussfully")

label cleaning succussfully
CPU times: user 3.82 s, sys: 148 ms, total: 3.97 s
Wall time: 4.53 s


In [20]:
%%time

## Step 5 : Train the classifier

COL_OUTCOME = 'class'
COL_FEATURE = [str(col) for col in list(df['train'].columns) if col != COL_OUTCOME]

cls2num = {cls:ind for (ind, cls) in enumerate(df['train']['class'].unique())}

def my_input_fn(dataset):
    # Save dataset in tf format
    feature_cols = {
        str(col): tf.constant(
            df[dataset][str(col)].values
        )
        for col in COL_FEATURE
    }
    labels = tf.constant([cls2num[labelname] for labelname in df[dataset][COL_OUTCOME].values])
    # Returns the feature columns and labels in tf format
    return feature_cols, labels

feature_columns = [tf.contrib.layers.real_valued_column(column_name=str(col)) for col in COL_FEATURE]
clf = tf.contrib.learn.DNNClassifier(
    feature_columns=feature_columns, 
    hidden_units=[512], 
    n_classes=len(df['train']['class'].unique())
)

clf.fit(input_fn=lambda: my_input_fn('train'), steps=2000)

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_num_ps_replicas': 0, '_keep_checkpoint_max': 5, '_tf_random_seed': None, '_task_type': None, '_environment': 'local', '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7fd820168610>, '_tf_config': gpu_options {
  per_process_gpu_memory_fraction: 1.0
}
, '_task_id': 0, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_evaluation_master': '', '_keep_checkpoint_every_n_hours': 10000, '_master': ''}


Instructions for updating:
Please switch to tf.summary.scalar. Note that tf.summary.scalar uses the node name instead of the tag. This means that TensorFlow will automatically de-duplicate summary names based on the scope they are created in. Also, passing a tensor or list of tags to a scalar summary op is no longer supported.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/tmpXSrbXD/model.ckpt.
INFO:tensorflow:loss = 1.60711, step = 1
INFO:tensorflow:global_step/sec: 11.7525
INFO:tensorflow:loss = 1.40578, step = 101
INFO:tensorflow:global_step/sec: 11.9453
INFO:tensorflow:loss = 1.22552, step = 201
INFO:tensorflow:global_step/sec: 11.8355
INFO:tensorflow:loss = 1.07758, step = 301
INFO:tensorflow:global_step/sec: 12.038
INFO:tensorflow:loss = 0.946373, step = 401
INFO:tensorflow:global_step/sec: 11.9142
INFO:tensorflow:loss = 0.838808, step = 501
INFO:tensorflow:global_step/sec: 11.9694
INFO:tensorflow:loss = 0.753202, step = 601
INFO:te

In [21]:
%%time

## Step 6: Evaluate

accuracy_score = clf.evaluate(input_fn=lambda: my_input_fn('test'), steps=df['test'].shape[0])['accuracy']
print("Test Accuracy by TensorFlow: {}".format(accuracy_score))

X_tensor_test, yt = my_input_fn('test')
tensorPredCls = list(clf.predict(input_fn=lambda: my_input_fn('test')))
num2cls = {v:k for (k, v) in cls2num.items()}
tensorPredClsStr = [num2cls[i] for i in tensorPredCls]
y_test_true = df['test']['class']
print('Test Accuracy by Scikit-learn: ', f1_score(y_test_true, tensorPredClsStr, average='micro'))

Instructions for updating:
Please switch to tf.summary.scalar. Note that tf.summary.scalar uses the node name instead of the tag. This means that TensorFlow will automatically de-duplicate summary names based on the scope they are created in. Also, passing a tensor or list of tags to a scalar summary op is no longer supported.
INFO:tensorflow:Starting evaluation at 2017-05-14-07:06:48
INFO:tensorflow:Evaluation [1/1900]
INFO:tensorflow:Evaluation [2/1900]
INFO:tensorflow:Evaluation [3/1900]
INFO:tensorflow:Evaluation [4/1900]
INFO:tensorflow:Evaluation [5/1900]
INFO:tensorflow:Evaluation [6/1900]
INFO:tensorflow:Evaluation [7/1900]
INFO:tensorflow:Evaluation [8/1900]
INFO:tensorflow:Evaluation [9/1900]
INFO:tensorflow:Evaluation [10/1900]
INFO:tensorflow:Evaluation [11/1900]
INFO:tensorflow:Evaluation [12/1900]
INFO:tensorflow:Evaluation [13/1900]
INFO:tensorflow:Evaluation [14/1900]
INFO:tensorflow:Evaluation [15/1900]
INFO:tensorflow:Evaluation [16/1900]
INFO:tensorflow:Evaluation [1

INFO:tensorflow:Evaluation [73/1900]
INFO:tensorflow:Evaluation [74/1900]
INFO:tensorflow:Evaluation [75/1900]
INFO:tensorflow:Evaluation [76/1900]
INFO:tensorflow:Evaluation [77/1900]
INFO:tensorflow:Evaluation [78/1900]
INFO:tensorflow:Evaluation [79/1900]
INFO:tensorflow:Evaluation [80/1900]
INFO:tensorflow:Evaluation [81/1900]
INFO:tensorflow:Evaluation [82/1900]
INFO:tensorflow:Evaluation [83/1900]
INFO:tensorflow:Evaluation [84/1900]
INFO:tensorflow:Evaluation [85/1900]
INFO:tensorflow:Evaluation [86/1900]
INFO:tensorflow:Evaluation [87/1900]
INFO:tensorflow:Evaluation [88/1900]
INFO:tensorflow:Evaluation [89/1900]
INFO:tensorflow:Evaluation [90/1900]
INFO:tensorflow:Evaluation [91/1900]
INFO:tensorflow:Evaluation [92/1900]
INFO:tensorflow:Evaluation [93/1900]
INFO:tensorflow:Evaluation [94/1900]
INFO:tensorflow:Evaluation [95/1900]
INFO:tensorflow:Evaluation [96/1900]
INFO:tensorflow:Evaluation [97/1900]
INFO:tensorflow:Evaluation [98/1900]
INFO:tensorflow:Evaluation [99/1900]
I

INFO:tensorflow:Evaluation [290/1900]
INFO:tensorflow:Evaluation [291/1900]
INFO:tensorflow:Evaluation [292/1900]
INFO:tensorflow:Evaluation [293/1900]
INFO:tensorflow:Evaluation [294/1900]
INFO:tensorflow:Evaluation [295/1900]
INFO:tensorflow:Evaluation [296/1900]
INFO:tensorflow:Evaluation [297/1900]
INFO:tensorflow:Evaluation [298/1900]
INFO:tensorflow:Evaluation [299/1900]
INFO:tensorflow:Evaluation [300/1900]
INFO:tensorflow:Evaluation [301/1900]
INFO:tensorflow:Evaluation [302/1900]
INFO:tensorflow:Evaluation [303/1900]
INFO:tensorflow:Evaluation [304/1900]
INFO:tensorflow:Evaluation [305/1900]
INFO:tensorflow:Evaluation [306/1900]
INFO:tensorflow:Evaluation [307/1900]
INFO:tensorflow:Evaluation [308/1900]
INFO:tensorflow:Evaluation [309/1900]
INFO:tensorflow:Evaluation [310/1900]
INFO:tensorflow:Evaluation [311/1900]
INFO:tensorflow:Evaluation [312/1900]
INFO:tensorflow:Evaluation [313/1900]
INFO:tensorflow:Evaluation [314/1900]
INFO:tensorflow:Evaluation [315/1900]
INFO:tensorf

INFO:tensorflow:Evaluation [506/1900]
INFO:tensorflow:Evaluation [507/1900]
INFO:tensorflow:Evaluation [508/1900]
INFO:tensorflow:Evaluation [509/1900]
INFO:tensorflow:Evaluation [510/1900]
INFO:tensorflow:Evaluation [511/1900]
INFO:tensorflow:Evaluation [512/1900]
INFO:tensorflow:Evaluation [513/1900]
INFO:tensorflow:Evaluation [514/1900]
INFO:tensorflow:Evaluation [515/1900]
INFO:tensorflow:Evaluation [516/1900]
INFO:tensorflow:Evaluation [517/1900]
INFO:tensorflow:Evaluation [518/1900]
INFO:tensorflow:Evaluation [519/1900]
INFO:tensorflow:Evaluation [520/1900]
INFO:tensorflow:Evaluation [521/1900]
INFO:tensorflow:Evaluation [522/1900]
INFO:tensorflow:Evaluation [523/1900]
INFO:tensorflow:Evaluation [524/1900]
INFO:tensorflow:Evaluation [525/1900]
INFO:tensorflow:Evaluation [526/1900]
INFO:tensorflow:Evaluation [527/1900]
INFO:tensorflow:Evaluation [528/1900]
INFO:tensorflow:Evaluation [529/1900]
INFO:tensorflow:Evaluation [530/1900]
INFO:tensorflow:Evaluation [531/1900]
INFO:tensorf

INFO:tensorflow:Evaluation [722/1900]
INFO:tensorflow:Evaluation [723/1900]
INFO:tensorflow:Evaluation [724/1900]
INFO:tensorflow:Evaluation [725/1900]
INFO:tensorflow:Evaluation [726/1900]
INFO:tensorflow:Evaluation [727/1900]
INFO:tensorflow:Evaluation [728/1900]
INFO:tensorflow:Evaluation [729/1900]
INFO:tensorflow:Evaluation [730/1900]
INFO:tensorflow:Evaluation [731/1900]
INFO:tensorflow:Evaluation [732/1900]
INFO:tensorflow:Evaluation [733/1900]
INFO:tensorflow:Evaluation [734/1900]
INFO:tensorflow:Evaluation [735/1900]
INFO:tensorflow:Evaluation [736/1900]
INFO:tensorflow:Evaluation [737/1900]
INFO:tensorflow:Evaluation [738/1900]
INFO:tensorflow:Evaluation [739/1900]
INFO:tensorflow:Evaluation [740/1900]
INFO:tensorflow:Evaluation [741/1900]
INFO:tensorflow:Evaluation [742/1900]
INFO:tensorflow:Evaluation [743/1900]
INFO:tensorflow:Evaluation [744/1900]
INFO:tensorflow:Evaluation [745/1900]
INFO:tensorflow:Evaluation [746/1900]
INFO:tensorflow:Evaluation [747/1900]
INFO:tensorf

...

INFO:tensorflow:Evaluation [1150/1900]
INFO:tensorflow:Evaluation [1151/1900]
INFO:tensorflow:Evaluation [1152/1900]
INFO:tensorflow:Evaluation [1153/1900]
INFO:tensorflow:Evaluation [1154/1900]
INFO:tensorflow:Evaluation [1155/1900]
INFO:tensorflow:Evaluation [1156/1900]
INFO:tensorflow:Evaluation [1157/1900]
INFO:tensorflow:Evaluation [1158/1900]
INFO:tensorflow:Evaluation [1159/1900]
INFO:tensorflow:Evaluation [1160/1900]
INFO:tensorflow:Evaluation [1161/1900]
INFO:tensorflow:Evaluation [1162/1900]
INFO:tensorflow:Evaluation [1163/1900]
INFO:tensorflow:Evaluation [1164/1900]
INFO:tensorflow:Evaluation [1165/1900]
INFO:tensorflow:Evaluation [1166/1900]
INFO:tensorflow:Evaluation [1167/1900]
INFO:tensorflow:Evaluation [1168/1900]
INFO:tensorflow:Evaluation [1169/1900]
INFO:tensorflow:Evaluation [1170/1900]
INFO:tensorflow:Evaluation [1171/1900]
INFO:tensorflow:Evaluation [1172/1900]
INFO:tensorflow:Evaluation [1173/1900]
INFO:tensorflow:Evaluation [1174/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1361/1900]
INFO:tensorflow:Evaluation [1362/1900]
INFO:tensorflow:Evaluation [1363/1900]
INFO:tensorflow:Evaluation [1364/1900]
INFO:tensorflow:Evaluation [1365/1900]
INFO:tensorflow:Evaluation [1366/1900]
INFO:tensorflow:Evaluation [1367/1900]
INFO:tensorflow:Evaluation [1368/1900]
INFO:tensorflow:Evaluation [1369/1900]
INFO:tensorflow:Evaluation [1370/1900]
INFO:tensorflow:Evaluation [1371/1900]
INFO:tensorflow:Evaluation [1372/1900]
INFO:tensorflow:Evaluation [1373/1900]
INFO:tensorflow:Evaluation [1374/1900]
INFO:tensorflow:Evaluation [1375/1900]
INFO:tensorflow:Evaluation [1376/1900]
INFO:tensorflow:Evaluation [1377/1900]
INFO:tensorflow:Evaluation [1378/1900]
INFO:tensorflow:Evaluation [1379/1900]
INFO:tensorflow:Evaluation [1380/1900]
INFO:tensorflow:Evaluation [1381/1900]
INFO:tensorflow:Evaluation [1382/1900]
INFO:tensorflow:Evaluation [1383/1900]
INFO:tensorflow:Evaluation [1384/1900]
INFO:tensorflow:Evaluation [1385/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1572/1900]
INFO:tensorflow:Evaluation [1573/1900]
INFO:tensorflow:Evaluation [1574/1900]
INFO:tensorflow:Evaluation [1575/1900]
INFO:tensorflow:Evaluation [1576/1900]
INFO:tensorflow:Evaluation [1577/1900]
INFO:tensorflow:Evaluation [1578/1900]
INFO:tensorflow:Evaluation [1579/1900]
INFO:tensorflow:Evaluation [1580/1900]
INFO:tensorflow:Evaluation [1581/1900]
INFO:tensorflow:Evaluation [1582/1900]
INFO:tensorflow:Evaluation [1583/1900]
INFO:tensorflow:Evaluation [1584/1900]
INFO:tensorflow:Evaluation [1585/1900]
INFO:tensorflow:Evaluation [1586/1900]
INFO:tensorflow:Evaluation [1587/1900]
INFO:tensorflow:Evaluation [1588/1900]
INFO:tensorflow:Evaluation [1589/1900]
INFO:tensorflow:Evaluation [1590/1900]
INFO:tensorflow:Evaluation [1591/1900]
INFO:tensorflow:Evaluation [1592/1900]
INFO:tensorflow:Evaluation [1593/1900]
INFO:tensorflow:Evaluation [1594/1900]
INFO:tensorflow:Evaluation [1595/1900]
INFO:tensorflow:Evaluation [1596/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1783/1900]
INFO:tensorflow:Evaluation [1784/1900]
INFO:tensorflow:Evaluation [1785/1900]
INFO:tensorflow:Evaluation [1786/1900]
INFO:tensorflow:Evaluation [1787/1900]
INFO:tensorflow:Evaluation [1788/1900]
INFO:tensorflow:Evaluation [1789/1900]
INFO:tensorflow:Evaluation [1790/1900]
INFO:tensorflow:Evaluation [1791/1900]
INFO:tensorflow:Evaluation [1792/1900]
INFO:tensorflow:Evaluation [1793/1900]
INFO:tensorflow:Evaluation [1794/1900]
INFO:tensorflow:Evaluation [1795/1900]
INFO:tensorflow:Evaluation [1796/1900]
INFO:tensorflow:Evaluation [1797/1900]
INFO:tensorflow:Evaluation [1798/1900]
INFO:tensorflow:Evaluation [1799/1900]
INFO:tensorflow:Evaluation [1800/1900]
INFO:tensorflow:Evaluation [1801/1900]
INFO:tensorflow:Evaluation [1802/1900]
INFO:tensorflow:Evaluation [1803/1900]
INFO:tensorflow:Evaluation [1804/1900]
INFO:tensorflow:Evaluation [1805/1900]
INFO:tensorflow:Evaluation [1806/1900]
INFO:tensorflow:Evaluation [1807/1900]
INFO:tensorflow:Evaluatio

Test Accuracy by Scikit-learn:  0.800526315789
CPU times: user 8min 47s, sys: 38.9 s, total: 9min 26s
Wall time: 1min 41s


###### CNN classifier(TensorFlow + text8)

In [22]:
%%time

import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

sess = tf.InteractiveSession()

COL_OUTCOME = 'class'
COL_FEATURE = [col for col in list(df['train'].columns) if col != COL_OUTCOME]

# cls2num = {cls:ind for (ind, cls) in enumerate(df['train']['class'].unique())}

count_feature = len(COL_FEATURE)
count_class = len(df['train']['class'].unique())

x = tf.placeholder(tf.float32, shape=[None, 784], name='x')
y_ = tf.placeholder(tf.float32, shape=[None, count_class], name='y_')

W = tf.Variable(tf.zeros([count_feature, count_class]))
b = tf.Variable(tf.zeros([count_class]))
y = tf.matmul(x, W) + b

# cross_entropy = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=y_, logits=y))

def weight_variable(shape):
    initial = tf.truncated_normal(shape, stddev=0.1)
    return tf.Variable(initial)

def bias_variable(shape):
    initial = tf.constant(0.1, shape=shape)
    return tf.Variable(initial)

def conv2d(x, W):
    return tf.nn.conv2d(x, W, strides=[1, 1, 1, 1], padding='SAME')

def max_pool_2x2(x):
    return tf.nn.max_pool(x, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')

W_conv1 = weight_variable([5, 5, 1, 32])
b_conv1 = bias_variable([32])
x_text = tf.reshape(x, [-1, 28, 28, 1])
h_conv1 = tf.nn.relu(conv2d(x_text, W_conv1) + b_conv1)
h_pool1 = max_pool_2x2(h_conv1)

W_conv2 = weight_variable([5, 5, 32, 64])
b_conv2 = bias_variable([64])
h_conv2 = tf.nn.relu(conv2d(h_pool1, W_conv2) + b_conv2)
h_pool2 = max_pool_2x2(h_conv2)

W_fc1 = weight_variable([7 * 7 * 64, 1024])
b_fc1 = bias_variable([1024])

h_pool2_flat = tf.reshape(h_pool2, [-1, 7 * 7 * 64])
h_fc1 = tf.nn.relu(tf.matmul(h_pool2_flat, W_fc1) + b_fc1)

keep_prob = tf.placeholder(tf.float32, name='keep_prob')
h_fc1_drop = tf.nn.dropout(h_fc1, keep_prob)

W_fc2 = weight_variable([1024, count_class])
b_fc2 = bias_variable([count_class])

y_conv = tf.matmul(h_fc1_drop, W_fc2) + b_fc2

print("CNN initialization finished")

CNN initialization finished
CPU times: user 36 ms, sys: 0 ns, total: 36 ms
Wall time: 39.4 ms


In [23]:
%%time

### Start to traini and evaluate the model

cross_entropy = tf.reduce_mean(
    tf.nn.softmax_cross_entropy_with_logits(labels=y_, logits=y_conv))
train_step = tf.train.AdamOptimizer(1e-4).minimize(cross_entropy)
correct_prediction = tf.equal(tf.argmax(y_conv, 1), tf.argmax(y_, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

sess.run(tf.global_variables_initializer())

x_input = df_new['train']['x']
x_input = [np.array([
            np.float32(x_input.iloc[i].values)
        ])
    for i in range(x_input.shape[0])]
y_input = df_new['train']['y']
y_input = [np.array([
            np.float32(y_input.iloc[i].values)
        ])
    for i in range(y_input.shape[0])]
# y_input = [np.array([y_input.iloc[i].values]) for i in range(y_input.shape[0])]

# not use random input

for i in range(df['train'].shape[0] - 50):
    if 0 == i % 100:
        train_accuracy = []
        for j in range(50):
            train_accuracy.append(accuracy.eval(feed_dict={
                    keep_prob: 1,
                    x:  np.array([elem[0] for elem in x_input[i+j:i+j+50]]),#x_input.iloc[i+j].values, #
                    y_: np.array([elem[0] for elem in y_input[i+j:i+j+50]])#y_input.iloc[i+j].values #
                })
            )
        print("step {}, training accuracy {}".format(i, np.mean(train_accuracy)))
    train_step.run(feed_dict={
        keep_prob: 0.5,
        x:  np.array([elem[0] for elem in x_input[i:i+50]]),#x_input.iloc[i].values, #
        y_: np.array([elem[0] for elem in y_input[i:i+50]])#y_input.iloc[i].values#
    })

print("CNN training finished")

step 0, training accuracy 0.161200001836
step 100, training accuracy 0.347199976444
step 200, training accuracy 0.456800013781
step 300, training accuracy 0.485999971628
step 400, training accuracy 0.664000034332
step 500, training accuracy 0.6167999506
step 600, training accuracy 0.714800059795
step 700, training accuracy 0.753199994564
step 800, training accuracy 0.766399979591
step 900, training accuracy 0.841200053692
step 1000, training accuracy 0.761199951172
step 1100, training accuracy 0.744000017643
step 1200, training accuracy 0.800000011921
step 1300, training accuracy 0.795599997044
step 1400, training accuracy 0.789199888706
step 1500, training accuracy 0.835200071335
step 1600, training accuracy 0.843999922276
step 1700, training accuracy 0.740400016308
step 1800, training accuracy 0.779199957848
step 1900, training accuracy 0.874400019646
step 2000, training accuracy 0.837999939919
step 2100, training accuracy 0.911200046539
step 2200, training accuracy 0.805199861526
st

In [24]:
%%time

# Evaluate

x_input = df_new['test']['x']#df_new['test']['x']
x_input = [np.array([
            np.float32(x_input.iloc[i].values)
        ])
    for i in range(x_input.shape[0])]
y_input = df_new['test']['y']#df_new['test']['y']
y_input = [np.array([
            np.float32(y_input.iloc[i].values)
        ])
    for i in range(y_input.shape[0])]

for i in range(df['test'].shape[0] - 50):
    if 0 == i % 100:
        train_accuracy = []
        for j in range(50):
            train_accuracy.append(accuracy.eval(feed_dict={
                    keep_prob: 1,
                    x:  np.array([elem[0] for elem in x_input[i+j:i+j+50]]),#x_input.iloc[i+j].values, #
                    y_: np.array([elem[0] for elem in y_input[i+j:i+j+50]])#y_input.iloc[i+j].values #
                })
            )
        print("step {}, testing accuracy {}".format(i, np.mean(train_accuracy)))

        
print("CNN testing finished")

step 0, testing accuracy 0.529199957848
step 100, testing accuracy 0.734799981117
step 200, testing accuracy 0.681600034237
step 300, testing accuracy 0.772399961948
step 400, testing accuracy 0.712800145149
step 500, testing accuracy 0.677600026131
step 600, testing accuracy 0.713600158691
step 700, testing accuracy 0.653599977493
step 800, testing accuracy 0.701599955559
step 900, testing accuracy 0.740800023079
step 1000, testing accuracy 0.761199951172
step 1100, testing accuracy 0.695600032806
step 1200, testing accuracy 0.726800024509
step 1300, testing accuracy 0.803600013256
step 1400, testing accuracy 0.67040002346
step 1500, testing accuracy 0.712799966335
step 1600, testing accuracy 0.627199947834
step 1700, testing accuracy 0.757600069046
step 1800, testing accuracy 0.600000023842
CNN testing finished
CPU times: user 2min 41s, sys: 5.69 s, total: 2min 46s
Wall time: 27.4 s


##### 3.2.1.2 只用待学习语料建模

In [8]:
embedFrom = 'corpus'

In [9]:
%%time

# collect sentences from raw data
sentences = {}
pathtmp = {}
pathtmp['root'] = os.path.join(paths['dir.dataroot'], 'trialdata')
for tpart in ['train']:#, 'test']:
    pathtmp[tpart] = os.path.join(pathtmp['root'], tpart)
    sentences[tpart] = []
    folderList = os.listdir(pathtmp[tpart])
    for folder in folderList:
        fileList = os.listdir(os.path.join(pathtmp[tpart], folder))
        for eachf in fileList:
            fpathtmp = os.path.join(pathtmp[tpart], folder, eachf)
            with open(fpathtmp, 'r') as f:
                sentences[tpart].append(f.read())
      #save sentences in file
        sentencePath = os.path.join(pathtmp['root'], 'corpus')
        with open(sentencePath, 'w') as f:
            for sentence in sentences[tpart]:
                f.write(sentence)
                f.write('\n')

filepathtmp = os.path.join(pathtmp['root'], 'corpus')
sentences = ""#[]
with open(filepathtmp, 'r') as f:
    buff = f.read()
    sentencesBuffer = buff.split('\n')
    sentencesBucket = [ch for stcbuffer in sentencesBuffer for ch in stcbuffer.split()]
    for ch in sentencesBucket:
        sentences += ch
        sentences += " "

filepathtmp = os.path.join(pathtmp['root'], 'corpus')
with open(filepathtmp, 'w') as f:
    f.write(sentences)
        
print('get sentences from training corpus successfully')
print('example:')
print(len(sentences))
print(sentences[:60]) #random.randrange(len(sentences))])        

get sentences from training corpus successfully
example:
4546437
from jenk microsoft com jen kilmer subject re sex education 
CPU times: user 280 ms, sys: 52 ms, total: 332 ms
Wall time: 660 ms


In [12]:
%%time

FLAGS.train_data = os.path.join(paths['dir.dataroot'], 'trialdata', embedFrom)
FLAGS.eval_data = os.path.join(paths['dir.dataroot'], 'trialdata', 'questions-words.txt')
FLAGS.save_path = paths['dir.{}.{}'.format(modelFrom, embedFrom)]
FLAGS.epochs_to_train = 15
FLAGS.embedding_size = vecsize

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 35 µs


In [13]:
!cat ../modules/embedding/w2v_opt_full_02.py

import tensorflow as tf

session = tf.InteractiveSession()
"""Train a word2vec model."""
if not FLAGS.train_data or not FLAGS.eval_data or not FLAGS.save_path:
  print("--train_data --eval_data and --save_path must be specified.")
  sys.exit(1)
opts = Options()
#with tf.Graph().as_default() as session:
with tf.device("/cpu:0"):
  model = Word2Vec(opts, session)
  model.read_analogies() # Read analogy questions
for _ in xrange(opts.epochs_to_train):
  model.train()  # Process one epoch
  model.eval()  # Eval analogies.
# Perform a final save.
model.saver.save(session, os.path.join(opts.save_path, "model.ckpt"),
                 global_step=model.global_step)
if FLAGS.interactive:
  # E.g.,
  # [0]: model.analogy(b'france', b'paris', b'russia')
  # [1]: model.nearby([b'proton', b'elephant', b'maxwell'])
  _start_shell(locals())



In [14]:
%%time

session = tf.InteractiveSession()
"""Train a word2vec model."""
if not FLAGS.train_data or not FLAGS.eval_data or not FLAGS.save_path:
    print("--train_data --eval_data and --save_path must be specified.")
    sys.exit(1)
opts = Options()
#with tf.Graph().as_default() as session:
with tf.device("/cpu:0"):
    model = Word2Vec(opts, session)
    model.read_analogies() # Read analogy questions
for _ in xrange(opts.epochs_to_train):
    model.train()  # Process one epoch
    model.eval()  # Eval analogies.
# Perform a final save.
model.saver.save(session, os.path.join(opts.save_path, "model-{}.ckpt".format(embedFrom)),
                 global_step=model.global_step)
if FLAGS.interactive:
    # E.g.,
    # [0]: model.analogy(b'france', b'paris', b'russia')
    # [1]: model.nearby([b'proton', b'elephant', b'maxwell'])
    _start_shell(locals())

Data file:  /home/sushangjun/gits/Udacity/MLND/capstone.now/proposal/new/notebooks/../data/trialdata/corpus
Vocab size:  10790  + UNK
Words per epoch:  843524
Initialization:  [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 ..., 
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
Eval analogy file:  /home/sushangjun/gits/Udacity/MLND/capstone.now/proposal/new/notebooks/../data/trialdata/questions-words.txt
Questions:  3905
Skipped:  15639
Epoch    1 Step     7455: lr = 0.024 words/sec =    11815
Eval   16/3905 accuracy =  0.4%
Epoch    2 Step    14916: lr = 0.023 words/sec =    15091
Eval   50/3905 accuracy =  1.3%
Epoch    3 Step    22378: lr = 0.021 words/sec =    17318
Eval   51/3905 accuracy =  1.3%
Epoch    4 Step    29829: lr = 0.020 words/sec =    17931
Eval   49/3905 accuracy =  1.3%
Epoch    5 Step    37290: lr = 0.019 words/sec =    17999
Eval   60/3905 accuracy =  1.5%
Epoch    6 S

In [200]:
# from scipy.spatial.distance import cosine

# # tmma=model._w_in.eval()
# # tmma
# tmpemb = model._w_out.eval()
# print(len(tmpemb[model._word2id['slow']]))
# # print(tmpemb[model._word2id['slowly']])
# # print(cosine(tmpemb[model._word2id['slow']], tmpemb[model._word2id['slowly']]))
# # print(cosine(tmpemb[model._word2id['man']], tmpemb[model._word2id['men']]))
# # print(cosine(tmpemb[model._word2id['woman']], tmpemb[model._word2id['women']]))
# # print(cosine(tmpemb[model._word2id['woman']], tmpemb[model._word2id['woman']]))
# print(tmpemb[model._word2id['UNK']])

In [201]:
%%time

# Step 1: preprocess the data

# import stoplist
stopwords = ""

pathtemp_TFIDF = os.path.join(paths['dir.dataroot'], 'stoplist-baseTFIDF.txt')
with open(pathtemp_TFIDF, 'r') as stoplistfile:
    stopwords = stoplistfile.read()
stopwords = stopwords.split()

pathtemp_web = os.path.join(paths['dir.dataroot'], 'stoplist-web.txt')
with open(pathtemp_web, 'r') as stoplistfile2:
    stopwords2 = stoplistfile2.read()
    stopwords2 = stopwords2.split('\n')
    stopwords = set(stopwords)
    stopwords = list(stopwords.union(set(stopwords)))
    
print("Read stop words successfully.")

Read stop words successfully.
CPU times: user 16 ms, sys: 0 ns, total: 16 ms
Wall time: 534 ms


In [203]:
%%time

# Step 2: read data and save it in data['vec.train'] 和 data['vec.test']

data = {}
data['vec.train'] = {'w2v.mean':[], 'class':[]}
data['vec.test'] = {'w2v.mean':[], 'class':[]}

for tpart in ['train', 'test']:
    dirpath = paths['dir.{}'.format(tpart)]
    for (ind, cls) in enumerate(os.listdir(dirpath)):
        clspath = os.path.join(dirpath, cls)
        files = os.listdir(clspath)
        for f in files:
            fpath = os.path.join(clspath, f)
            with open(fpath, 'r') as readf:
                tokens = [token for token in readf.read().split() if token not in stopwords]#readf.read().split()#
                # Word2Vec representation
                # begin
                vec = np.array([0.0 for i in range(vecsize)])
                expectationVal = np.array([0.0 for i in range(vecsize)])
                countvec = 0
                for token in tokens:
                    try:
                        vec += tmpemb[model._word2id[token]] #model[token]
                        countvec += 1
                    except:
                        vec += tmpemb[model._word2id['UNK']]
                vec = vec / float(countvec)
                 # end
            data['vec.{}'.format(tpart)]['w2v.mean'].append(vec)
            data['vec.{}'.format(tpart)]['class'].append(cls)

    tmp = data['vec.{}'.format(tpart)]
    ind = (random.sample(range(len(tmp['class'])), 1))[0]
    print("sample(transformed) from {}[{}]:\n[corpus]\n {}\n[class]\n{}".format(tpart, ind, tmp['w2v.mean'][ind], tmp['class'][ind]))
    print()
    
print("Step 2 Succeed")

sample(transformed) from train[1134]:
[corpus]
 [ -9.14742260e-02   1.97657122e-02   4.88034414e-02  -2.14501246e-02
   2.89537850e-02   3.69584016e-02  -1.96420203e-02   2.52398994e-02
   2.04244950e-02   1.09431348e-01  -1.63828118e-02  -3.04512786e-02
   4.90008398e-02  -4.13084460e-02  -4.08775516e-02   1.13422616e-01
   1.09650938e-01   1.24379964e-01   6.62501065e-02   1.37616521e-01
  -7.81755025e-02   5.58870664e-02   9.81221798e-02  -7.58008440e-03
  -2.30257731e-02   3.67379372e-02  -3.06308693e-02   4.86731597e-02
   5.36724845e-02   5.25526757e-02   1.73793200e-02   5.38565988e-02
  -8.19522027e-02  -1.23996193e-01   3.59019776e-02  -1.04500795e-01
   2.66090137e-02   5.39927276e-02  -1.18805606e-02  -7.62467396e-03
  -5.00652456e-02   1.40609098e-01  -3.06014993e-02  -1.45811353e-01
  -1.23290552e-01   1.14025326e-02   6.53584848e-02   6.93422551e-02
   6.93176080e-03   2.72750730e-02  -1.49903798e-01  -5.76191623e-02
  -1.00610992e-01   1.58461575e-02  -6.41822497e-02   8

sample(transformed) from test[1150]:
[corpus]
 [ -1.03927469e-01   1.28367011e-02   3.54833295e-02  -2.80670408e-02
   5.74810325e-02   3.48400845e-02  -5.37967970e-03   1.45811907e-02
  -6.20764606e-03   9.07164651e-02  -3.09716331e-02  -3.27652136e-02
   3.21756180e-02  -3.75893238e-02  -2.12911729e-02   1.18714038e-01
   1.05336746e-01   1.26588981e-01   6.89988573e-02   1.23069280e-01
  -8.59222234e-02   6.09937534e-02   6.97960741e-02  -9.31329114e-03
  -3.33334676e-02   2.60146730e-03  -3.20336184e-02   6.50785132e-02
   5.16393836e-02   4.05634036e-02   4.33328248e-02   3.59174728e-02
  -9.40747148e-02  -1.00249261e-01   3.92326864e-02  -1.02162152e-01
   1.11504561e-02   5.20214231e-02  -9.51513184e-03   8.30358924e-03
  -7.12003048e-02   1.40510476e-01  -1.49001290e-02  -1.54843942e-01
  -1.17387325e-01   2.95322843e-03   7.48798623e-02   7.76931734e-02
   3.62647636e-03   3.74099804e-02  -1.25890590e-01  -5.80434733e-02
  -1.03830822e-01   3.48429638e-03  -6.69677367e-02   1.

In [204]:
%%time

# Step 3: Save in Pandas.DataFrame
#
# 将 data['matrix.train'] 与 data['matrix.test'] 转换成 Pandas.DataFrame 格式，保存到 df['train'] 和 df['test'] 中（df 为字典格式：String -> DataFrame）

df = {}
csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')
for tpart in ['train', 'test']:
    datadict = {}
    datadict['class'] = data['vec.{}'.format(tpart)]['class']
    datavec = np.array(data['vec.{}'.format(tpart)]['w2v.mean'])
    for col in range(vecsize):
        datadict[col]= datavec[:, col]

    df[tpart] = pd.DataFrame(data=datadict)
    print("See df[{}]".format(tpart))
    display(df[tpart])
    print("\n\n\n")
    # write data in DataFrame into CSV
    csvpath = os.path.join(csvpath_root, '{}-w2v-{}-{}.csv'.format(tpart, embedFrom, modelFrom))
    df[tpart].to_csv(csvpath, columns=df[tpart].columns)
    
print("Step 3 Succeed.")

# 繁琐点：研究如何把 CSR 矩阵中的数据规整好放到 DataFrame 中，并与 Class 一一对应

See df[train]


0         1         2         3         4         5         6  \
0    -0.116876  0.033983  0.030950 -0.042242  0.033010  0.035774 -0.030156   
1    -0.106944  0.028698  0.018356 -0.023065  0.009855  0.023431 -0.000504   
2    -0.106025  0.013320  0.046333 -0.019221  0.056579  0.037451 -0.001478   
3    -0.098518  0.012643  0.057831 -0.033276  0.055667  0.037273 -0.017768   
4    -0.106880  0.023066  0.033355 -0.026325  0.048548  0.032794  0.000838   
5    -0.115496  0.003603  0.051215 -0.015904  0.054078  0.045506 -0.014170   
6    -0.099007  0.014794  0.044544 -0.028178  0.029779  0.008130 -0.015576   
7    -0.113498  0.003352  0.040725 -0.053493  0.014363  0.038982 -0.013571   
8    -0.087977  0.000019  0.049841 -0.039036  0.048831  0.028929  0.001292   
9    -0.072080  0.011728  0.031687 -0.046160  0.015392  0.020370 -0.014864   
10   -0.092933  0.014205  0.042456 -0.036895  0.057273  0.040972 -0.010591   
11   -0.093317  0.014799  0.036265 -0.034092  0.070755 -0.003159 -0.032132   
12   -0.105489  0.001688  0.057110 -0.035069  0.022218  0.022594 -0.004722   
13   -0.111718  0.020124  0.051424 -0.034052  0.045818  0.017149  0.007821   
14   -0.110920  0.025066  0.046369 -0.039282  0.037000  0.015365 -0.022109   
15   -0.101297  0.013497  0.033460 -0.022034  0.012278  0.030038 -0.020486   
16   -0.085684  0.007161  0.036673 -0.035146  0.038113  0.031399 -0.004771   
17   -0.115780  0.029407  0.027378 -0.001929  0.056662  0.063108  0.017764   
18   -0.087986  0.025730  0.036709 -0.041618  0.047347  0.029774  0.001763   
19   -0.084293  0.024897  0.044680 -0.029308  0.035160  0.032077 -0.017226   
20   -0.107781  0.014434  0.059175 -0.034728  0.044236  0.011831 -0.001411   
21   -0.075262  0.019310  0.060751 -0.025655  0.034183  0.010676 -0.002137   
22   -0.089373  0.018367 -0.001354 -0.027300  0.039698  0.037010  0.051772   
23   -0.113860  0.007897  0.040566 -0.032465  0.044944  0.046835 -0.008107   
24   -0.101821  0.007968  0.054912 -0.030905  0.033457  0.019099  0.000435   
25   -0.090276  0.015859  0.034384 -0.031621  0.028986  0.004249 -0.007115   
26   -0.093455  0.011452  0.026761 -0.032768  0.011375  0.030269 -0.003627   
27   -0.077962  0.007315  0.022984 -0.051428  0.025841  0.008582 -0.010960   
28   -0.094812  0.030361  0.053298 -0.035993  0.040674  0.021952 -0.004464   
29   -0.117028  0.015573  0.023880 -0.024324  0.035769  0.018860 -0.007579   
...        ...       ...       ...       ...       ...       ...       ...   
2825 -0.110074  0.024120  0.053276 -0.020377  0.038276  0.039235 -0.017379   
2826 -0.050457  0.034557  0.076265 -0.024334  0.022843  0.041522  0.011836   
2827 -0.105067 -0.016129  0.041349 -0.026893  0.028282  0.004604  0.042097   
2828 -0.098170  0.030866  0.062570  0.004777  0.069855  0.068348 -0.018894   
2829 -0.114362  0.009759  0.039774 -0.022020  0.030173  0.026344 -0.016332   
2830 -0.112097  0.035567  0.078703 -0.037135  0.060209 -0.002094 -0.014001   
2831 -0.129604  0.058151  0.050531 -0.030822  0.014035  0.034233  0.036153   
2832 -0.075964  0.026775  0.050199 -0.036570  0.070577  0.040663 -0.010477   
2833 -0.091611  0.011961  0.034916 -0.050268  0.040659 -0.000870  0.040945   
2834 -0.042429  0.084644  0.007314 -0.047744  0.032638  0.047717  0.023167   
2835 -0.097539  0.008459  0.039085 -0.024829  0.037913  0.006871 -0.009508   
2836 -0.099593  0.005096  0.080635 -0.000037  0.040121  0.043724 -0.020458   
2837 -0.108450  0.020720  0.044558 -0.033252  0.051171  0.033359 -0.000499   
2838 -0.078281  0.027882  0.058173 -0.029840  0.010239  0.031222 -0.014823   
2839 -0.102286  0.037771  0.017173  0.005030  0.034946  0.011280 -0.034909   
2840 -0.051871 -0.006938  0.009600  0.006248  0.000068  0.026365 -0.007443   
2841 -0.094369  0.040484  0.060293 -0.025232  0.013790  0.044788  0.014015   
2842 -0.087663  0.015409  0.037284 -0.039100  0.023053  0.027570 -0.014151   
2843 -0.142789  0.012135  0.055778 -0.034622  0.073733  0.050113 -0.010781   
2844 -0.084787  0.027595  0.072316 





See df[test]


0         1         2         3         4         5         6  \
0    -0.109175  0.006434  0.052499 -0.035539  0.038042  0.018722 -0.021271   
1    -0.086023  0.010532  0.035806 -0.040836  0.001932  0.040264 -0.030591   
2    -0.100463  0.017651  0.039525 -0.041685  0.015738  0.011001 -0.007462   
3    -0.099581  0.019049  0.059957 -0.031027  0.070112  0.034792 -0.003536   
4    -0.101563  0.012229  0.047215 -0.022962  0.049003  0.006819 -0.019644   
5    -0.090941  0.031712  0.027228 -0.032390  0.019586  0.018775 -0.001527   
6    -0.091229  0.019519  0.055969 -0.043914  0.028017  0.020788 -0.000473   
7    -0.084787  0.027582  0.035511 -0.017268  0.010101  0.015533 -0.015024   
8    -0.106846  0.024212  0.025683 -0.037574  0.034163  0.034421 -0.000292   
9    -0.086679  0.009507  0.031419 -0.043341  0.038208  0.027166 -0.013665   
10   -0.089644  0.009640  0.034998 -0.039874  0.017386  0.018077 -0.006372   
11   -0.094009  0.026807  0.069452 -0.032321  0.063230  0.012426  0.001792   
12   -0.106491  0.010946  0.036617 -0.038633  0.029004  0.025561 -0.024386   
13   -0.090587  0.009936  0.041014 -0.035999  0.043696  0.026375 -0.002212   
14   -0.088855  0.017651  0.040565 -0.024751  0.031132 -0.001691 -0.021980   
15   -0.108579  0.019245  0.055803 -0.039393  0.043993  0.018905 -0.006326   
16   -0.093750  0.010556  0.029355 -0.034517  0.032362  0.033468 -0.025526   
17   -0.087161  0.012966  0.034233 -0.045521  0.024968  0.032481 -0.002485   
18   -0.097103  0.028878  0.061511 -0.030739  0.051034  0.047497  0.013819   
19   -0.097911  0.008437  0.036912 -0.039693  0.043369  0.012843 -0.002162   
20   -0.081547  0.025022  0.034068 -0.040865  0.032901  0.016171 -0.009805   
21   -0.119115  0.004851  0.042861 -0.040141  0.050774  0.001565  0.008106   
22   -0.100857  0.032221  0.062815 -0.019085  0.036776  0.043971 -0.014102   
23   -0.077599  0.022086  0.043817 -0.034852  0.026236  0.017556 -0.015942   
24   -0.120233  0.020982  0.027413 -0.041769  0.010057  0.001111 -0.011993   
25   -0.100673  0.008794  0.046477 -0.052999  0.067213  0.023600  0.002969   
26   -0.080068  0.010614  0.037057 -0.043262  0.027771  0.020673 -0.013138   
27   -0.114017  0.005926  0.067333 -0.081252  0.034526  0.009147 -0.022762   
28   -0.094963  0.029234  0.046690 -0.030781  0.019186  0.028773 -0.034097   
29   -0.136973 -0.011892  0.092195 -0.027608  0.076468  0.044459 -0.007411   
...        ...       ...       ...       ...       ...       ...       ...   
1870 -0.115278  0.026628  0.065120 -0.015157  0.056583  0.018031 -0.011895   
1871 -0.105987  0.023885  0.052162 -0.027437  0.076228  0.032918  0.021685   
1872 -0.099401  0.027140  0.050081 -0.049412  0.050426  0.028618 -0.017552   
1873 -0.114409  0.036388  0.045354 -0.022429  0.062000  0.020990 -0.013065   
1874 -0.115604  0.023691  0.046045 -0.031095  0.049060  0.025040 -0.014753   
1875 -0.107353  0.001912  0.044000 -0.055892  0.022758  0.011762 -0.015686   
1876 -0.120111  0.029435  0.043347 -0.023495  0.038399  0.033503 -0.021067   
1877 -0.104556  0.019725  0.059125 -0.021940  0.072773  0.012484 -0.005390   
1878 -0.106313  0.020710  0.092160 -0.029120  0.094085  0.044040 -0.014370   
1879 -0.113749  0.009800  0.023957 -0.031312  0.050404  0.023293 -0.016088   
1880 -0.060950 -0.000150  0.045897 -0.026509  0.037216  0.031371  0.003306   
1881 -0.109297  0.014944  0.100758 -0.069911  0.050822  0.000329 -0.025563   
1882 -0.066406  0.012496  0.030392 -0.025592  0.030608  0.066513 -0.023931   
1883 -0.102071  0.030640  0.065684 -0.029501  0.087805  0.027266 -0.006332   
1884 -0.117992  0.015905  0.047474 -0.022354  0.066168  0.016856 -0.012249   
1885 -0.090418  0.027270  0.018791 -0.025679  0.037285  0.042868 -0.012701   
1886 -0.104352  0.027657  0.079303 -0.045221  0.052252  0.025729 -0.017518   
1887 -0.142060  0.007109  0.043763 -0.044013  0.088198  0.021909  0.016344   
1888 -0.091715  0.011951  0.039913 -0.042615  0.034609  0.040580 -0.002716   
1889 -0.104954  0.029700  0.056095 





Step 3 Succeed.
CPU times: user 2.14 s, sys: 40 ms, total: 2.18 s
Wall time: 2.86 s


In [205]:
%%time

# if wanna read data from CSV file

df = {}

for tpart in ['train', 'test']:
    csvpath = os.path.join(
        csvpath_root, '{}-w2v-{}-{}.csv'.format(
            tpart, embedFrom, modelFrom
        )
    )
    if os.path.exists(csvpath):
        df[tpart] = pd.DataFrame.from_csv(csvpath)
        df[tpart] = df[tpart].sample(frac=1)
        df[tpart].reset_index(drop=True, inplace=True)
        print("read {} successfully".format(tpart))
        display(df[tpart])

read train successfully


0         1         2         3         4         5         6  \
0    -0.102856  0.036089  0.045112 -0.024410  0.045801  0.025042 -0.017396   
1    -0.089879  0.018595  0.033348 -0.034271  0.051995  0.031616 -0.028541   
2    -0.096920  0.031071  0.032962  0.026218  0.023096  0.052752  0.006651   
3    -0.074621  0.020761  0.032951  0.007336  0.034159  0.019508 -0.003822   
4    -0.093792  0.023535  0.048847 -0.036319  0.073383  0.017483 -0.003060   
5    -0.095458  0.016303  0.053389 -0.042542  0.024726  0.018404 -0.015711   
6    -0.072861  0.004685  0.084253 -0.041709 -0.001089  0.033984 -0.018489   
7    -0.081550  0.013147  0.071630 -0.034115  0.004887  0.036768 -0.007111   
8    -0.099867  0.027510  0.046250 -0.010917  0.059423  0.023384 -0.034621   
9    -0.110281  0.025558  0.059280 -0.022295  0.053129  0.026960  0.017374   
10   -0.099773  0.040300  0.044304 -0.040847  0.036465  0.029940  0.000914   
11   -0.100183  0.032655  0.038119 -0.039813  0.055256  0.029826 -0.015288   
12   -0.091429  0.013493  0.042521 -0.024909  0.036315  0.031186 -0.011103   
13   -0.120363  0.026458  0.049438 -0.042692  0.052110  0.028116 -0.019341   
14   -0.102096  0.019407  0.052083 -0.033198  0.050701  0.034167 -0.013596   
15   -0.094708  0.019170  0.038519 -0.033945  0.041238  0.039762  0.003360   
16   -0.100582  0.013009  0.055997 -0.045982  0.038896  0.011627 -0.026275   
17   -0.110591  0.017627  0.026135 -0.021253  0.046227  0.029210 -0.009805   
18   -0.095990  0.010582  0.021786 -0.027738  0.011144  0.034422 -0.005171   
19   -0.092146  0.027806  0.033425 -0.037793  0.032772  0.019343 -0.012869   
20   -0.108314  0.028968  0.056565 -0.030039  0.056083  0.001707  0.003326   
21   -0.053999 -0.004960  0.049359  0.007085 -0.001480  0.030026 -0.007340   
22   -0.099877  0.026690  0.040733 -0.037452  0.040852  0.020388 -0.003111   
23   -0.093340  0.017623  0.043988 -0.020963  0.054426  0.021336 -0.020340   
24   -0.109836  0.029576  0.055647 -0.041508  0.050535  0.022747 -0.013897   
25   -0.108084  0.024011  0.043130  0.000450  0.030553  0.024688 -0.000068   
26   -0.108601  0.019265  0.043284  0.004264  0.015576  0.018556 -0.005313   
27   -0.099467  0.011812  0.053106 -0.036702  0.051050  0.016365 -0.006598   
28   -0.120763  0.025442  0.041608 -0.025878  0.035143  0.014850 -0.005317   
29   -0.140004  0.026525  0.073211 -0.007022  0.037162  0.033897 -0.011010   
...        ...       ...       ...       ...       ...       ...       ...   
2825 -0.085350  0.009964  0.038722 -0.036405  0.020088  0.028390 -0.016293   
2826 -0.088661  0.028551  0.037714 -0.029293  0.039499  0.012202 -0.009779   
2827 -0.096564  0.016660  0.029858 -0.014043  0.062316  0.033363 -0.010089   
2828 -0.099520  0.010452  0.034982 -0.026064  0.025815  0.022942 -0.011872   
2829 -0.087936  0.012345  0.032704 -0.003457  0.039252  0.006486 -0.018737   
2830 -0.067472  0.015094  0.030080 -0.038561  0.052669  0.026478  0.007562   
2831 -0.074066  0.012710  0.029432 -0.028025  0.038771  0.062711  0.021953   
2832 -0.058590  0.028756  0.010799 -0.043596 -0.003104  0.050020  0.007100   
2833 -0.143724 -0.007099  0.045374 -0.006772  0.012948  0.020199 -0.025705   
2834 -0.084238  0.041033  0.028511 -0.030412  0.011652  0.039836 -0.012640   
2835 -0.098458  0.013063  0.058486 -0.014839  0.058654  0.023653 -0.011271   
2836 -0.080487  0.026017  0.058041 -0.011163  0.082336  0.059558 -0.006461   
2837 -0.085549  0.011846  0.062991 -0.019410  0.031193  0.038732 -0.009713   
2838 -0.094875  0.014228  0.024702 -0.031046  0.026447  0.023595 -0.008570   
2839 -0.097106  0.017759  0.047875 -0.026630  0.049450  0.030103  0.003340   
2840 -0.092933  0.014205  0.042456 -0.036895  0.057273  0.040972 -0.010591   
2841 -0.090797  0.011231  0.048104 -0.048795  0.050362  0.031691 -0.035703   
2842 -0.118895  0.039402  0.042773 -0.036090  0.043086  0.026687 -0.000992   
2843 -0.074653  0.014347  0.040528 -0.016396  0.042238  0.038079 -0.010476   
2844 -0.088666  0.029093  0.016950 

read test successfully


0         1         2         3         4         5         6  \
0    -0.085709  0.013900  0.040913 -0.032098  0.070461  0.038555 -0.023598   
1    -0.062669  0.049578  0.052611  0.038462  0.013200  0.062592 -0.012973   
2    -0.100344  0.002995  0.033974 -0.028160  0.022248  0.025789  0.003818   
3    -0.083875  0.030184  0.075929 -0.046418  0.107492  0.030632 -0.003442   
4    -0.091570  0.027541  0.059540 -0.057670  0.075479  0.030094 -0.025848   
5    -0.116354  0.022108  0.056102 -0.030260  0.060148  0.022880 -0.019455   
6    -0.084998  0.011209  0.026111 -0.047338  0.009979  0.025555  0.004694   
7    -0.071892  0.003674  0.040130 -0.032850  0.012505  0.048784 -0.000445   
8    -0.095329  0.012222  0.022365 -0.008072  0.044362  0.049514 -0.003086   
9    -0.132657  0.037954  0.041172 -0.072653  0.036338  0.005063 -0.019449   
10   -0.086673  0.012163  0.023874 -0.032955  0.030119  0.040720  0.004132   
11   -0.094607  0.020728  0.035021 -0.049352  0.043070  0.018622 -0.009801   
12   -0.087405  0.021858  0.037499 -0.035391  0.019837  0.019424 -0.019592   
13   -0.105932  0.031943  0.053977 -0.041679  0.039025  0.026666 -0.006545   
14   -0.071635  0.009367  0.047044 -0.045089  0.043404  0.046967  0.012439   
15   -0.103166  0.017520  0.052380 -0.035798  0.053949  0.016772  0.001801   
16   -0.100633  0.021347  0.051033 -0.028051  0.047246  0.009879 -0.022681   
17   -0.120200  0.026366  0.037835  0.004106  0.043216  0.007729 -0.011818   
18   -0.085731 -0.010968  0.026906 -0.030514  0.040848  0.055405 -0.032131   
19   -0.103426  0.013561  0.055749 -0.045425  0.040311  0.018632 -0.031228   
20   -0.102012  0.021022  0.073075 -0.035640  0.054719  0.027189 -0.007187   
21   -0.086888  0.004122  0.071440 -0.013964  0.113314  0.036496 -0.072733   
22   -0.086037  0.014691  0.027867 -0.056992  0.042826  0.045405 -0.014361   
23   -0.118926  0.020172  0.040510 -0.028689  0.070933  0.014916 -0.019428   
24   -0.077537  0.023009  0.031781 -0.008733  0.045397  0.028182 -0.030995   
25   -0.091240  0.002517  0.040142 -0.033661  0.069536  0.032868 -0.017920   
26   -0.078242  0.025759  0.029216 -0.035897  0.056789  0.033643 -0.008109   
27   -0.110104  0.015184  0.058493 -0.039677  0.054985  0.014252 -0.015729   
28   -0.109297  0.014944  0.100758 -0.069911  0.050822  0.000329 -0.025563   
29   -0.093279  0.026482  0.038887 -0.028739  0.024635  0.007678 -0.024840   
...        ...       ...       ...       ...       ...       ...       ...   
1870 -0.105541  0.008055  0.041486 -0.042083  0.054791  0.024400 -0.009834   
1871 -0.090611  0.008233  0.043248 -0.039276  0.055188  0.058894 -0.009112   
1872 -0.109114  0.010124  0.035286 -0.033904  0.052583  0.042642 -0.018470   
1873 -0.100967  0.006456  0.055505 -0.020248  0.055378  0.014799 -0.001257   
1874 -0.107586  0.018559  0.045530 -0.031981  0.067040  0.038532  0.006807   
1875 -0.108077  0.029921  0.011758 -0.031467  0.045488  0.040208  0.030883   
1876 -0.098642  0.004438  0.047239 -0.036384  0.062939  0.041966 -0.011789   
1877 -0.067906  0.027816  0.031383 -0.005640  0.022747  0.031838 -0.038672   
1878 -0.127381  0.035334  0.097557 -0.021739  0.063239  0.047456 -0.011989   
1879 -0.118818  0.015940  0.051373 -0.032204  0.054785  0.017959 -0.020027   
1880 -0.119149  0.011714  0.044667 -0.025542  0.032846  0.004457 -0.011919   
1881 -0.085915  0.061445  0.065203 -0.021673  0.044704  0.021952 -0.001365   
1882 -0.171399  0.012613  0.074639 -0.053495  0.128123  0.034771 -0.007818   
1883 -0.109087  0.014137  0.062743 -0.020553  0.055124  0.022013 -0.001307   
1884 -0.108113  0.007017  0.069125 -0.027628  0.067686  0.050472 -0.012449   
1885 -0.085580  0.020618  0.030408 -0.030175  0.032468  0.024187 -0.012410   
1886 -0.118802  0.019507  0.042864 -0.034820  0.033518  0.023801 -0.014396   
1887 -0.106649  0.008893  0.048954 -0.021979  0.045183  0.021419  0.001448   
1888 -0.117722  0.018892  0.045227 -0.028798  0.050261  0.026704 -0.010060   
1889 -0.101858  0.010579  0.043230 

CPU times: user 924 ms, sys: 28 ms, total: 952 ms
Wall time: 1.18 s


###### SVM classifier(TensorFlow + corpus)

In [206]:
%%time

# Step 5.1.1: SVM

# if 'TFIDF' == modelChoice:

#train
X_train = df['train'].drop('class', axis=1)
y_train = df['train']['class']
#test
X_test = df['test'].drop('class', axis=1)
y_test_true = df['test']['class']

# else:
#     #train
#     X_train = df_new['train']['x']
#     y_train = df_new['train']['y']
#     #test
#     X_test = df_new['test']['x']
#     y_test_true = df_new['test']['y']

clf = LinearSVC()
clf.fit(X_train, y_train)

print("Step 4 finished")

Step 4 finished
CPU times: user 2.19 s, sys: 8 ms, total: 2.2 s
Wall time: 2.25 s


In [207]:
%%time
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score

# Step 5.1.2: Test
y_test_pred = clf.predict(X_test)
print(accuracy_score(y_test_true, y_test_pred))
print(f1_score(y_test_true, y_test_pred, average='macro'))
print(f1_score(y_test_true, y_test_pred, average='micro'))

0.766842105263
0.762434507233
0.766842105263
CPU times: user 20 ms, sys: 4 ms, total: 24 ms
Wall time: 132 ms


###### DNN classifier(TensorFlow + corpus)

In [208]:
%%time

# Step 4: One-hot representation for labels

csvpath_root = os.path.join(paths['dir.dataroot'], 'data_CSV')

lb = LabelBinarizer()
lb.fit(df['train']['class'])

df_new = {}
for tpart in ['train', 'test']:
    labels = lb.transform(df[tpart]['class'])
    labelsDf = pd.DataFrame(labels, columns=["class-{}".format(i) for i in range(len(lb.classes_))])
    df_new[tpart] = {}
    df_new[tpart]['y'] = labelsDf
    df_new[tpart]['x'] = df[tpart].drop('class', axis=1)
    df_new[tpart]['all'] = df_new[tpart]['x'].join(df_new[tpart]['y'])
    #save in CSV
    for subpart in ['x', 'y', 'all']:
        csvpath = os.path.join(csvpath_root, "{}-cleanLabels-{}-{}.csv".format(tpart, subpart, modelFrom))
        df_new[tpart][subpart].to_csv(csvpath)
    
print("label cleaning succussfully")

label cleaning succussfully
CPU times: user 3.86 s, sys: 72 ms, total: 3.93 s
Wall time: 4.55 s


In [209]:
%%time

## Step 5 : Train the classifier

COL_OUTCOME = 'class'
COL_FEATURE = [str(col) for col in list(df['train'].columns) if col != COL_OUTCOME]

cls2num = {cls:ind for (ind, cls) in enumerate(df['train']['class'].unique())}

def my_input_fn(dataset):
    # Save dataset in tf format
    feature_cols = {
        str(col): tf.constant(
            df[dataset][str(col)].values
        )
        for col in COL_FEATURE
    }
    labels = tf.constant([cls2num[labelname] for labelname in df[dataset][COL_OUTCOME].values])
    # Returns the feature columns and labels in tf format
    return feature_cols, labels

feature_columns = [tf.contrib.layers.real_valued_column(column_name=str(col)) for col in COL_FEATURE]
clf = tf.contrib.learn.DNNClassifier(
    feature_columns=feature_columns, 
    hidden_units=[512], 
    n_classes=len(df['train']['class'].unique())
)

clf.fit(input_fn=lambda: my_input_fn('train'), steps=2000)

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_num_ps_replicas': 0, '_keep_checkpoint_max': 5, '_tf_random_seed': None, '_task_type': None, '_environment': 'local', '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f14cca7e9d0>, '_tf_config': gpu_options {
  per_process_gpu_memory_fraction: 1.0
}
, '_task_id': 0, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_evaluation_master': '', '_keep_checkpoint_every_n_hours': 10000, '_master': ''}


Instructions for updating:
Please switch to tf.summary.scalar. Note that tf.summary.scalar uses the node name instead of the tag. This means that TensorFlow will automatically de-duplicate summary names based on the scope they are created in. Also, passing a tensor or list of tags to a scalar summary op is no longer supported.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/tmpnd64UN/model.ckpt.
INFO:tensorflow:loss = 1.60874, step = 1
INFO:tensorflow:global_step/sec: 11.2287
INFO:tensorflow:loss = 1.57178, step = 101
INFO:tensorflow:global_step/sec: 11.9962
INFO:tensorflow:loss = 1.52732, step = 201
INFO:tensorflow:global_step/sec: 12.0191
INFO:tensorflow:loss = 1.45977, step = 301
INFO:tensorflow:global_step/sec: 12.1779
INFO:tensorflow:loss = 1.37355, step = 401
INFO:tensorflow:global_step/sec: 12.2203
INFO:tensorflow:loss = 1.2847, step = 501
INFO:tensorflow:global_step/sec: 12.0566
INFO:tensorflow:loss = 1.20312, step = 601
INFO:tenso

In [210]:
%%time

## Step 6: Evaluate

accuracy_score = clf.evaluate(input_fn=lambda: my_input_fn('test'), steps=df['test'].shape[0])['accuracy']
print("Test Accuracy by TensorFlow: {}".format(accuracy_score))

X_tensor_test, yt = my_input_fn('test')
tensorPredCls = list(clf.predict(input_fn=lambda: my_input_fn('test')))
num2cls = {v:k for (k, v) in cls2num.items()}
tensorPredClsStr = [num2cls[i] for i in tensorPredCls]
y_test_true = df['test']['class']
print('Test Accuracy by Scikit-learn: ', f1_score(y_test_true, tensorPredClsStr, average='micro'))

Instructions for updating:
Please switch to tf.summary.scalar. Note that tf.summary.scalar uses the node name instead of the tag. This means that TensorFlow will automatically de-duplicate summary names based on the scope they are created in. Also, passing a tensor or list of tags to a scalar summary op is no longer supported.
INFO:tensorflow:Starting evaluation at 2017-05-14-01:44:47
INFO:tensorflow:Evaluation [1/1900]
INFO:tensorflow:Evaluation [2/1900]
INFO:tensorflow:Evaluation [3/1900]
INFO:tensorflow:Evaluation [4/1900]
INFO:tensorflow:Evaluation [5/1900]
INFO:tensorflow:Evaluation [6/1900]
INFO:tensorflow:Evaluation [7/1900]
INFO:tensorflow:Evaluation [8/1900]
INFO:tensorflow:Evaluation [9/1900]
INFO:tensorflow:Evaluation [10/1900]
INFO:tensorflow:Evaluation [11/1900]
INFO:tensorflow:Evaluation [12/1900]
INFO:tensorflow:Evaluation [13/1900]
INFO:tensorflow:Evaluation [14/1900]
INFO:tensorflow:Evaluation [15/1900]
INFO:tensorflow:Evaluation [16/1900]
INFO:tensorflow:Evaluation [1

INFO:tensorflow:Evaluation [73/1900]
INFO:tensorflow:Evaluation [74/1900]
INFO:tensorflow:Evaluation [75/1900]
INFO:tensorflow:Evaluation [76/1900]
INFO:tensorflow:Evaluation [77/1900]
INFO:tensorflow:Evaluation [78/1900]
INFO:tensorflow:Evaluation [79/1900]
INFO:tensorflow:Evaluation [80/1900]
INFO:tensorflow:Evaluation [81/1900]
INFO:tensorflow:Evaluation [82/1900]
INFO:tensorflow:Evaluation [83/1900]
INFO:tensorflow:Evaluation [84/1900]
INFO:tensorflow:Evaluation [85/1900]
INFO:tensorflow:Evaluation [86/1900]
INFO:tensorflow:Evaluation [87/1900]
INFO:tensorflow:Evaluation [88/1900]
INFO:tensorflow:Evaluation [89/1900]
INFO:tensorflow:Evaluation [90/1900]
INFO:tensorflow:Evaluation [91/1900]
INFO:tensorflow:Evaluation [92/1900]
INFO:tensorflow:Evaluation [93/1900]
INFO:tensorflow:Evaluation [94/1900]
INFO:tensorflow:Evaluation [95/1900]
INFO:tensorflow:Evaluation [96/1900]
INFO:tensorflow:Evaluation [97/1900]
INFO:tensorflow:Evaluation [98/1900]
INFO:tensorflow:Evaluation [99/1900]
I

INFO:tensorflow:Evaluation [290/1900]
INFO:tensorflow:Evaluation [291/1900]
INFO:tensorflow:Evaluation [292/1900]
INFO:tensorflow:Evaluation [293/1900]
INFO:tensorflow:Evaluation [294/1900]
INFO:tensorflow:Evaluation [295/1900]
INFO:tensorflow:Evaluation [296/1900]
INFO:tensorflow:Evaluation [297/1900]
INFO:tensorflow:Evaluation [298/1900]
INFO:tensorflow:Evaluation [299/1900]
INFO:tensorflow:Evaluation [300/1900]
INFO:tensorflow:Evaluation [301/1900]
INFO:tensorflow:Evaluation [302/1900]
INFO:tensorflow:Evaluation [303/1900]
INFO:tensorflow:Evaluation [304/1900]
INFO:tensorflow:Evaluation [305/1900]
INFO:tensorflow:Evaluation [306/1900]
INFO:tensorflow:Evaluation [307/1900]
INFO:tensorflow:Evaluation [308/1900]
INFO:tensorflow:Evaluation [309/1900]
INFO:tensorflow:Evaluation [310/1900]
INFO:tensorflow:Evaluation [311/1900]
INFO:tensorflow:Evaluation [312/1900]
INFO:tensorflow:Evaluation [313/1900]
INFO:tensorflow:Evaluation [314/1900]
INFO:tensorflow:Evaluation [315/1900]
INFO:tensorf

INFO:tensorflow:Evaluation [506/1900]
INFO:tensorflow:Evaluation [507/1900]
INFO:tensorflow:Evaluation [508/1900]
INFO:tensorflow:Evaluation [509/1900]
INFO:tensorflow:Evaluation [510/1900]
INFO:tensorflow:Evaluation [511/1900]
INFO:tensorflow:Evaluation [512/1900]
INFO:tensorflow:Evaluation [513/1900]
INFO:tensorflow:Evaluation [514/1900]
INFO:tensorflow:Evaluation [515/1900]
INFO:tensorflow:Evaluation [516/1900]
INFO:tensorflow:Evaluation [517/1900]
INFO:tensorflow:Evaluation [518/1900]
INFO:tensorflow:Evaluation [519/1900]
INFO:tensorflow:Evaluation [520/1900]
INFO:tensorflow:Evaluation [521/1900]
INFO:tensorflow:Evaluation [522/1900]
INFO:tensorflow:Evaluation [523/1900]
INFO:tensorflow:Evaluation [524/1900]
INFO:tensorflow:Evaluation [525/1900]
INFO:tensorflow:Evaluation [526/1900]
INFO:tensorflow:Evaluation [527/1900]
INFO:tensorflow:Evaluation [528/1900]
INFO:tensorflow:Evaluation [529/1900]
INFO:tensorflow:Evaluation [530/1900]
INFO:tensorflow:Evaluation [531/1900]
INFO:tensorf

INFO:tensorflow:Evaluation [722/1900]
INFO:tensorflow:Evaluation [723/1900]
INFO:tensorflow:Evaluation [724/1900]
INFO:tensorflow:Evaluation [725/1900]
INFO:tensorflow:Evaluation [726/1900]
INFO:tensorflow:Evaluation [727/1900]
INFO:tensorflow:Evaluation [728/1900]
INFO:tensorflow:Evaluation [729/1900]
INFO:tensorflow:Evaluation [730/1900]
INFO:tensorflow:Evaluation [731/1900]
INFO:tensorflow:Evaluation [732/1900]
INFO:tensorflow:Evaluation [733/1900]
INFO:tensorflow:Evaluation [734/1900]
INFO:tensorflow:Evaluation [735/1900]
INFO:tensorflow:Evaluation [736/1900]
INFO:tensorflow:Evaluation [737/1900]
INFO:tensorflow:Evaluation [738/1900]
INFO:tensorflow:Evaluation [739/1900]
INFO:tensorflow:Evaluation [740/1900]
INFO:tensorflow:Evaluation [741/1900]
INFO:tensorflow:Evaluation [742/1900]
INFO:tensorflow:Evaluation [743/1900]
INFO:tensorflow:Evaluation [744/1900]
INFO:tensorflow:Evaluation [745/1900]
INFO:tensorflow:Evaluation [746/1900]
INFO:tensorflow:Evaluation [747/1900]
INFO:tensorf

...

INFO:tensorflow:Evaluation [1150/1900]
INFO:tensorflow:Evaluation [1151/1900]
INFO:tensorflow:Evaluation [1152/1900]
INFO:tensorflow:Evaluation [1153/1900]
INFO:tensorflow:Evaluation [1154/1900]
INFO:tensorflow:Evaluation [1155/1900]
INFO:tensorflow:Evaluation [1156/1900]
INFO:tensorflow:Evaluation [1157/1900]
INFO:tensorflow:Evaluation [1158/1900]
INFO:tensorflow:Evaluation [1159/1900]
INFO:tensorflow:Evaluation [1160/1900]
INFO:tensorflow:Evaluation [1161/1900]
INFO:tensorflow:Evaluation [1162/1900]
INFO:tensorflow:Evaluation [1163/1900]
INFO:tensorflow:Evaluation [1164/1900]
INFO:tensorflow:Evaluation [1165/1900]
INFO:tensorflow:Evaluation [1166/1900]
INFO:tensorflow:Evaluation [1167/1900]
INFO:tensorflow:Evaluation [1168/1900]
INFO:tensorflow:Evaluation [1169/1900]
INFO:tensorflow:Evaluation [1170/1900]
INFO:tensorflow:Evaluation [1171/1900]
INFO:tensorflow:Evaluation [1172/1900]
INFO:tensorflow:Evaluation [1173/1900]
INFO:tensorflow:Evaluation [1174/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1361/1900]
INFO:tensorflow:Evaluation [1362/1900]
INFO:tensorflow:Evaluation [1363/1900]
INFO:tensorflow:Evaluation [1364/1900]
INFO:tensorflow:Evaluation [1365/1900]
INFO:tensorflow:Evaluation [1366/1900]
INFO:tensorflow:Evaluation [1367/1900]
INFO:tensorflow:Evaluation [1368/1900]
INFO:tensorflow:Evaluation [1369/1900]
INFO:tensorflow:Evaluation [1370/1900]
INFO:tensorflow:Evaluation [1371/1900]
INFO:tensorflow:Evaluation [1372/1900]
INFO:tensorflow:Evaluation [1373/1900]
INFO:tensorflow:Evaluation [1374/1900]
INFO:tensorflow:Evaluation [1375/1900]
INFO:tensorflow:Evaluation [1376/1900]
INFO:tensorflow:Evaluation [1377/1900]
INFO:tensorflow:Evaluation [1378/1900]
INFO:tensorflow:Evaluation [1379/1900]
INFO:tensorflow:Evaluation [1380/1900]
INFO:tensorflow:Evaluation [1381/1900]
INFO:tensorflow:Evaluation [1382/1900]
INFO:tensorflow:Evaluation [1383/1900]
INFO:tensorflow:Evaluation [1384/1900]
INFO:tensorflow:Evaluation [1385/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1572/1900]
INFO:tensorflow:Evaluation [1573/1900]
INFO:tensorflow:Evaluation [1574/1900]
INFO:tensorflow:Evaluation [1575/1900]
INFO:tensorflow:Evaluation [1576/1900]
INFO:tensorflow:Evaluation [1577/1900]
INFO:tensorflow:Evaluation [1578/1900]
INFO:tensorflow:Evaluation [1579/1900]
INFO:tensorflow:Evaluation [1580/1900]
INFO:tensorflow:Evaluation [1581/1900]
INFO:tensorflow:Evaluation [1582/1900]
INFO:tensorflow:Evaluation [1583/1900]
INFO:tensorflow:Evaluation [1584/1900]
INFO:tensorflow:Evaluation [1585/1900]
INFO:tensorflow:Evaluation [1586/1900]
INFO:tensorflow:Evaluation [1587/1900]
INFO:tensorflow:Evaluation [1588/1900]
INFO:tensorflow:Evaluation [1589/1900]
INFO:tensorflow:Evaluation [1590/1900]
INFO:tensorflow:Evaluation [1591/1900]
INFO:tensorflow:Evaluation [1592/1900]
INFO:tensorflow:Evaluation [1593/1900]
INFO:tensorflow:Evaluation [1594/1900]
INFO:tensorflow:Evaluation [1595/1900]
INFO:tensorflow:Evaluation [1596/1900]
INFO:tensorflow:Evaluatio

INFO:tensorflow:Evaluation [1783/1900]
INFO:tensorflow:Evaluation [1784/1900]
INFO:tensorflow:Evaluation [1785/1900]
INFO:tensorflow:Evaluation [1786/1900]
INFO:tensorflow:Evaluation [1787/1900]
INFO:tensorflow:Evaluation [1788/1900]
INFO:tensorflow:Evaluation [1789/1900]
INFO:tensorflow:Evaluation [1790/1900]
INFO:tensorflow:Evaluation [1791/1900]
INFO:tensorflow:Evaluation [1792/1900]
INFO:tensorflow:Evaluation [1793/1900]
INFO:tensorflow:Evaluation [1794/1900]
INFO:tensorflow:Evaluation [1795/1900]
INFO:tensorflow:Evaluation [1796/1900]
INFO:tensorflow:Evaluation [1797/1900]
INFO:tensorflow:Evaluation [1798/1900]
INFO:tensorflow:Evaluation [1799/1900]
INFO:tensorflow:Evaluation [1800/1900]
INFO:tensorflow:Evaluation [1801/1900]
INFO:tensorflow:Evaluation [1802/1900]
INFO:tensorflow:Evaluation [1803/1900]
INFO:tensorflow:Evaluation [1804/1900]
INFO:tensorflow:Evaluation [1805/1900]
INFO:tensorflow:Evaluation [1806/1900]
INFO:tensorflow:Evaluation [1807/1900]
INFO:tensorflow:Evaluatio

Test Accuracy by Scikit-learn:  0.69
CPU times: user 9min 13s, sys: 4.73 s, total: 9min 17s
Wall time: 1min 29s


###### CNN classifier(TensorFlow + corpus)

In [211]:
%%time

import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

sess = tf.InteractiveSession()

COL_OUTCOME = 'class'
COL_FEATURE = [col for col in list(df['train'].columns) if col != COL_OUTCOME]

# cls2num = {cls:ind for (ind, cls) in enumerate(df['train']['class'].unique())}

count_feature = len(COL_FEATURE)
count_class = len(df['train']['class'].unique())

x = tf.placeholder(tf.float32, shape=[None, 784], name='x')
y_ = tf.placeholder(tf.float32, shape=[None, count_class], name='y_')

W = tf.Variable(tf.zeros([count_feature, count_class]))
b = tf.Variable(tf.zeros([count_class]))
y = tf.matmul(x, W) + b

# cross_entropy = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(labels=y_, logits=y))

def weight_variable(shape):
    initial = tf.truncated_normal(shape, stddev=0.1)
    return tf.Variable(initial)

def bias_variable(shape):
    initial = tf.constant(0.1, shape=shape)
    return tf.Variable(initial)

def conv2d(x, W):
    return tf.nn.conv2d(x, W, strides=[1, 1, 1, 1], padding='SAME')

def max_pool_2x2(x):
    return tf.nn.max_pool(x, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')

W_conv1 = weight_variable([5, 5, 1, 32])
b_conv1 = bias_variable([32])
x_text = tf.reshape(x, [-1, 28, 28, 1])
h_conv1 = tf.nn.relu(conv2d(x_text, W_conv1) + b_conv1)
h_pool1 = max_pool_2x2(h_conv1)

W_conv2 = weight_variable([5, 5, 32, 64])
b_conv2 = bias_variable([64])
h_conv2 = tf.nn.relu(conv2d(h_pool1, W_conv2) + b_conv2)
h_pool2 = max_pool_2x2(h_conv2)

W_fc1 = weight_variable([7 * 7 * 64, 1024])
b_fc1 = bias_variable([1024])

h_pool2_flat = tf.reshape(h_pool2, [-1, 7 * 7 * 64])
h_fc1 = tf.nn.relu(tf.matmul(h_pool2_flat, W_fc1) + b_fc1)

keep_prob = tf.placeholder(tf.float32, name='keep_prob')
h_fc1_drop = tf.nn.dropout(h_fc1, keep_prob)

W_fc2 = weight_variable([1024, count_class])
b_fc2 = bias_variable([count_class])

y_conv = tf.matmul(h_fc1_drop, W_fc2) + b_fc2

print("CNN initialization finished")

CNN initialization finished
CPU times: user 40 ms, sys: 0 ns, total: 40 ms
Wall time: 128 ms


In [212]:
%%time

### Start to traini and evaluate the model

cross_entropy = tf.reduce_mean(
    tf.nn.softmax_cross_entropy_with_logits(labels=y_, logits=y_conv))
train_step = tf.train.AdamOptimizer(1e-4).minimize(cross_entropy)
correct_prediction = tf.equal(tf.argmax(y_conv, 1), tf.argmax(y_, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

sess.run(tf.global_variables_initializer())

x_input = df_new['train']['x']
x_input = [np.array([
            np.float32(x_input.iloc[i].values)
        ])
    for i in range(x_input.shape[0])]
y_input = df_new['train']['y']
y_input = [np.array([
            np.float32(y_input.iloc[i].values)
        ])
    for i in range(y_input.shape[0])]
# y_input = [np.array([y_input.iloc[i].values]) for i in range(y_input.shape[0])]

# not use random input

for i in range(df['train'].shape[0] - 50):
    if 0 == i % 100:
        train_accuracy = []
        for j in range(50):
            train_accuracy.append(accuracy.eval(feed_dict={
                    keep_prob: 1,
                    x:  np.array([elem[0] for elem in x_input[i+j:i+j+50]]),#x_input.iloc[i+j].values, #
                    y_: np.array([elem[0] for elem in y_input[i+j:i+j+50]])#y_input.iloc[i+j].values #
                })
            )
        print("step {}, training accuracy {}".format(i, np.mean(train_accuracy)))
    train_step.run(feed_dict={
        keep_prob: 0.5,
        x:  np.array([elem[0] for elem in x_input[i:i+50]]),#x_input.iloc[i].values, #
        y_: np.array([elem[0] for elem in y_input[i:i+50]])#y_input.iloc[i].values#
    })

print("CNN training finished")

step 0, training accuracy 0.188000023365
step 100, training accuracy 0.180399984121
step 200, training accuracy 0.409599989653
step 300, training accuracy 0.482399970293
step 400, training accuracy 0.457200020552
step 500, training accuracy 0.402399927378
step 600, training accuracy 0.383599996567
step 700, training accuracy 0.559599995613
step 800, training accuracy 0.49279999733
step 900, training accuracy 0.458400040865
step 1000, training accuracy 0.594000041485
step 1100, training accuracy 0.546400010586
step 1200, training accuracy 0.595999956131
step 1300, training accuracy 0.656800031662
step 1400, training accuracy 0.738400042057
step 1500, training accuracy 0.557600021362
step 1600, training accuracy 0.60480004549
step 1700, training accuracy 0.583599984646
step 1800, training accuracy 0.600800037384
step 1900, training accuracy 0.6507999897
step 2000, training accuracy 0.793999910355
step 2100, training accuracy 0.631200015545
step 2200, training accuracy 0.733600020409
step

In [213]:
%%time

# Evaluate

x_input = df_new['test']['x']#df_new['test']['x']
x_input = [np.array([
            np.float32(x_input.iloc[i].values)
        ])
    for i in range(x_input.shape[0])]
y_input = df_new['test']['y']#df_new['test']['y']
y_input = [np.array([
            np.float32(y_input.iloc[i].values)
        ])
    for i in range(y_input.shape[0])]

for i in range(df['test'].shape[0] - 50):
    if 0 == i % 100:
        train_accuracy = []
        for j in range(50):
            train_accuracy.append(accuracy.eval(feed_dict={
                    keep_prob: 1,
                    x:  np.array([elem[0] for elem in x_input[i+j:i+j+50]]),#x_input.iloc[i+j].values, #
                    y_: np.array([elem[0] for elem in y_input[i+j:i+j+50]])#y_input.iloc[i+j].values #
                })
            )
        print("step {}, testing accuracy {}".format(i, np.mean(train_accuracy)))

        
print("CNN testing finished")

step 0, testing accuracy 0.665600061417
step 100, testing accuracy 0.600000023842
step 200, testing accuracy 0.609199941158
step 300, testing accuracy 0.561600029469
step 400, testing accuracy 0.722000062466
step 500, testing accuracy 0.772000074387
step 600, testing accuracy 0.748399972916
step 700, testing accuracy 0.624000012875
step 800, testing accuracy 0.529599964619
step 900, testing accuracy 0.729199886322
step 1000, testing accuracy 0.660800039768
step 1100, testing accuracy 0.676400065422
step 1200, testing accuracy 0.694399952888
step 1300, testing accuracy 0.536000013351
step 1400, testing accuracy 0.725200116634
step 1500, testing accuracy 0.678799986839
step 1600, testing accuracy 0.76240003109
step 1700, testing accuracy 0.602800011635
step 1800, testing accuracy 0.668000102043
CNN testing finished
CPU times: user 2min 41s, sys: 728 ms, total: 2min 42s
Wall time: 23.7 s


## 数据总结

In [156]:
import datetime

def timeInFormat(s):
    return str(datetime.timedelta(seconds=s))

In [166]:
tmplist = {}
record_data = {}

tmplist['model'] = [
    6206/float(1000), 6206/float(1000), 6206/float(1000), 
    6979/float(1000), 6979/float(1000), 6979/float(1000), 
    10549/float(1000), 10549/float(1000), 10549/float(1000), 
    32*60+17, 32*60+20, 32*60+20, 
    41142/float(1000), 44892/float(1000), 44892/float(1000),
    2*3600+46*60+50, 2*3600+46+55, 2*3600+46+55,
    15*60+7, 15*60+12, 15*60+12
]

tmplist['train'] = [
    89.2/float(1000), 68.4/float(1000), 222/float(1000), 
    202/float(1000), 12.2/float(1000), 425/float(1000), 
    97.7/float(1000), 7.25/float(1000), 239/float(1000), 
    1.99, 3*60+6, 5*60+52,
    1.25, 3*60+3, 5*60+26,
    2.19, 3*60+5, 5*60+15,
    2.25, 3*60+3, 5*60+20
]
# data['time.train'] = [str(datetime.timedelta(seconds=sec)) for sec in tmplist]

tmplist['evaluate'] = [
    29.9/float(1000), 61.9/float(1000), 29.3/float(1000), 
    16.5/float(1000), 25.5/float(1000), 27.6/float(1000), 
    13.5/float(1000), 13.7/float(1000), 26/float(1000), 
    21.3/float(1000), 1*60+45, 26,
    19.7/float(1000), 1*60+4, 27.1,
    47.5/float(1000), 1*60+41, 27,
    132/float(1000), 1*60+29, 23.7
]
# data['time.evaluate'] = [str(datetime.timedelta(seconds=sec)) for sec in tmplist]


tmplist['all'] = [(x+y+z) for (x, y, z) in zip(tmplist['model'], tmplist['train'], tmplist['evaluate'])]

for phase in ['model', 'train', 'evaluate', 'all'] :
    record_data['time.{}.format'.format(phase)] = [timeInFormat(sec) for sec in tmplist[phase]]
    record_data['time.{}.raw'.format(phase)] = [sec for sec in tmplist[phase]]
    #[('{}'.format(datetime.timedelta(seconds=sec))).split('.')[0] for sec in tmplist[phase]]

tmplist['acc'] = [
    86.16, 82.00, 81.79,
    86.74, 70.79, 73.42,
    59.32, 48.21, 52.05,
    83.05, 80.95, 75.30,
    82.74, 81.84, 78.10,
    84.42, 80.05, 69.86,
    76.68, 69.00, 66.14
]
record_data['accuracy(%)'] = [acc for acc in tmplist['acc']]

record_data['tool'] = [
        'sklearn', 'sklearn', 'sklearn', 
        'sklearn', 'sklearn', 'sklearn', 
        'sklearn', 'sklearn', 'sklearn', 
        'gensim', 'gensim', 'gensim', 
        'gensim', 'gensim', 'gensim',
        'TensorFlow', 'TensorFlow', 'TensorFlow', 
        'TensorFlow', 'TensorFlow', 'TensorFlow'
]

record_data['model.source'] = [
        'Plain', 'Plain', 'Plain', 
        'LSA', 'LSA', 'LSA', 
        'LDA', 'LDA', 'LDA', 
        'text8', 'text8', 'text8', 
        'corpus', 'corpus', 'corpus', 
        'text8', 'text8', 'text8', 
        'corpus', 'corpus', 'corpus'
]

record_data['model.word'] = [
        'BOW-TFIDF', 'BOW-TFIDF', 'BOW-TFIDF', 
        'BOW-TFIDF', 'BOW-TFIDF', 'BOW-TFIDF', 
        'BOW-TFIDF', 'BOW-TFIDF', 'BOW-TFIDF', 
        'Word2Vec', 'Word2Vec', 'Word2Vec', 
        'Word2Vec', 'Word2Vec', 'Word2Vec', 
        'Word2Vec', 'Word2Vec', 'Word2Vec', 
        'Word2Vec', 'Word2Vec', 'Word2Vec', 
]

record_data['model.document'] = [
        'Plain', 'Plain', 'Plain', 
        'LSA', 'LSA', 'LSA', 
        'LDA', 'LDA', 'LDA', 
        'w2v-mean', 'w2v-mean', 'w2v-mean', 
        'w2v-mean', 'w2v-mean', 'w2v-mean', 
        'w2v-mean', 'w2v-mean', 'w2v-mean', 
        'w2v-mean', 'w2v-mean', 'w2v-mean', 
]

record_data['classifier'] = [
        'SVM', 'GaussianNB', 'RF',
        'SVM', 'GaussianNB', 'RF',
        'SVM', 'GaussianNB', 'RF',
        'SVM', 'DNN', 'CNN', 
        'SVM', 'DNN', 'CNN', 
        'SVM', 'DNN', 'CNN', 
        'SVM', 'DNN', 'CNN'
]

records = pd.DataFrame(
    data=record_data, 
    columns=[
        'tool', 
        'model.source', 'model.word', 'model.document',
        'classifier',
        'time.model.format', 'time.train.format', 'time.evaluate.format', 'time.all.format',
        'accuracy(%)', 
        'time.train.raw', 
        'time.evaluate.raw', 
        'time.all.raw'
    ]
)

display(records.drop(['time.train.raw', 'time.evaluate.raw', 'time.all.raw'], axis=1))

tool model.source model.word model.document  classifier  \
0      sklearn        Plain  BOW-TFIDF          Plain         SVM   
1      sklearn        Plain  BOW-TFIDF          Plain  GaussianNB   
2      sklearn        Plain  BOW-TFIDF          Plain          RF   
3      sklearn          LSA  BOW-TFIDF            LSA         SVM   
4      sklearn          LSA  BOW-TFIDF            LSA  GaussianNB   
5      sklearn          LSA  BOW-TFIDF            LSA          RF   
6      sklearn          LDA  BOW-TFIDF            LDA         SVM   
7      sklearn          LDA  BOW-TFIDF            LDA  GaussianNB   
8      sklearn          LDA  BOW-TFIDF            LDA          RF   
9       gensim        text8   Word2Vec       w2v-mean         SVM   
10      gensim        text8   Word2Vec       w2v-mean         DNN   
11      gensim        text8   Word2Vec       w2v-mean         CNN   
12      gensim       corpus   Word2Vec       w2v-mean         SVM   
13      gensim       corpus   Word2Vec       w2v-mean         DNN   
14      gensim       corpus   Word2Vec       w2v-mean         CNN   
15  TensorFlow        text8   Word2Vec       w2v-mean         SVM   
16  TensorFlow        text8   Word2Vec       w2v-mean         DNN   
17  TensorFlow        text8   Word2Vec       w2v-mean         CNN   
18  TensorFlow       corpus   Word2Vec       w2v-mean         SVM   
19  TensorFlow       corpus   Word2Vec       w2v-mean         DNN   
20  TensorFlow       corpus   Word2Vec       w2v-mean         CNN   

   time.model.format time.train.format time.evaluate.format time.all.format  \
0     0:00:06.206000    0:00:00.089200       0:00:00.029900  0:00:06.325100   
1     0:00:06.206000    0:00:00.068400       0:00:00.061900  0:00:06.336300   
2     0:00:06.206000    0:00:00.222000       0:00:00.029300  0:00:06.457300   
3     0:00:06.979000    0:00:00.202000       0:00:00.016500  0:00:07.197500   
4     0:00:06.979000    0:00:00.012200       0:00:00.025500  0:00:07.016700   
5     0:00:06.979000    0:00:00.425000       0:00:00.027600  0:00:07.431600   
6     0:00:10.549000    0:00:00.097700       0:00:00.013500  0:00:10.660200   
7     0:00:10.549000    0:00:00.007250       0:00:00.013700  0:00:10.569950   
8     0:00:10.549000    0:00:00.239000       0:00:00.026000  0:00:10.814000   
9            0:32:17    0:00:01.990000       0:00:00.021300  0:32:19.011300   
10           0:32:20           0:03:06              0:01:45         0:37:11   
11           0:32:20           0:05:52              0:00:26         0:38:38   
12    0:00:41.142000    0:00:01.250000       0:00:00.019700  0:00:42.411700   
13    0:00:44.892000           0:03:03              0:01:04  0:04:51.892000   
14    0:00:44.892000           0:05:26       0:00:27.100000  0:06:37.992000   
15           2:46:50    0:00:02.190000       0:00:00.047500  2:46:52.237500   
16           2:01:41           0:03:05              0:01:41         2:06:27   
17           2:01:41           0:05:15              0:00:27         2:07:23   
18           0:15:07    0:00:02.250000       0:00:00.132000  0:15:09.382000   
19           0:15:12           0:03:03              0:01:29         0:19:44   
20           0:15:12           0:05:20       0:00:23.700000  0:20:55.700000   

    accuracy(%)  
0         86.16  
1         82.00  
2         81.79  
3         86.74  
4         70.79  
5         73.42  
6         59.32  
7         48.21  
8         52.05  
9         83.05  
10        80.95  
11        75.30  
12        82.74  
13        81.84  
14        78.10  
15        84.42  
16        80.05  
17        69.86  
18        76.68  
19        69.00  
20        66.14

In [90]:
# display(records['Word2Vec' == records['model.word']].sort_values(by=['time.all.format'], ascending=[True]))

## 总结

In [171]:
dataStat = {}
for basepart in ['classifier', 'model.word', 'model.document']: 
    dataStat[basepart] = {'time.train.raw':{}, 'time.evaluate.raw':{}, 'time.all.raw':{}, 'accuracy':{}}

> 在本次小试中，仅以查准率（Precision，也译作「精度」）作为训练效果度量。实际完成 20 分类的任务时，应使用 $F_{1}$ 进行性能度量

### 1. 对于同一种分类器训练法，不同表示模型对结果的影响

本次小试训练了在不同文本表示模型上的 5 种分类器，包括 3 种传统分类器（支持向量机 SVM，高斯朴素贝叶斯分类器 GaussianNB，随机森林分类器 RandomForest）与 2 种神经网络分类器（深度神经网络 DNN，卷积神经网络 CNN）。各种分类器在不同文本表示模型上的训练结果如下列各表格所示，小结如下：

#### 1. 对于同种分类器，不同表示模型会对训练结果造成影响

+ 从**训练效果**上看：
    - 查看标准差（`std`）：
        * CNN 受文本表示模型的影响最小，GaussianNB 受文本表示模型的影响最大。
            - 该结论的成立依赖于忽略下述事实：神经网络分类器仅在 2 种文本表示模型（两种词嵌入模型，即：基于 text8 训练的词向量均值表示；基于待学习语料训练的词向量均值表示）下进行训练，而传统分类器在 5 种文本表示模型（BOW+TFIDF 的直接表示，BOW+TFIDF+LSA，BOW+TFIDF+LDA，以及上述两种词嵌入模型）
        * 若考虑上述事实（传统算法在更多的文本表示模型上进行训练，因而变化的可能性更大），则
            - 传统分类器中：SVM 受文本表示模型的影响最小，GaussianNB 受文本表示模型的影响最大
            - 神经网络分类器种：CNN 比 DNN 受文本表示模型的影响更小
            
。。。待续

In [180]:
# DO NOT execute this cell UNITL get all data from all the cells below

statFrames = {basepart:{'time.train.raw':{}, 'time.train.evaluate':{}, 'time.all.raw':{}, 'accuracy':{}} for basepart in dataStat}
for basepart in ['classifier', 'model.word', 'model.document']: 
    print('Statistics for part: **{}**'.format(basepart))
    for statpart in ['accuracy', 'time.train.raw', 'time.evaluate.raw', 'time.all.raw']:
        if 0 != len(dataStat[basepart][statpart]):
            statFrames[basepart][statpart] = pd.concat([dframe[1] for dframe in dataStat[basepart][statpart].items()])
            print('Details for *{}*:'.format(statpart))
            display(statFrames[basepart][statpart])
            print()
    print('--------------------------------------------------')

Statistics for part: **classifier**
Details for *accuracy*:


name  count_nonzero    max    min       mean    med        std
0         CNN              4  78.10  66.14  72.350000  72.58   4.651054
0          RF              3  81.79  52.05  69.086667  73.42  12.521987
0         SVM              7  86.74  59.32  79.872857  83.05   8.930616
0         DNN              4  81.84  69.00  77.960000  80.50   5.211626
0  GaussianNB              3  82.00  48.21  67.000000  70.79  14.052618


Details for *time.train.raw*:


name  count_nonzero             max             min            mean  \
0         CNN              4         0:05:52         0:05:15  0:05:28.250000   
0          RF              3  0:00:00.425000  0:00:00.222000  0:00:00.295333   
0         SVM              7  0:00:02.250000  0:00:00.089200  0:00:01.152700   
0         DNN              4         0:03:06         0:03:03  0:03:04.250000   
0  GaussianNB              3  0:00:00.068400  0:00:00.007250  0:00:00.029283   

              med             std  
0         0:05:23  0:00:14.254385  
0  0:00:00.239000  0:00:00.091950  
0  0:00:01.250000  0:00:00.936443  
0         0:03:04  0:00:01.299038  
0  0:00:00.012200  0:00:00.027733


Details for *time.evaluate.raw*:


name  count_nonzero             max             min            mean  \
0         CNN              4  0:00:27.100000  0:00:23.700000  0:00:25.950000   
0          RF              3  0:00:00.029300  0:00:00.026000  0:00:00.027633   
0         SVM              7  0:00:00.132000  0:00:00.013500  0:00:00.040057   
0         DNN              4         0:01:45         0:01:04  0:01:29.750000   
0  GaussianNB              3  0:00:00.061900  0:00:00.013700  0:00:00.033700   

              med             std  
0  0:00:26.500000  0:00:01.368393  
0  0:00:00.027600  0:00:00.001347  
0  0:00:00.021300  0:00:00.038984  
0         0:01:35  0:00:15.990231  
0  0:00:00.025500  0:00:00.020514


Details for *time.all.raw*:


name  count_nonzero             max             min            mean  \
0         CNN              4         2:07:23  0:06:37.992000  0:48:23.673000   
0          RF              3  0:00:10.814000  0:00:06.457300  0:00:08.234300   
0         SVM              7  2:46:52.237500  0:00:06.325100  0:30:46.746471   
0         DNN              4         2:06:27  0:04:51.892000  0:47:03.473000   
0  GaussianNB              3  0:00:10.569950  0:00:06.336300  0:00:07.974317   

              med             std  
0  0:29:46.850000  0:46:59.507296  
0  0:00:07.431600  0:00:01.866986  
0  0:00:42.411700  0:56:40.847304  
0  0:28:27.500000  0:47:14.562921  
0  0:00:07.016700  0:00:01.856290


--------------------------------------------------
Statistics for part: **model.word**
--------------------------------------------------
Statistics for part: **model.document**
--------------------------------------------------


In [173]:
def stat_clf(thisClf):
    partName = thisClf
    tmpRecord = records[partName == records['classifier']]
    print('Raw data in {}'.format(partName))
    display(tmpRecord.drop(['time.train.raw', 'time.evaluate.raw', 'time.all.raw'], axis=1))

    print('Statistics for **accuracy(%)** in {}'.format(partName))

    tmpCol = tmpRecord['accuracy(%)'].values
    dataDetails = {
        'name': partName,
        'count_nonzero': [np.count_nonzero(tmpCol)],
        'max': [np.max(tmpCol)],
        'min': [np.min(tmpCol)],
        'mean': [np.mean(tmpCol)],
        'med': [np.median(tmpCol)],
        'std': [np.std(tmpCol)]
    }
    dataStat['classifier']['accuracy'][partName] = pd.DataFrame(
        data=dataDetails,
        columns=[
            'name',
            'count_nonzero', 
            'max',
            'min',
            'mean',
            'med',
            'std'
        ]
    )
    display(dataStat['classifier']['accuracy'][partName])

    for timepart in ['time.train.raw', 'time.evaluate.raw', 'time.all.raw']:
        print('Statistics for **{}** in {}'.format(timepart, partName))
        tmpCol = tmpRecord[timepart].values
        dataDetails = {
            'name': partName,
            'count_nonzero': [np.count_nonzero(tmpCol)],
            'max': [timeInFormat(np.max(tmpCol))],
            'min': [timeInFormat(np.min(tmpCol))],
            'mean': [timeInFormat(np.mean(tmpCol))],
            'med': [timeInFormat(np.median(tmpCol))],
            'std': [timeInFormat(np.std(tmpCol))]
        }

        dataStat['classifier'][timepart][partName] =  pd.DataFrame(
            data=dataDetails,
            columns=[
                'name',
                'count_nonzero', 
                'max',
                'min',
                'mean',
                'med',
                'std'
            ]
        )
        display(dataStat['classifier'][timepart][partName])

In [174]:
stat_clf('SVM')

Raw data in SVM


tool model.source model.word model.document classifier  \
0      sklearn        Plain  BOW-TFIDF          Plain        SVM   
3      sklearn          LSA  BOW-TFIDF            LSA        SVM   
6      sklearn          LDA  BOW-TFIDF            LDA        SVM   
9       gensim        text8   Word2Vec       w2v-mean        SVM   
12      gensim       corpus   Word2Vec       w2v-mean        SVM   
15  TensorFlow        text8   Word2Vec       w2v-mean        SVM   
18  TensorFlow       corpus   Word2Vec       w2v-mean        SVM   

   time.model.format time.train.format time.evaluate.format time.all.format  \
0     0:00:06.206000    0:00:00.089200       0:00:00.029900  0:00:06.325100   
3     0:00:06.979000    0:00:00.202000       0:00:00.016500  0:00:07.197500   
6     0:00:10.549000    0:00:00.097700       0:00:00.013500  0:00:10.660200   
9            0:32:17    0:00:01.990000       0:00:00.021300  0:32:19.011300   
12    0:00:41.142000    0:00:01.250000       0:00:00.019700  0:00:42.411700   
15           2:46:50    0:00:02.190000       0:00:00.047500  2:46:52.237500   
18           0:15:07    0:00:02.250000       0:00:00.132000  0:15:09.382000   

    accuracy(%)  
0         86.16  
3         86.74  
6         59.32  
9         83.05  
12        82.74  
15        84.42  
18        76.68

Statistics for **accuracy(%)** in SVM


name  count_nonzero    max    min       mean    med       std
0  SVM              7  86.74  59.32  79.872857  83.05  8.930616

Statistics for **time.train.raw** in SVM


name  count_nonzero             max             min            mean  \
0  SVM              7  0:00:02.250000  0:00:00.089200  0:00:01.152700   

              med             std  
0  0:00:01.250000  0:00:00.936443

Statistics for **time.evaluate.raw** in SVM


name  count_nonzero             max             min            mean  \
0  SVM              7  0:00:00.132000  0:00:00.013500  0:00:00.040057   

              med             std  
0  0:00:00.021300  0:00:00.038984

Statistics for **time.all.raw** in SVM


name  count_nonzero             max             min            mean  \
0  SVM              7  2:46:52.237500  0:00:06.325100  0:30:46.746471   

              med             std  
0  0:00:42.411700  0:56:40.847304

In [176]:
stat_clf('GaussianNB')

Raw data in GaussianNB


tool model.source model.word model.document  classifier  \
1  sklearn        Plain  BOW-TFIDF          Plain  GaussianNB   
4  sklearn          LSA  BOW-TFIDF            LSA  GaussianNB   
7  sklearn          LDA  BOW-TFIDF            LDA  GaussianNB   

  time.model.format time.train.format time.evaluate.format time.all.format  \
1    0:00:06.206000    0:00:00.068400       0:00:00.061900  0:00:06.336300   
4    0:00:06.979000    0:00:00.012200       0:00:00.025500  0:00:07.016700   
7    0:00:10.549000    0:00:00.007250       0:00:00.013700  0:00:10.569950   

   accuracy(%)  
1        82.00  
4        70.79  
7        48.21

Statistics for **accuracy(%)** in GaussianNB


name  count_nonzero   max    min  mean    med        std
0  GaussianNB              3  82.0  48.21  67.0  70.79  14.052618

Statistics for **time.train.raw** in GaussianNB


name  count_nonzero             max             min            mean  \
0  GaussianNB              3  0:00:00.068400  0:00:00.007250  0:00:00.029283   

              med             std  
0  0:00:00.012200  0:00:00.027733

Statistics for **time.evaluate.raw** in GaussianNB


name  count_nonzero             max             min            mean  \
0  GaussianNB              3  0:00:00.061900  0:00:00.013700  0:00:00.033700   

              med             std  
0  0:00:00.025500  0:00:00.020514

Statistics for **time.all.raw** in GaussianNB


name  count_nonzero             max             min            mean  \
0  GaussianNB              3  0:00:10.569950  0:00:06.336300  0:00:07.974317   

              med             std  
0  0:00:07.016700  0:00:01.856290

In [177]:
stat_clf('RF')

Raw data in RF


tool model.source model.word model.document classifier  \
2  sklearn        Plain  BOW-TFIDF          Plain         RF   
5  sklearn          LSA  BOW-TFIDF            LSA         RF   
8  sklearn          LDA  BOW-TFIDF            LDA         RF   

  time.model.format time.train.format time.evaluate.format time.all.format  \
2    0:00:06.206000    0:00:00.222000       0:00:00.029300  0:00:06.457300   
5    0:00:06.979000    0:00:00.425000       0:00:00.027600  0:00:07.431600   
8    0:00:10.549000    0:00:00.239000       0:00:00.026000  0:00:10.814000   

   accuracy(%)  
2        81.79  
5        73.42  
8        52.05

Statistics for **accuracy(%)** in RF


name  count_nonzero    max    min       mean    med        std
0   RF              3  81.79  52.05  69.086667  73.42  12.521987

Statistics for **time.train.raw** in RF


name  count_nonzero             max             min            mean  \
0   RF              3  0:00:00.425000  0:00:00.222000  0:00:00.295333   

              med             std  
0  0:00:00.239000  0:00:00.091950

Statistics for **time.evaluate.raw** in RF


name  count_nonzero             max             min            mean  \
0   RF              3  0:00:00.029300  0:00:00.026000  0:00:00.027633   

              med             std  
0  0:00:00.027600  0:00:00.001347

Statistics for **time.all.raw** in RF


name  count_nonzero             max             min            mean  \
0   RF              3  0:00:10.814000  0:00:06.457300  0:00:08.234300   

              med             std  
0  0:00:07.431600  0:00:01.866986

In [178]:
stat_clf('DNN')

Raw data in DNN


tool model.source model.word model.document classifier  \
10      gensim        text8   Word2Vec       w2v-mean        DNN   
13      gensim       corpus   Word2Vec       w2v-mean        DNN   
16  TensorFlow        text8   Word2Vec       w2v-mean        DNN   
19  TensorFlow       corpus   Word2Vec       w2v-mean        DNN   

   time.model.format time.train.format time.evaluate.format time.all.format  \
10           0:32:20           0:03:06              0:01:45         0:37:11   
13    0:00:44.892000           0:03:03              0:01:04  0:04:51.892000   
16           2:01:41           0:03:05              0:01:41         2:06:27   
19           0:15:12           0:03:03              0:01:29         0:19:44   

    accuracy(%)  
10        80.95  
13        81.84  
16        80.05  
19        69.00

Statistics for **accuracy(%)** in DNN


name  count_nonzero    max   min   mean   med       std
0  DNN              4  81.84  69.0  77.96  80.5  5.211626

Statistics for **time.train.raw** in DNN


name  count_nonzero      max      min            mean      med  \
0  DNN              4  0:03:06  0:03:03  0:03:04.250000  0:03:04   

              std  
0  0:00:01.299038

Statistics for **time.evaluate.raw** in DNN


name  count_nonzero      max      min            mean      med  \
0  DNN              4  0:01:45  0:01:04  0:01:29.750000  0:01:35   

              std  
0  0:00:15.990231

Statistics for **time.all.raw** in DNN


name  count_nonzero      max             min            mean  \
0  DNN              4  2:06:27  0:04:51.892000  0:47:03.473000   

              med             std  
0  0:28:27.500000  0:47:14.562921

In [179]:
stat_clf('CNN')

Raw data in CNN


tool model.source model.word model.document classifier  \
11      gensim        text8   Word2Vec       w2v-mean        CNN   
14      gensim       corpus   Word2Vec       w2v-mean        CNN   
17  TensorFlow        text8   Word2Vec       w2v-mean        CNN   
20  TensorFlow       corpus   Word2Vec       w2v-mean        CNN   

   time.model.format time.train.format time.evaluate.format time.all.format  \
11           0:32:20           0:05:52              0:00:26         0:38:38   
14    0:00:44.892000           0:05:26       0:00:27.100000  0:06:37.992000   
17           2:01:41           0:05:15              0:00:27         2:07:23   
20           0:15:12           0:05:20       0:00:23.700000  0:20:55.700000   

    accuracy(%)  
11        75.30  
14        78.10  
17        69.86  
20        66.14

Statistics for **accuracy(%)** in CNN


name  count_nonzero   max    min   mean    med       std
0  CNN              4  78.1  66.14  72.35  72.58  4.651054

Statistics for **time.train.raw** in CNN


name  count_nonzero      max      min            mean      med  \
0  CNN              4  0:05:52  0:05:15  0:05:28.250000  0:05:23   

              std  
0  0:00:14.254385

Statistics for **time.evaluate.raw** in CNN


name  count_nonzero             max             min            mean  \
0  CNN              4  0:00:27.100000  0:00:23.700000  0:00:25.950000   

              med             std  
0  0:00:26.500000  0:00:01.368393

Statistics for **time.all.raw** in CNN


name  count_nonzero      max             min            mean  \
0  CNN              4  2:07:23  0:06:37.992000  0:48:23.673000   

              med             std  
0  0:29:46.850000  0:46:59.507296

### 2. 对于同一种表示模型，不同训练模型对结果的影响

In [82]:
display(records['Word2Vec' == records['model.word']])

tool model.source model.word model.document classifier  \
9       gensim        text8   Word2Vec       w2v-mean        SVM   
10      gensim        text8   Word2Vec       w2v-mean        DNN   
11      gensim        text8   Word2Vec       w2v-mean        CNN   
12      gensim       corpus   Word2Vec       w2v-mean        SVM   
13      gensim       corpus   Word2Vec       w2v-mean        DNN   
14      gensim       corpus   Word2Vec       w2v-mean        CNN   
15  TensorFlow        text8   Word2Vec       w2v-mean        SVM   
16  TensorFlow        text8   Word2Vec       w2v-mean        DNN   
17  TensorFlow        text8   Word2Vec       w2v-mean        CNN   
18  TensorFlow       corpus   Word2Vec       w2v-mean        SVM   
19  TensorFlow       corpus   Word2Vec       w2v-mean        DNN   
20  TensorFlow       corpus   Word2Vec       w2v-mean        CNN   

        time.model      time.train   time.evaluate        time.all accuracy  
9          0:32:17  0:00:01.990000  0:00:00.021300  0:32:19.011300   83.05%  
10         0:32:20         0:03:06         0:01:45         0:37:11   80.95%  
11         0:32:20         0:05:52         0:00:26         0:38:38    75.3%  
12  0:00:41.142000  0:00:01.250000  0:00:00.019700  0:00:42.411700   82.74%  
13  0:00:44.892000         0:03:03         0:01:04  0:04:51.892000   81.84%  
14  0:00:44.892000         0:05:26  0:00:27.100000  0:06:37.992000    78.1%  
15         2:46:50  0:00:02.190000  0:00:00.047500  2:46:52.237500   84.42%  
16         2:01:41         0:03:05         0:01:41         2:06:27   80.05%  
17         2:01:41         0:05:15         0:00:27         2:07:23   69.86%  
18         0:15:07  0:00:02.250000  0:00:00.132000  0:15:09.382000   76.68%  
19         0:15:12         0:03:03         0:01:29         0:19:44    69.0%  
20         0:15:12         0:05:20  0:00:23.700000  0:20:55.700000   66.14%

### 3. 综合来看，「表示模型 + 分类器」组合的效果评估

### 4. 展望